In [75]:
import numpy as np
import pandas as pd
import datetime
import calendar
import adodbapi
import matplotlib.pyplot as plt
#%matplotlib inline
import smtplib
import schedule
import time
from email.mime.image import MIMEImage
from email.mime.multipart import MIMEMultipart
from IPython.display import HTML
# Import the email modules we'll need
from email.mime.text import MIMEText
from scipy.optimize import minimize
import math 
from io import StringIO
import io
import requests
from requests.auth import HTTPBasicAuth

In [76]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_colwidth', -1)

In [77]:
db_prov = 'SQLOLEDB' # ADO can use OLE
db_serv = 'daprod.cdntxa4at56p.us-east-1.rds.amazonaws.com,1433'
db_user = 'ctam'
db_pass = 'aOI7iOG3GD'
db_name = 'ads'

conn_string = 'Provider=%s;Data Source=%s;Initial Catalog=%s;User ID=%s;Password=%s;' % ( db_prov, db_serv, db_name, db_user, db_pass )

conn = adodbapi.connect(conn_string,200)

print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

Timestamp: 2019-07-25 14:00:58


In [78]:
Impression_table="""
select 
advertisername
,bankproductname
,placementname
,impression_time as impression_date
,impressioncount
,max(cast(impressioncount as float)) over (partition by impression_time, placementname) as max 
,case when 
placementname like '%Bank Pages Sponsored%'
then 1
else
round(cast(impressioncount as float)/max(cast(impressioncount as float)) over (partition by impression_time, placementname),1)
end as percentage_split_estimate
from(
select
b.name as bankname,
a.name as advertisername,
bp.name as bankproductname,
z.name as placementname,
cast(dateadd(hour,-5,i.impressiontime) as date) as impression_time,
sum(impressioncount) as impressioncount
from Ads..impressions i
left outer join findata..bankproducts bp on i.productid = bp.id
left outer join findata..banks b on bp.bankid=b.id
left outer join Ads..tags t on i.tagid=t.id
left outer join Ads..taggroups tg on t.taggroupid=tg.id
left outer join Ads..advertisers a on tg.advertiserid = a.id
left outer join Ads..Zones z on i.ZoneId = z.Id
where --cast(dateadd(hour,-5,i.impressiontime) as date) >= cast(format(dateadd(month,-2,dateadd(hour,-5,GETDATE())), 'yyyy-MM-01') as Date) and a.name not like ('%Portal%')
cast(dateadd(hour,-5,i.impressiontime) as date) >= '2018-12-31' and cast(dateadd(hour,-5,i.impressiontime) as date) <= '2019-02-28' and a.name not like ('%Portal%')
group by b.name,a.name,bp.name, z.name,cast(dateadd(hour,-5,i.impressiontime) as date)) gp1
"""

In [79]:
SQL_DA_Raw="""

select
c.id as ClickId
,c.DateClicked as old_dateClicked
,dateadd(hour,-5,c.DateClicked) as DateClicked -- Converting to EST
,cast(dateadd(hour,-5,c.DateClicked) as date) as DateOfMonth
,p.epc as ClickValue
,pm.pricingmodelname
,isnull(isnull(p.Epc,pt.RevenuePerClick),p.RevenuePerAccount) as Revenue
,a.name as AdvertiserName
,p.displayname as PackageName
,s.name as SiteName
,z.name as ZoneName
,case when z.name like '%Magnify%' and z.name not like ('%Featured Accounts Sidebar%') then 'zone_1'
when z.name in ('Bank Pages Sponsored - Open An Account', 'Bank Pages Sponsored - Most Popular Accounts') then 'zone_2'
when z.name like '%Display%' then 'zone_3'
else 'zone_4' end as zonegroup
,case when z.name like '%Magnify%' and z.name not like ('%Featured Accounts Sidebar%') or z.name in ('Bank Pages Sponsored - Open An Account', 'Bank Pages Sponsored - Most Popular Accounts') 
or z.name like '%Display%' then 'Y'
else 'N' end as zone_pre_det
,z.Id as ZoneID
,z.MinAds
,z.MaxAds
,case when z.ZoneType = ('Bank Page - Own') then 20
else z.MaxAds end as SpotAvailable
,z.ZoneType
,bp.name as ProductName
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
when bp.Name like '%month%' and bp.Name like '%9%' then '9-month'
when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
else 'Other' end as Term
,case when bp.Name like '%Business%' then 'Business'
when sc.Name like '%CD%' then 'CDs' 
when sc.Name like '%Money%' then 'MMA'
when sc.Name like '%IRA%' then 'IRAs'
when bp.Name like '%Health%' then 'HSA'
else sc.Name end as ProductDetail
,tg.name as TagName
,c.apy
,bpt.Apy as cur_apy
from ads..Clicks c with (nolock) --the click
inner join ads..Zones z on z.Id=c.ZoneId --the ad zone
inner join ads..Sites s on s.id=z.SiteId --the site
inner join ads..Tags t on t.Id=c.TagId --the ad link
inner join ads..TagGroups tg on tg.Id=t.TagGroupId --the parent grouping for the tag (links change often, so we group them)
inner join ads..Advertisers a on a.Id=tg.AdvertiserId --the advertiser
inner join ads..Packages p on p.Id=t.PackageId --the bucket we are delivering to
inner join ads..InsertionOrders i on i.Id=p.InsertionOrderId --the insertion order
left outer join tPriceTiers pt on t.pricetierid = pt.pricetierid
inner join tPricingModelLookup pm on p.PricingModelId = pm.PricingModelId
inner join findata.dbo.bankproducts bp on bp.id=c.productid --the product
inner join FinData..Sections sc on sc.Id = bp.SectionId--get product details
inner join findata.dbo.bankproducttiers bpt on bpt.BankProductId=bp.id and 25000 between bpt.MinAmount and bpt.MaxAmount
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
inner join ads..sessions ss on ss.id=c.SessionId --user info
--left join FinData..Products pd on bp.productid=pd.id
--where dateadd(hour,-5,c.DateClicked) >= cast(format(dateadd(Day,-8,GETDATE()), 'yyyy-MM-dd') as Date) 
--where dateadd(hour,-5,c.DateClicked) >= cast(format(dateadd(WEEK,-1,GETDATE()), 'yyyy-MM-dd') as Date)  and dateadd(hour,-5,c.DateClicked)<convert(datetime,convert(varchar,GETDATE(),1))
where dateadd(hour,-5,c.DateClicked) >= cast(format(dateadd(month,-2,dateadd(hour,-5,'2018-12-31')), 'yyyy-MM-01') as Date)  and dateadd(hour,-5,c.DateClicked)<convert(datetime,convert(varchar,dateadd(hour,-5,'2019-02-28'),1))  -- this will get matching number of clicks
and Exclude != 1
"""

In [80]:
master_rotation_cpd='''
select day(DateofMonth) as dayOfMonth
,month(DateofMonth) as monthofmonth
,DateOfMonth
,DATEPART(dw,DateOfMonth) as dayofweek
,SiteName
,ZoneType
,ZoneName
,zonegroup
,zone_pre_det
,ZoneID
,SpotAvailable
,da.AdvertiserName
,ProductName
,ProductDetail
,Term
,cur_apy -- not ready yet, wait for a few months for data to be matured
,count(1) as DailyClicks
,count(1)*da.Revenue as Revenue
,isnull(i.impressioncount,0) impressioncount
,isnull(i.percentage_split_estimate,1) percentage_split_estimate
from ({0}) da
left join ({1}) i 
on da.DateOfMonth=i.impression_date
and da.AdvertiserName = i.advertisername
and da.ZoneName = i.placementname
and da.ProductName = i.bankproductname
where da.AdvertiserName not like '%Portal%'
group by DateOfMonth,
SiteName, da.AdvertiserName, ZoneID,
ZoneType, ZoneName,  ProductName,ProductDetail,SpotAvailable,zonegroup
,zone_pre_det, i.impressioncount, i.percentage_split_estimate,Term, cur_apy, revenue
'''.format(SQL_DA_Raw,Impression_table)

In [95]:
date_l_joint_7_days="""
select SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName, 
sum(isnull(impressioncount,0)) as impressioncount_7d, round(avg(ISNULL(percentage_split_estimate,1)),2) as percentage_split_7d, 
sum(DailyClicks) as clicks_7d,
sum(Revenue) as rev_last_7_days,
round(sum(DailyClicks)/cast(count(DateOfMonth) as float),1) ClickPerDay_last_7_days,
round(sum(Revenue)/cast(count(DateOfMonth) as float),1) RevPerDay_last_7_days
from ({}) ggggg
where DateOfMonth>= cast(format(dateadd(WEEK,-1,dateadd(hour,-5,'2019-02-28')), 'yyyy-MM-dd') as Date) 
group by SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName""".format(master_rotation_cpd)

In [82]:
date_l_joint_last_week="""
select SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName,
sum(isnull(impressioncount,0)) as impressioncount_lw, 
round(avg(ISNULL(percentage_split_estimate,1)),2) as percentage_split_lw, 
sum(DailyClicks) as clicks_lw,
round(sum(DailyClicks)/cast(count(DateOfMonth) as float),1) ClickPerDay_same_day_last_week,
sum(Revenue) as rev_same_day_last_week,
round(sum(Revenue)/cast(count(DateOfMonth) as float),1) RevPerDay_same_day_last_week
from ({}) ggggg
where DateOfMonth = cast(format(dateadd(Day,-8,dateadd(hour,-5,'2019-02-28')), 'yyyy-MM-dd') as Date) 
group by SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName""".format(master_rotation_cpd)

In [83]:
date_l_joint_yesterday="""
select SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName,sum(isnull(impressioncount,0)) as impressioncount_ytd, 
round(avg(ISNULL(percentage_split_estimate,1)),2) as percentage_split_ytd, 
sum(DailyClicks) as clicks_ytd,
round(sum(DailyClicks)/cast(count(DateOfMonth) as float),1) ClickPerDay_yesterday,
sum(Revenue) as rev_yesterday,
round(sum(Revenue)/cast(count(DateOfMonth) as float),1) RevPerDay_yesterday
from ({}) ggggg
where DateOfMonth = cast(format(dateadd(Day,-1,dateadd(hour,-5,'2019-02-28')), 'yyyy-MM-dd') as Date) 
group by SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName
""".format(master_rotation_cpd)

In [84]:
date_l_joint_31d="""
select SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName,sum(isnull(impressioncount,0)) as impressioncount_1m, 
round(avg(ISNULL(percentage_split_estimate,1)),2) as percentage_split_1m, 
sum(DailyClicks) as clicks_1m,
round(sum(DailyClicks)/cast(count(DateOfMonth) as float),1) ClickPerDay_last_31_days,
sum(Revenue) as rev_last_31_days,
round(sum(Revenue)/cast(count(DateOfMonth) as float),1) RevPerDay_last_31_days
from ({}) ggggg
where 
--DateOfMonth>= cast(format(dateadd(Day,-31,dateadd(hour,-5,GETDATE())), 'yyyy-MM-dd') as Date) 
DateOfMonth >= '2018-12-31' and DateOfMonth <= '2019-02-28'
group by SiteName, ZoneName,zonegroup
,zone_pre_det, ZoneID, AdvertiserName, ProductName
""".format(master_rotation_cpd)

In [85]:
sql_placement_data = """
select 
SiteName
,ZoneName
,ZoneType
,ZoneID
,(SUM(DailyClicks)/cast(Count(DateOfMonth) as decimal(4,0))) as averageClicks
from 
({0}) aaa
where --ZoneName not like ('%MagnifyMoney - LP (CD)%') and 
ZoneName not like ('%MagnifyMoney - LP - CDB%') and --SiteName != ('LendingTree.com') and 
ZoneName not like ('%MagnifyMoney - LP - SavingsB%')
group by
SiteName
,ZoneName
,ZoneType
,ZoneID
order by 
SiteName
,ZoneName
""".format(master_rotation_cpd)

In [86]:
sql_catch_all_data="""
select
SiteName
,ZoneName
,zonegroup
,zone_pre_det
,ZoneID
,ProductDetail
,sum(isnull(impressioncount,0)) as impressioncount_avg
,round(avg(ISNULL(percentage_split_estimate,1)),2) as percentage_split_avg
,sum(DailyClicks) as clicks_avg
,(SUM(DailyClicks)/cast(Count(DateOfMonth) as decimal(4,0))) as averageClicks
from 
({0}) aaa
group by
SiteName
,ZoneName
,zonegroup
,zone_pre_det
,ZoneID
,ProductDetail
""".format(master_rotation_cpd)

In [87]:
advertiser_product_a="""
select case when a.name like '%Nationwide%' then 'Nationwide Bank' else a.name end advertiser_name,
bp.name product_name, 
case when bp.Name like '%Business%' then 'Business'
	when sc.Name like '%CD%' then 'CDs' 
	when sc.Name like '%Money%' then 'MMA'
	when sc.Name like '%IRA%' then 'IRAs'
    when bp.Name like '%Health%' then 'HSA'
	else sc.Name end as ProductDetail,
case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
	when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
	when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
	when bp.Name like '%month%' and bp.Name like '%9%' then '9-month'
	when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
	when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
	when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
	when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
	when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
	when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
	when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
	when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
	when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
	else 'Other' end as Term
from Ads..Advertisers a 
join FinData..BankProducts bp on a.BankId=bp.BankId and bp.Active=1
inner join FinData..Sections sc on sc.Id = bp.SectionId--get product details
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
--join FinData..Products p on p.Id=bp.ProductId
where a.Archived=0
and bp.id in (
    select ProductId from Ads..TagGroupProducts where TagGroupId in (
        select Id from Ads..TagGroups where archived=0 and TagGroupId in (
            select TagGroupId from Ads..Tags where dateadd(hour,-5,'2019-02-28') between StartTime and EndTime and Archived=0 and PackageId>0)))
and a.name not like '%portal%'
"""

In [88]:
ad_product_apy="""
select 
AdvertiserName,ProductDetail, ProductName, Apy 
from ({0}) aaaa
where AdvertiserName not like '%Portal%'
group by AdvertiserName,ProductDetail, ProductName, Apy
""".format(SQL_DA_Raw)

In [89]:
prior_d_pl="""
select b.Name as ZoneName,ZoneID, a.Priority, d.Name as AdvertiserName, bp.Name as ProductName
,case when bp.Name like '%Business%' then 'Business'
	when sc.Name like '%CD%' then 'CDs' 
	when sc.Name like '%Money%' then 'MMA'
	when sc.Name like '%IRA%' then 'IRAs'
    when bp.Name like '%Health%' then 'HSA'
	else sc.Name end as ProductDetail
from Ads..Placements a
left join Ads..Zones b
on a.ZoneID=b.ID
left join Ads..TagGroups c
on a.TagGroupId=c.Id
left join Ads..Advertisers d
on c.AdvertiserId=d.Id
inner join findata.dbo.bankproducts bp on bp.id=a.productid --the product
inner join FinData..Sections sc on sc.Id = bp.SectionId--get product details
where PlacementStatusTypeID=1 and d.Name not like '%Portal%' and c.Name not like '%test%'
"""

In [96]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
data_7d = pd.read_sql(date_l_joint_7_days,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
data_lw = pd.read_sql(date_l_joint_last_week,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
data_ytd = pd.read_sql(date_l_joint_yesterday,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
data_lm = pd.read_sql(date_l_joint_31d,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now(  )))
data_cpd = pd.read_sql(master_rotation_cpd,conn)


Timestamp: 2019-07-25 14:04:37
Timestamp: 2019-07-25 14:04:41
Timestamp: 2019-07-25 14:04:42
Timestamp: 2019-07-25 14:04:44
Timestamp: 2019-07-25 14:04:50


In [106]:
data_ytd

SiteName  \
0    DepositAccounts.com   
1    DepositAccounts.com   
2    DepositAccounts.com   
3    DepositAccounts.com   
4    DepositAccounts.com   
5    DepositAccounts.com   
6    DepositAccounts.com   
7    DepositAccounts.com   
8    DepositAccounts.com   
9    DepositAccounts.com   
10   DepositAccounts.com   
11   DepositAccounts.com   
12   DepositAccounts.com   
13   DepositAccounts.com   
14   DepositAccounts.com   
15   DepositAccounts.com   
16   DepositAccounts.com   
17   DepositAccounts.com   
18   DepositAccounts.com   
19   DepositAccounts.com   
20   DepositAccounts.com   
21   DepositAccounts.com   
22   DepositAccounts.com   
23   DepositAccounts.com   
24   DepositAccounts.com   
25   DepositAccounts.com   
26   DepositAccounts.com   
27   DepositAccounts.com   
28   DepositAccounts.com   
29   DepositAccounts.com   
30   DepositAccounts.com   
31   DepositAccounts.com   
32   DepositAccounts.com   
33   DepositAccounts.com   
34   DepositAccounts.com   
35   DepositAccounts.com   
36   DepositAccounts.com   
37   DepositAccounts.com   
38   DepositAccounts.com   
39   DepositAccounts.com   
40   DepositAccounts.com   
41   DepositAccounts.com   
42   DepositAccounts.com   
43   DepositAccounts.com   
44   DepositAccounts.com   
45   DepositAccounts.com   
46   DepositAccounts.com   
47   DepositAccounts.com   
48   DepositAccounts.com   
49   DepositAccounts.com   
50   DepositAccounts.com   
51   DepositAccounts.com   
52   DepositAccounts.com   
53   DepositAccounts.com   
54   DepositAccounts.com   
55   DepositAccounts.com   
56   DepositAccounts.com   
57   DepositAccounts.com   
58   DepositAccounts.com   
59   DepositAccounts.com   
60   DepositAccounts.com   
61   DepositAccounts.com   
62   DepositAccounts.com   
63   DepositAccounts.com   
64   DepositAccounts.com   
65   DepositAccounts.com   
66   DepositAccounts.com   
67   DepositAccounts.com   
68   DepositAccounts.com   
69   DepositAccounts.com   
70   DepositAccounts.com   
71   DepositAccounts.com   
72   DepositAccounts.com   
73   DepositAccounts.com   
74   DepositAccounts.com   
75   DepositAccounts.com   
76   DepositAccounts.com   
77   DepositAccounts.com   
78   DepositAccounts.com   
79   DepositAccounts.com   
80   DepositAccounts.com   
81   DepositAccounts.com   
82   DepositAccounts.com   
83   DepositAccounts.com   
84   DepositAccounts.com   
85   DepositAccounts.com   
86   DepositAccounts.com   
87   DepositAccounts.com   
88   DepositAccounts.com   
89   DepositAccounts.com   
90   DepositAccounts.com   
91   DepositAccounts.com   
92   DepositAccounts.com   
93   DepositAccounts.com   
94   DepositAccounts.com   
95   DepositAccounts.com   
96   DepositAccounts.com   
97   DepositAccounts.com   
98   DepositAccounts.com   
99   DepositAccounts.com   
100  DepositAccounts.com   
101  DepositAccounts.com   
102  DepositAccounts.com   
103  DepositAccounts.com   
104  DepositAccounts.com   
105  DepositAccounts.com   
106  DepositAccounts.com   
107  DepositAccounts.com   
108  DepositAccounts.com   
109  DepositAccounts.com   
110  DepositAccounts.com   
111  DepositAccounts.com   
112  DepositAccounts.com   
113  DepositAccounts.com   
114  DepositAccounts.com   
115  DepositAccounts.com   
116  DepositAccounts.com   
117  DepositAccounts.com   
118  DepositAccounts.com   
119  DepositAccounts.com   
120  DepositAccounts.com   
121  DepositAccounts.com   
122  DepositAccounts.com   
123  DepositAccounts.com   
124  DepositAccounts.com   
125  DepositAccounts.com   
126  DepositAccounts.com   
127  DepositAccounts.com   
128  DepositAccounts.com   
129  DepositAccounts.com   
130  DepositAccounts.com   
131  DepositAccounts.com   
132  DepositAccounts.com   
133  DepositAccounts.com   
134  DepositAccounts.com   
135  DepositAccounts.com   
136  DepositAccounts.com   
137  HiatusApp.com         
138  HiatusApp.com         
139  LendingTree.com       
140  LendingTree.com       
141  LendingTree.com       
142  Lending

In [101]:
##Since the SQL timeout, I manually mimmick the SQL query in Pandas
data_cpd1=pd.merge(data_cpd,data_7d[['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName','impressioncount_7d','percentage_split_7d','clicks_7d','ClickPerDay_last_7_days','rev_last_7_days','RevPerDay_last_7_days']]\
         ,how='left',on=['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName'])

In [102]:
data_cpd1=pd.merge(data_cpd1,data_lw[['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName','impressioncount_lw','percentage_split_lw','clicks_lw','ClickPerDay_same_day_last_week','rev_same_day_last_week','RevPerDay_same_day_last_week']]\
         ,how='left',on=['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName'])

In [105]:
data_cpd1=pd.merge(data_cpd1,data_lm[['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName','impressioncount_1m','percentage_split_1m','clicks_1m','ClickPerDay_last_31_days','rev_last_31_days','RevPerDay_last_31_days']]\
         ,how='left',on=['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName'])

In [107]:
data_cpd1=pd.merge(data_cpd1,data_ytd[['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName','impressioncount_ytd','percentage_split_ytd','clicks_ytd','ClickPerDay_yesterday','rev_yesterday','RevPerDay_yesterday']]\
         ,how='left',on=['SiteName','ZoneName','zonegroup','zone_pre_det','AdvertiserName','ProductName'])

In [108]:
##Fill NA with 0
data_cpd1.update(data_cpd1[['impressioncount_7d','clicks_7d','ClickPerDay_last_7_days','rev_last_7_days','RevPerDay_last_7_days',
                           'impressioncount_lw','clicks_lw','ClickPerDay_same_day_last_week','rev_same_day_last_week','RevPerDay_same_day_last_week',
                           'impressioncount_1m','clicks_1m','ClickPerDay_last_31_days','rev_last_31_days','RevPerDay_last_31_days',
                           'impressioncount_ytd','clicks_ytd','ClickPerDay_yesterday','rev_yesterday','RevPerDay_yesterday']].fillna(0))

In [109]:
##fill NA with 1
data_cpd1.update(data_cpd1[['percentage_split_7d','percentage_split_lw','percentage_split_1m','percentage_split_ytd']].fillna(1))

In [110]:
## temp fix to fill 0 with some value
data_cpd1.percentage_split_lw=np.where(data_cpd1.percentage_split_lw==0.0,data_cpd1.percentage_split_7d,data_cpd1.percentage_split_lw)

In [111]:
##Rename non-adjusted CPD so the naming for the adjusted one can be used for the code below
data_cpd1.rename(columns={'ClickPerDay_last_7_days':'ClickPerDay_last_7_days_o',
                         'ClickPerDay_same_day_last_week':'ClickPerDay_same_day_last_week_o',
                         'ClickPerDay_last_31_days':'ClickPerDay_last_31_days_o',
                         'ClickPerDay_yesterday':'ClickPerDay_yesterday_o',
                         'RevPerDay_last_7_days':'RevPerDay_last_7_days_o',
                          'RevPerDay_same_day_last_week':'RevPerDay_same_day_last_week_o',
                          'RevPerDay_last_31_days':'RevPerDay_last_31_days_o',
                          'RevPerDay_yesterday':'RevPerDay_yesterday_o'
                         },inplace=True)

In [115]:
#Computer adjusted CPD
data_cpd1['ClickPerDay_last_31_days']=data_cpd1['ClickPerDay_last_31_days_o']/data_cpd1['percentage_split_1m']
data_cpd1['ClickPerDay_last_7_days']=data_cpd1['ClickPerDay_last_7_days_o']/data_cpd1['percentage_split_7d']
data_cpd1['ClickPerDay_same_day_last_week']=data_cpd1['ClickPerDay_same_day_last_week_o']/data_cpd1['percentage_split_lw']
data_cpd1['ClickPerDay_yesterday']=data_cpd1['ClickPerDay_yesterday_o']/data_cpd1['percentage_split_ytd']
#Computer adjusted RPD
data_cpd1['RevPerDay_last_31_days']=data_cpd1['RevPerDay_last_31_days_o']/data_cpd1['percentage_split_1m']
data_cpd1['RevPerDay_last_7_days']=data_cpd1['RevPerDay_yesterday_o']/data_cpd1['percentage_split_7d']
data_cpd1['RevPerDay_same_day_last_week']=data_cpd1['RevPerDay_same_day_last_week_o']/data_cpd1['percentage_split_lw']
data_cpd1['RevPerDay_yesterday']=data_cpd1['RevPerDay_yesterday_o']/data_cpd1['percentage_split_ytd']

In [116]:
data_cpd1

dayOfMonth  monthofmonth DateOfMonth  dayofweek             SiteName  \
0      16          1             2019-01-16  4          MagnifyMoney.com      
1      30          11            2018-11-30  6          LendingTree.com       
2      31          1             2019-01-31  5          DepositAccounts.com   
3      12          12            2018-12-12  4          LendingTree.com       
4      3           10            2018-10-03  4          DepositAccounts.com   
5      17          11            2018-11-17  7          DepositAccounts.com   
6      12          2             2019-02-12  3          DepositAccounts.com   
7      16          1             2019-01-16  4          DepositAccounts.com   
8      13          12            2018-12-13  5          MagnifyMoney.com      
9      24          12            2018-12-24  2          MagnifyMoney.com      
10     23          1             2019-01-23  4          MagnifyMoney.com      
11     27          11            2018-11-27  3          DepositAccounts.com   
12     4           1             2019-01-04  6          DepositAccounts.com   
13     28          11            2018-11-28  4          DepositAccounts.com   
14     1           10            2018-10-01  2          DepositAccounts.com   
15     3           12            2018-12-03  2          DepositAccounts.com   
16     14          2             2019-02-14  5          MagnifyMoney.com      
17     15          12            2018-12-15  7          DepositAccounts.com   
18     25          1             2019-01-25  6          DepositAccounts.com   
19     11          11            2018-11-11  1          DepositAccounts.com   
20     28          1             2019-01-28  2          MagnifyMoney.com      
21     7           11            2018-11-07  4          DepositAccounts.com   
22     8           1             2019-01-08  3          DepositAccounts.com   
23     8           10            2018-10-08  2          DepositAccounts.com   
24     3           1             2019-01-03  5          DepositAccounts.com   
25     12          12            2018-12-12  4          DepositAccounts.com   
26     20          11            2018-11-20  3          DepositAccounts.com   
27     21          10            2018-10-21  1          DepositAccounts.com   
28     4           12            2018-12-04  3          DepositAccounts.com   
29     4           10            2018-10-04  5          DepositAccounts.com   
30     13          11            2018-11-13  3          DepositAccounts.com   
31     21          10            2018-10-21  1          MagnifyMoney.com      
32     15          2             2019-02-15  6          DepositAccounts.com   
33     3           2             2019-02-03  1          DepositAccounts.com   
34     14          2             2019-02-14  5          MagnifyMoney.com      
35     18          2             2019-02-18  2          DepositAccounts.com   
36     29          11            2018-11-29  5          DepositAccounts.com   
37     31          12            2018-12-31  2          MagnifyMoney.com      
38     15          10            2018-10-15  2          DepositAccounts.com   
39     5           12            2018-12-05  4          DepositAccounts.com   
40     15          2             2019-02-15  6          MagnifyMoney.com      
41     10          11            2018-11-10  7          DepositAccounts.com   
42     14          10            2018-10-14  1          MagnifyMoney.com      
43     2           2             2019-02-02  7          MagnifyMoney.com      
44     6           1             2019-01-06  1          DepositAccounts.com   
45     17          1             2019-01-17  5          DepositAccounts.com   
46     28          11            2018-11-28  4          MagnifyMoney.com      
47     7           12            2018-12-07  6          DepositAccounts.com   
48     18          1             2019-01-18  6          DepositAccounts.com   
49     9           1             2019-01-09  4          M

In [118]:
##Agg total clicks and days
data_cpd2=data_cpd1.groupby(by=['SiteName','AdvertiserName','ZoneType','ZoneName','zonegroup','zone_pre_det','ZoneID','SpotAvailable',
                               'ProductName','ProductDetail','ClickPerDay_last_7_days','ClickPerDay_same_day_last_week',
                                'ClickPerDay_yesterday','ClickPerDay_last_31_days','impressioncount_7d','impressioncount_lw'
                                ,'impressioncount_ytd','impressioncount_1m','clicks_1m','clicks_7d','clicks_lw','clicks_ytd'
                                ,'percentage_split_1m','percentage_split_7d','percentage_split_lw','percentage_split_ytd',
                               'ClickPerDay_last_7_days_o','ClickPerDay_same_day_last_week_o',
                                'ClickPerDay_yesterday_o','ClickPerDay_last_31_days_o'
                                ,'RevPerDay_last_7_days','RevPerDay_last_31_days',
                                'RevPerDay_same_day_last_week','RevPerDay_yesterday','RevPerDay_last_7_days_o','RevPerDay_last_31_days_o',
                                'RevPerDay_same_day_last_week_o','RevPerDay_yesterday_o','rev_last_7_days','rev_same_day_last_week',
                                'rev_last_31_days','rev_yesterday'
                               ]).agg({'DateOfMonth':'count', 'DailyClicks': 'sum'})\
.reset_index()\
.rename(columns={'DateOfMonth':'DayCount','DailyClicks':'TotalClicks'})

In [119]:
#compute CPD Total
data_cpd2['ClickPerDay_2Months']=data_cpd2['TotalClicks']/data_cpd2['DayCount']
data_cpd2['ClickPerDay']=0

In [120]:
data_cpd2

SiteName                  AdvertiserName  \
0    CompareCards.com     Ally Bank                        
1    CompareCards.com     American Express National Bank   
2    CompareCards.com     Barclays                         
3    CompareCards.com     Synchrony Bank                   
4    DepositAccounts.com  Ally Bank                        
5    DepositAccounts.com  Ally Bank                        
6    DepositAccounts.com  Ally Bank                        
7    DepositAccounts.com  Ally Bank                        
8    DepositAccounts.com  Ally Bank                        
9    DepositAccounts.com  Ally Bank                        
10   DepositAccounts.com  Ally Bank                        
11   DepositAccounts.com  Ally Bank                        
12   DepositAccounts.com  Ally Bank                        
13   DepositAccounts.com  Ally Bank                        
14   DepositAccounts.com  Ally Bank                        
15   DepositAccounts.com  Ally Bank                        
16   DepositAccounts.com  Ally Bank                        
17   DepositAccounts.com  Ally Bank                        
18   DepositAccounts.com  Ally Bank                        
19   DepositAccounts.com  Ally Bank                        
20   DepositAccounts.com  Ally Bank                        
21   DepositAccounts.com  Ally Bank                        
22   DepositAccounts.com  Ally Bank                        
23   DepositAccounts.com  Ally Bank                        
24   DepositAccounts.com  Ally Bank                        
25   DepositAccounts.com  Ally Bank                        
26   DepositAccounts.com  Ally Bank                        
27   DepositAccounts.com  Ally Bank                        
28   DepositAccounts.com  Ally Bank                        
29   DepositAccounts.com  Ally Bank                        
30   DepositAccounts.com  Ally Bank                        
31   DepositAccounts.com  Ally Bank                        
32   DepositAccounts.com  Ally Bank                        
33   DepositAccounts.com  Ally Bank                        
34   DepositAccounts.com  Ally Bank                        
35   DepositAccounts.com  Ally Bank                        
36   DepositAccounts.com  Ally Bank                        
37   DepositAccounts.com  Ally Bank                        
38   DepositAccounts.com  Ally Bank                        
39   DepositAccounts.com  Ally Bank                        
40   DepositAccounts.com  Ally Bank                        
41   DepositAccounts.com  Ally Bank                        
42   DepositAccounts.com  Ally Bank                        
43   DepositAccounts.com  Ally Bank                        
44   DepositAccounts.com  Ally Bank                        
45   DepositAccounts.com  Ally Bank                        
46   DepositAccounts.com  Ally Bank                        
47   DepositAccounts.com  Ally Bank                        
48   DepositAccounts.com  Ally Bank                        
49   DepositAccounts.com  Ally Bank                        
50   DepositAccounts.com  American Express National Bank   
51   DepositAccounts.com  American Express National Bank   
52   DepositAccounts.com  American Express National Bank   
53   DepositAccounts.com  American Express National Bank   
54   DepositAccounts.com  American Express National Bank   
55   DepositAccounts.com  American Express National Bank   
56   DepositAccounts.com  American Express National Bank   
57   DepositAccounts.com  American Express National Bank   
58   DepositAccounts.com  American Express National Bank   
59   DepositAccounts.com  American Express National Bank   
60   DepositAccounts.com  American Express National Bank   
61   DepositAccounts.com  American Express National Bank   
62   DepositAccounts.com  American Express National Bank   
63   DepositAccounts.com  American Express National Bank   
64   DepositAccounts.com  American Express National Bank   
65   DepositAccounts.com  American Express National Bank

In [121]:
#merge available spots
df=data_cpd2.copy()

In [122]:
source_of_truth_n="""
select Priority, Rotation, Paused, p.Archived, pst.Name as Status, z.Name as ZoneName, z.ZoneType, z.Id ZoneID
,case when z.Name like '%Magnify%' and z.Name not like ('%Featured Accounts Sidebar%') then 'zone_1'
when z.Name in ('Bank Pages Sponsored - Open An Account', 'Bank Pages Sponsored - Most Popular Accounts') then 'zone_2'
when z.Name like '%Display%' then 'zone_3'
else 'zone_4' end as zonegroup
,case when z.ZoneType = ('Bank Page - Own') then 20
else z.MaxAds end as SpotAvailable
, a.Name as AdvertiserName, bp.Name as ProductName, pd.ShortName
,case when bp.Name like '%Business%' then 'Business'
	when sc.Name like '%CD%' then 'CDs' 
	when sc.Name like '%Money%' then 'MMA'
	when sc.Name like '%IRA%' then 'IRAs'
    when bp.Name like '%Health%' then 'HSA'
	else sc.Name end as ProductDetail
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
when bp.Name like '%month%' and bp.Name like '%9%' then '6-month'
when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
else 'Other' end as Term
,bpt.Apy
from
Ads..placements p with(nolock)
inner join Ads..PlacementStatusType pst with(nolock) on p.placementstatustypeid = pst.id 
and pst.name in ('running','ready')
inner join ads..Zones z with(nolock)
on p.ZoneId = z.Id
inner join ads..Sites s  with(nolock) on s.id=z.SiteId --the site
inner join ads..TagGroups tg  with(nolock) on tg.Id=p.TagGroupId --the parent grouping for the tag (links change often, so we group them)
inner join ads..Advertisers a  with(nolock) on a.Id=tg.AdvertiserId --the advertiser
inner join findata.dbo.bankproducts bp with(nolock) on bp.id=p.productid
and bp.Active=1 -- and bp.Active=1 currently only is citi bank
inner join findata.dbo.bankproducttiers bpt on bpt.BankProductId=bp.id and 25000 between bpt.MinAmount and bpt.MaxAmount
inner join FinData..Sections sc  with(nolock) on sc.Id = bp.SectionId--get product details
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
where a.Name not like ('%Portal%')
and a.Archived=0 
"""

In [123]:
#Getting unique ZoneName
zone_mapping = df.groupby(by=['ZoneType','ZoneName','zonegroup','zone_pre_det'], as_index=False).last()[['ZoneType','ZoneName','zonegroup','zone_pre_det']]

In [124]:
zone_quality_sort_data = """
select
	DATEPART(year,DateClicked)*100+DATEPART(week,DateClicked) as year_week
	--,Cast(common_date - (@@DATEFIRST + DATEPART(WEEKDAY,common_date)) % 7 + 1 as date) as year_week_date_common
	,DATEPART(year,DateClicked)*100+DATEPART(MONTH,DateClicked) as year_month
	,DATEPART(year,logTime)*100+DATEPART(week,logTime) as year_week_AccountOpenings
	,DATEPART(year,logTime)*100+DATEPART(MONTH,logTime) as year_month_AccountOpenings
	,DATEPART(year,common_date)*100+DATEPART(week,common_date) as year_week_Common
	,cast(DATEADD(WEEK, DATEDIFF(WEEK, '1905-01-01', common_date), '1905-01-01')as date) year_week_date_common
	,DATEPART(year,common_date)*100+DATEPART(MONTH,common_date) as year_month_Common
	,logTime
	,DateClicked
	,common_date
	,ClickValue
	,AdvertiserName
	,SiteName
	,ZoneName
	,ZoneType
	,ZoneID
	,SpotAvailable
	,ProductName
	,ProductDetail
	,Term
	,TagName
	,isnull(CChannel,'ImpressionToOpens') as CChannel
	,isnull(LtCChannel,'ImpressionToOpens') as LtCChannel
	,isnull(BiddedKeyword,'ImpressionToOpens') as BiddedKeyword
	,isnull(SearchEngine,'ImpressionToOpens') as SearchEngine
	,isnull(Device,'ImpressionToOpens') as Device
	,isnull(PhysicalLocation,'ImpressionToOpens') as PhysicalLocation
	,isnull(KeywordContent,'ImpressionToOpens') as KeywordContent
	,isnull(SearchVsSearchPartners,'ImpressionToOpens') as SearchVsSearchPartners
	,isnull(LandingPage,'ImpressionToOpens') as LandingPage
	,isnull(AdPosition,'ImpressionToOpens') as AdPosition
	,isnull(MatchType,'ImpressionToOpens') as MatchType
	,count(DateClicked) as ClickCount
	,count(DateClicked)*ClickValue as AcquisitionCost
	,sum(TotalOpenings) as AccountOpenCount 
from (
--Based on Jordan's query
select cast(CONVERT(date, DateAdd(hh, -5, LogTime) ) as varchar(50)) as logTime,  
ao.Id
,count(ao.Id) as TotalOpenings
,dateadd(hour,-5,c.DateClicked) as DateClicked -- Converting to EST
,cast(dateadd(hour,-5,c.DateClicked) as date) as DateOfMonth
,DateAdd(hh, -5, LogTime) as common_date
,p.epc as ClickValue
,a.name as AdvertiserName
,s.name as SiteName
,z.name as ZoneName
,z.ZoneType
,z.id ZoneID
,case when z.ZoneType = ('Bank Page - Own') then 20
else z.MaxAds end as SpotAvailable
,bp.name as ProductName
,case when bp.name like '%Business%' then 'Business'
	when bp.name like '%CD%' then 'CDs' 
	when bp.name like '%Money Market Cert%' then 'CDs'
    when bp.Name like '%Health%' then 'HSA'
	when bp.name like '%Saving%' then 'Savings'
	when bp.name like '%Money%' then 'MMA'
	when bp.name like 'Personal Account' then 'Checking'
	when bp.name like '%IRA%' then 'IRAs'
	else 'Other' end as ProductDetail
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
	when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
	when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
	when bp.Name like '%month%' and bp.Name like '%9%' then '9-month'
	when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
	when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
	when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
	when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
	when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
	when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
	when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
	when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
	when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
	else 'Other' end as Term
,tg.name as TagName
,c.Exclude
--adding SEM parameters below
,ses.CChannel
,ses.LtCChannel
,ltrim(replace(replace(ses.Ppckw,'%20',' '),'%2B','+')) as BiddedKeyword
,ses.CSource as SearchEngine
,ses.CTerm as Device
,ses.CMethod as PhysicalLocation
,ses.CContent as KeywordContent
,ses.CType as SearchVsSearchPartners
,ses.CName as LandingPage
,ses.CCreative as AdPosition
,ses.MatchType
from Ads..AccountOpenings ao with (nolock)
left outer join clicks c with (nolock) on c.Id=ao.ClickId 
left outer join Zones z with (nolock) on z.Id = c.ZoneId 
left outer join Sites s with (nolock) on s.Id=z.SiteId 
left outer join Tags t with (nolock) on t.Id = c.TagId 
left outer join TagGroups tg with (nolock) on tg.Id = t.TagGroupId 
left outer join Advertisers a with (nolock) on a.id = ao.AdvertiserId 
left outer join Packages p with (nolock) on p.Id=t.PackageId --the bucket we are delivering to
left outer join findata.dbo.bankproducts bp with (nolock) on bp.id=c.productid
left outer join Sessions ses with (nolock) on (ao.SessionId = ses.id or c.SessionId = ses.id)--updated for new methodology
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
--Exclude account opens and added back in the union joint below
WHERE ao.Exclude=0  
--AND dateadd(hour,-5,LogTime) >= cast(format(dateadd(month,-2,dateadd(hour,-5,GETDATE())), 'yyyy-MM-01') as Date) and dateadd(hour,-5,LogTime) < convert(datetime,convert(varchar,dateadd(hour,-5,GETDATE()),1)) 
AND dateadd(hour,-5,LogTime) >= cast(format(dateadd(month,-2,dateadd(hour,-5,'2018-12-31')), 'yyyy-MM-01') as Date) 
and dateadd(hour,-5,LogTime) < convert(datetime,convert(varchar,dateadd(hour,-5,'2019-02-28'),1)) 

--and dateadd(hour,-5,LogTime) >= '2017-01-01'
and ao.AccountOpeningCorrelationTypeId=1 -- capturing just click type = 1
GROUP BY cast(CONVERT(date, DateAdd(hh, -5, LogTime) ) as varchar(50)) 
,dateadd(hour,-5,c.DateClicked) -- Converting to EST
,cast(dateadd(hour,-5,c.DateClicked) as date)
,DateAdd(hh, -5, LogTime)
,ao.Id
,p.epc
,a.name
,s.name
,z.name
,z.ZoneType
,z.id
,case when z.ZoneType = ('Bank Page - Own') then 20
else z.MaxAds end
,bp.name 
,case when bp.name like '%Business%' then 'Business'
	when bp.name like '%CD%' then 'CDs' 
	when bp.name like '%Money Market Cert%' then 'CDs' 
    when bp.Name like '%Health%' then 'HSA'
	when bp.name like '%Saving%' then 'Savings'
	when bp.name like '%Money%' then 'MMA'
	when bp.name like 'Personal Account' then 'Checking'
	when bp.name like '%IRA%' then 'IRAs'
	else 'Other' end
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
	when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
	when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
	when bp.Name like '%month%' and bp.Name like '%9%' then '9-month'
	when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
	when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
	when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
	when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
	when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
	when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
	when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
	when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
	when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
	else 'Other' end
,tg.name
,c.Exclude
,ses.CChannel
,ses.LtCChannel
,ses.Ppckw
,ses.CSource
,ses.CTerm 
,ses.CMethod 
,ses.CContent
,ses.CType
,ses.CName 
,ses.CCreative 
,ses.MatchType
union
--union all account open clicks
select
'2010-01-01 00:00:00' as logTime
,c.Id
,0 as TotalOpenings
,dateadd(hour,-5,c.DateClicked) as DateClicked -- Converting to EST
,cast(dateadd(hour,-5,c.DateClicked) as date) as DateOfMonth
,dateadd(hour,-5,c.DateClicked) as common_date
,p.epc as ClickValue
,a.name as AdvertiserName
,s.name as SiteName
,z.name as ZoneName
,z.ZoneType
,z.id
,case when z.ZoneType = ('Bank Page - Own') then 20
else z.MaxAds end as SpotAvailable
,bp.name as ProductName
,case when bp.name like '%Business%' then 'Business'
	when bp.name like '%CD%' then 'CDs' 
	when bp.name like '%Money Market Cert%' then 'CDs' 
    when bp.Name like '%Health%' then 'HSA'
	when bp.name like '%Saving%' then 'Savings'
	when bp.name like '%Money%' then 'MMA'
	when bp.name like 'Personal Account' then 'Checking'
	when bp.name like '%IRA%' then 'IRAs'
	else 'Other' end as ProductDetail
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
	when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
    when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
	when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
	when bp.Name like '%month%' and bp.Name like '%9%' then '9-month'
	when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
	when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
	when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
	when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
	when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
	when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
	when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
	when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
	when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
	when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
	when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
	else 'Other' end as Term
,tg.name as TagName
,c.Exclude
,ss.CChannel
,ss.LtCChannel
,ltrim(replace(replace(ss.Ppckw,'%20',' '),'%2B','+')) as BiddedKeyword
,ss.CSource as SearchEngine
,ss.CTerm as Device
,ss.CMethod as PhysicalLocation
,ss.CContent as KeywordContent
,ss.CType as SearchVsSearchPartners
,ss.CName as LandingPage
,ss.CCreative as AdPosition
,ss.MatchType
from Clicks c with (nolock) --the click
inner join Zones z with (nolock) on z.Id=c.ZoneId --the ad zone
	inner join Sites s with (nolock) on s.id=z.SiteId --the site
		inner join Tags t with (nolock) on t.Id=c.TagId --the ad link
			inner join TagGroups tg with (nolock)on tg.Id=t.TagGroupId --the parent grouping for the tag (links change often, so we group them)
				inner join Advertisers a with (nolock) on a.Id=tg.AdvertiserId --the advertiser
			inner join Packages p with (nolock) on p.Id=t.PackageId --the bucket we are delivering to
				inner join InsertionOrders i with (nolock) on i.Id=p.InsertionOrderId --the insertion order
inner join findata.dbo.bankproducts bp with (nolock) on bp.id=c.productid --the product
inner join sessions ss with (nolock) on ss.id=c.SessionId --user info
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
where 
dateadd(hour,-5,c.DateClicked) >= cast(format(dateadd(month,-2,dateadd(hour,-5,'2018-12-31')), 'yyyy-MM-01') as Date) 
and dateadd(hour,-5,c.DateClicked) < convert(datetime,convert(varchar,dateadd(hour,-5,'2019-02-28'),1)) -- conversion to make it at midnight
--dateadd(hour,-5,c.DateClicked) >= '2017-01-01'
and c.Exclude != 1
and a.Name in (
select distinct a.Name
from accountopenings ao with (nolock)
left outer join Advertisers a with (nolock) on a.id = ao.AdvertiserId 
where AccountOpeningCorrelationTypeId=1
group by a.Name, AccountOpeningCorrelationTypeId) 
and c.Id not in (
select
isnull(ao.ClickId,0) as id
from accountopenings ao with (nolock)
left outer join clicks c with (nolock) on c.Id=ao.ClickId 
left outer join Zones z with (nolock) on z.Id = c.ZoneId 
left outer join Sites s with (nolock) on s.Id=z.SiteId 
left outer join Tags t with (nolock) on t.Id = c.TagId 
left outer join TagGroups tg with (nolock) on tg.Id = t.TagGroupId 
left outer join Advertisers a with (nolock) on a.id = ao.AdvertiserId 
left outer join findata.dbo.bankproducts bp with (nolock) on bp.id=c.productid
left outer join Sessions ses with (nolock) on ses.Id=ao.SessionId 
WHERE ao.Exclude=0 AND 
dateadd(hour,-5,LogTime) >= cast(format(dateadd(month,-4,dateadd(hour,-5,'2018-12-31')), 'yyyy-MM-01') as Date) and 
dateadd(hour,-5,LogTime) < convert(datetime,convert(varchar,dateadd(hour,-5,'2019-02-28'),1)) 
--and dateadd(hour,-5,LogTime) >= '2017-01-01'
)) bbb
group by
DATEPART(year,DateClicked)*100+DATEPART(week,DateClicked) 
	,DATEPART(year,DateClicked)*100+DATEPART(MONTH,DateClicked)
	,DATEPART(year,logTime)*100+DATEPART(week,logTime) 
	,DATEPART(year,logTime)*100+DATEPART(MONTH,logTime) 
	,DATEPART(year,common_date)*100+DATEPART(week,common_date)
	,DATEPART(year,common_date)*100+DATEPART(MONTH,common_date) 
	,logTime
	,DateClicked
	,common_date
	,ClickValue
	,AdvertiserName
	,SiteName
	,ZoneName
	,ZoneType
	,ZoneID
	,SpotAvailable
	,ProductName
	,ProductDetail
	,Term
	,TagName
	,CChannel
	,LtCChannel
	,BiddedKeyword
	,SearchEngine
	,Device
	,PhysicalLocation
	,KeywordContent
	,SearchVsSearchPartners
	,LandingPage
	,AdPosition
	,MatchType
"""

In [125]:
zone_quality_sort = """
select ZoneName, ZoneType, ZoneID, SpotAvailable
,case when ZoneName like '%Magnify%' and Zonename not like ('%Featured Accounts Sidebar%') then 'zone_1'
when ZoneName in ('Bank Pages Sponsored - Open An Account', 'Bank Pages Sponsored - Most Popular Accounts') then 'zone_2'
when ZoneName like '%Display%' then 'zone_3'
else 'zone_4' end as zonegroup, 
round(cast(sum(AccountOpenCount) as float)/cast(sum(ClickCount) as float),3) open_rate 
from ({}) a
group by ZoneName,ZoneType, ZoneID, SpotAvailable
""".format(zone_quality_sort_data)

In [126]:
zone_quality_lp_sem = """
select ZoneName, Term
,case when ZoneName like '%Magnify%' and Zonename not like ('%Featured Accounts Sidebar%') then 'zone_1'
when ZoneName in ('Bank Pages Sponsored - Open An Account', 'Bank Pages Sponsored - Most Popular Accounts') then 'zone_2'
when ZoneName like '%Display%' then 'zone_3'
else 'zone_4' end as zonegroup, 
round(cast(sum(AccountOpenCount) as float)/cast(sum(ClickCount) as float),3) open_rate 
from ({}) a
where Zonename in ('LP - SEM (CD)')
group by ZoneName,Term
""".format(zone_quality_sort_data)

In [127]:
# prior_day_placement = """

# select * from 
# (
# SELECT
# a.Id, a.ZoneId, a.ZoneName, a.AdvertiserName, a.Rotation, a.Priority, bp.Name as ProductName
# ,case when bp.Name like '%Business%' then 'Business'
# 	when sc.Name like '%CD%' then 'CDs' 
# 	when sc.Name like '%Money%' then 'MMA'
# 	when sc.Name like '%IRA%' then 'IRAs'
# 	when bp.Name like '%Health%' then 'HSA'
# 	else sc.Name end as ProductDetail
# ,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
# when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
# when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
# when bp.Name like '%month%' and bp.Name like '%9%' then '6-month'
# when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
# when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
# when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
# when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
# when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
# when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
# when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
# when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
# when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
# when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
# when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
# else 'Other' end as Term
# FROM [Ads].[dbo].[LivePlacementsHistory] a 
# left join findata.dbo.bankproducts bp on a.productid = bp.id
# inner join FinData..Sections sc  with(nolock) on sc.Id = bp.SectionId--get product details
# left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
# WHERE GETUTCDATE()-1 BETWEEN a.ValidFrom AND a.ValidTo 
# UNION
# SELECT a.Id, a.ZoneId, a.ZoneName, a.AdvertiserName, a.Rotation, a.Priority, bp.Name as ProductName 
# ,case when bp.Name like '%Business%' then 'Business'
# 	when sc.Name like '%CD%' then 'CDs' 
# 	when sc.Name like '%Money%' then 'MMA'
# 	when sc.Name like '%IRA%' then 'IRAs'
# 	when bp.Name like '%Health%' then 'HSA'
# 	else sc.Name end as ProductDetail
# ,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
# when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
# when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
# when bp.Name like '%month%' and bp.Name like '%9%' then '6-month'
# when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
# when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
# when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
# when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
# when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
# when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
# when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
# when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
# when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
# when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
# when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
# when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
# else 'Other' end as Term
# FROM Ads..LivePlacements a 
# left join findata.dbo.bankproducts bp on a.productid = bp.id
# inner join FinData..Sections sc  with(nolock) on sc.Id = bp.SectionId--get product details
# left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
# WHERE GETUTCDATE()-1 >= a.InsertDateTime) b
# where AdvertiserName not like ('%Portal%')

# """

In [128]:
prior_day_placement ="""

SELECT a.Id, a.ZoneId, a.ZoneName, a.AdvertiserName, a.Rotation, a.Priority, bp.Name as ProductName 
,case when bp.Name like '%Business%' then 'Business'
	when sc.Name like '%CD%' then 'CDs' 
	when sc.Name like '%Money%' then 'MMA'
	when sc.Name like '%IRA%' then 'IRAs'
	when bp.Name like '%Health%' then 'HSA'
	else sc.Name end as ProductDetail
,case when pd.ShortName like '%CD%' then left(pd.ShortName,len(pd.shortname)-3)
when bp.Name like '%month%' and bp.Name like '%13%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%14%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%15%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%3%' then '3-month'
when bp.Name like '%month%' and bp.Name like '%6%' then '6-month'
when bp.Name like '%month%' and bp.Name like '%9%' then '6-month'
when bp.Name like '%month%' and bp.Name like '%11%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%12%' then '1-year'
when bp.Name like '%month%' and bp.Name like '%18%' then '18-month'
when bp.Name like '%month%' and bp.Name like '%24%' then '2-year'
when bp.Name like '%month%' and bp.Name like '%36%' then '3-year'
when bp.Name like '%month%' and bp.Name like '%48%' then '4-year'
when bp.Name like '%month%' and bp.Name like '%60%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%1%' then '1-year'
when bp.Name like '%year%' and bp.Name like '%2%' then '2-year'
when bp.Name like '%year%' and bp.Name like '%3%' then '3-year'
when bp.Name like '%year%' and bp.Name like '%4%' then '4-year'
when bp.Name like '%year%' and bp.Name like '%5%' then '5-year'
when bp.Name like '%year%' and bp.Name like '%6%' then '6-year'
else 'Other' end as Term
FROM Ads..LivePlacements a 
left join findata.dbo.bankproducts bp on a.productid = bp.id
inner join FinData..Sections sc  with(nolock) on sc.Id = bp.SectionId--get product details
left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
where a.AdvertiserName not like ('%Portal%')
order by ZoneName

"""

In [129]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
CPD_placement_all=pd.read_sql(sql_catch_all_data,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
PlacementRanking=pd.read_sql(sql_placement_data,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
advertiser_product=pd.read_sql(advertiser_product_a,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
ad_product_apy=pd.read_sql(ad_product_apy,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
prior_d_pl=pd.read_sql(prior_d_pl,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
source_of_truth_n=pd.read_sql(source_of_truth_n,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
zone_quality_sort=pd.read_sql(zone_quality_sort,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
zone_quality_lp_sem=pd.read_sql(zone_quality_lp_sem,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))
prior_day_placement=pd.read_sql(prior_day_placement,conn)
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

Timestamp: 2019-07-25 16:51:45
Timestamp: 2019-07-25 16:52:09
Timestamp: 2019-07-25 16:52:27
Timestamp: 2019-07-25 16:52:27
Timestamp: 2019-07-25 16:52:34
Timestamp: 2019-07-25 16:52:34
Timestamp: 2019-07-25 16:52:34
Timestamp: 2019-07-25 16:54:01
Timestamp: 2019-07-25 16:54:50
Timestamp: 2019-07-25 16:54:50


In [130]:
prior_day_placement.sort_values('ZoneName')

Id  ZoneId  \
0    3293  18       
1    3055  19       
2    2858  20       
3    2859  21       
4    3002  22       
5    3009  17       
6    1091  51       
7    3506  51       
26   2792  48       
27   2801  48       
28   2571  48       
29   2951  48       
30   672   48       
31   705   48       
35   3679  48       
33   1344  48       
34   3221  48       
25   2505  48       
36   3683  48       
37   2774  48       
32   729   48       
23   3018  48       
24   1977  48       
21   3184  48       
8    2968  48       
22   1127  48       
10   3266  48       
11   3609  48       
12   3616  48       
13   3623  48       
14   3507  48       
9    3566  48       
16   3452  48       
17   3054  48       
18   3208  48       
19   3049  48       
20   3542  48       
15   2108  48       
53   3048  49       
54   3209  49       
55   3541  49       
56   1458  49       
57   3508  49       
60   3617  49       
59   3622  49       
61   1976  49       
62   2967  49       
52   3053  49       
58   3265  49       
51   3185  49       
38   2775  49       
49   3017  49       
48   2838  49       
47   2504  49       
46   3300  49       
45   2793  49       
44   2950  49       
43   1343  49       
42   671   49       
41   923   49       
40   3222  49       
39   3678  49       
50   1126  49       
63   2862  93       
65   3050  88       
64   909   88       
66   3052  89       
67   2863  90       
68   2864  91       
69   915   92       
70   3509  94       
71   877   87       
72   3625  87       
73   3510  87       
74   2584  171      
75   3550  180      
76   2519  169      
79   3632  162      
78   3516  162      
77   3016  162      
80   2394  112      
81   1157  112      
82   1158  113      
83   2395  113      
84   2396  114      
85   807   114      
89   3517  165      
88   3012  165      
90   3633  165      
86   2825  165      
87   2826  165      
91   3518  175      
92   3634  175      
93   1263  155      
94   3045  155      
95   3056  155      
96   1267  155      
103  3511  154      
106  3626  154      
105  3088  154      
104  3620  154      
102  3091  154      
97   2843  154      
100  1250  154      
99   1248  154      
98   3545  154      
101  1354  154      
107  1731  160      
108  1745  160      
109  3057  160      
110  3044  160      
117  3512  159      
121  3546  159      
120  2844  159      
119  2518  159      
116  3087  159      
118  3627  159      
114  1723  159      
115  1724  159      
113  2872  159      
112  2871  159      
111  2870  159      
125  3058  151      
124  3618  151      
126  1012  151      
122  998   151      
123  3043  151      
127  2904  177      
128  2905  177      
129  2902  177      
142  3635  150      
141  3613  150      
140  3519  150      
139  3025  150      
138  2947  150      
136  1135  150      
137  1348  150      
134  3543  150      
133  2845  150      
132  2820  150      
131  2823  150      
130  2819  150      
135  993   150      
150  2893  167      
149  2891  167      
148  2890  167      
147  3636  167      
145  3579  167      
144  3013  167      
143  2441  167      
146  3520  167      
151  1704  123      
152  3042  123      
153  3061  125      
154  968   128      
155  2953  131      
159  3521  133      
158  2966  133      
157  2847  133      
156  3014  133      
160  3021  130      
161  3522  130      
162  1703  130      
163  3297  130      
164  3580  130      
165  1666  130      
166  1438  157      
167  3005  157      
168  1424  157      
186  2495  158      
187  3319  158      
188  3320  158      
189  2955  158      
190  1683  158      
191  3223  158      
196  2367  158      
193  1694  158      
194  1697  158      
195  2607  158      
185  3039  158      
198  3681  158      
199  2776  158      
192  2772  158      
184  3216  158      
197  2506  158      
182  3201  158      
179  1684  158      
183  3062  158      
181  2372  158      
180  3023  158   

In [131]:
#Remove Duplicates e.g. GS
source_of_truth_n.drop_duplicates(inplace=True)

In [132]:

# drop error placement
drop_zone_index = source_of_truth_n.loc[source_of_truth_n.ZoneName == 'Bank Pages Sponsored - Popular Accounts Comparison'].index.values
source_of_truth_n.drop(source_of_truth_n.index[drop_zone_index], inplace= True)

# Removing Ally MMA from source of truth
source_of_truth_n = source_of_truth_n.loc[(source_of_truth_n.ShortName!='Jumbo Money Market')]

# Expand Native LP CD Placement
source_of_truth_n.loc[(source_of_truth_n.Term == '18-month') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (18mo CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '1-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (1yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '2-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (2yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '3-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (3yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '4-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (4yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '5-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (5yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '6-year') & (source_of_truth_n.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (6yr CD)']

source_of_truth_n.loc[(source_of_truth_n.Term == '18-month') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (18mo CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '1-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (1yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '2-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (2yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '3-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (3yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '4-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (4yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '5-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (5yr CD)']
source_of_truth_n.loc[(source_of_truth_n.Term == '6-year') & (source_of_truth_n.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (6yr CD)']

In [133]:
#Bank budget adjustment - Since the budget comes from daily MOAT file, this modifier will work and we can adjust in month

#The day we are targetting - day of week adjustment
now = datetime.datetime.today()

#ways to obtain name of the day
# calendar.day_name[now.weekday()]

#Today's date
# now.day

#Yesterday = today minus 1 day 
ysd = now - datetime.timedelta(days=1)

# Compute number of days in month
days_cur_mth=calendar.monthrange(now.year,now.month)[1]

#Days left in month
days_left_cur_mth = days_cur_mth-now.day

In [134]:
#Import Step
path=r'P:\Sales\DA\placement_restrictions_v1.xlsx'
pathcd=r'P:\Sales\DA\PartnerPlacements.xlsx'

In [135]:
xl = pd.ExcelFile(path)
xl_pp = pd.ExcelFile(pathcd)
#xl.sheet_names
#xl_pp.sheet_names

In [136]:
Advertiser=xl.parse('Advertiser')
AdjustmentInMonth=xl.parse('In Month Adjustment')
AdjustmentInWeek=xl.parse('In Week Adjustment')
placement_input=xl.parse('ManualPlacementInput')
email_list=xl.parse('Email Distribution')

In [137]:
#Converting Grid to Rows
def melt(df, col_vars, key, value):
    """
    Converting Grid to List
    """
    keep_vars = df.columns.difference(col_vars)
    melted_sections = []
    for c in col_vars:
        melted_c = df[keep_vars].copy()
        melted_c[key] = c
        melted_c[value] = df[c]
        melted_sections.append(melted_c)
    melted = pd.concat(melted_sections)
    return melted
        

In [146]:
#copy the list
d_y = df['ClickPerDay_yesterday'].copy()
d_sdlw = df['ClickPerDay_same_day_last_week'].copy()
d_7d = df['ClickPerDay_last_7_days'].copy()
d_31d = df['ClickPerDay_last_31_days'].copy()
#d_2m = df['ClickPerDay_2Months'].copy()

#Set up as multiplier, so if not 0 replaced with 1
d_y[d_y>0] = 1
d_sdlw[d_sdlw>0] = 1
d_7d[d_7d>0] = 1
d_31d[d_31d>0] = 1
#d_2m[d_2m>0] = 1
    
# Function for weighting historical click per day
CPDHolder=[]
def CPDfunction(Weight4Mth,Weight2Mth,Weight31Day,Weight7day,Weight1dayLastWeek,WeightYTD):
    
    #assign weight as the value in array
    x1=np.multiply(np.full((df.shape[0],),WeightYTD),d_y)
    x2=np.multiply(np.full((df.shape[0],),Weight1dayLastWeek),d_sdlw)
    x3=np.multiply(np.full((df.shape[0],),Weight7day),d_7d)
    x4=np.multiply(np.full((df.shape[0],),Weight31Day),d_31d)
    #x5=np.multiply(np.full((df.shape[0],),Weight2Mth),d_2m)
    Total=np.sum([x1,x2,x3,x4],axis=0)
    
    n1 = np.multiply(x1,df['RevPerDay_yesterday'])
    n2 = np.multiply(x2,df['RevPerDay_same_day_last_week'])
    n3 = np.multiply(x3,df['RevPerDay_last_7_days'])
    n4 = np.multiply(x4,df['RevPerDay_last_31_days'])
    #n5 = np.multiply(x5,df['ClickPerDay_2Months'])

    df['RevenuePerDay']=np.sum([n1,n2,n3,n4],axis=0)/Total

In [147]:
df[['ClickPerDay_yesterday','ClickPerDay_same_day_last_week','ClickPerDay_last_7_days']]

ClickPerDay_yesterday  ClickPerDay_same_day_last_week  \
0    0.000000               0.000000                         
1    0.000000               0.000000                         
2    0.000000               1.000000                         
3    0.000000               0.000000                         
4    0.000000               0.000000                         
5    0.000000               0.000000                         
6    0.000000               0.000000                         
7    0.000000               0.000000                         
8    0.000000               0.000000                         
9    0.000000               0.000000                         
10   0.000000               0.000000                         
11   0.000000               0.000000                         
12   0.000000               0.000000                         
13   19.000000              18.000000                        
14   0.000000               0.000000                         
15   0.000000               0.000000                         
16   0.000000               0.000000                         
17   0.000000               0.000000                         
18   10.000000              9.000000                         
19   0.000000               0.000000                         
20   0.000000               0.000000                         
21   0.000000               0.000000                         
22   27.000000              14.000000                        
23   0.000000               0.000000                         
24   12.000000              0.000000                         
25   0.000000               0.000000                         
26   0.000000               0.000000                         
27   0.000000               0.000000                         
28   114.000000             0.000000                         
29   0.000000               0.000000                         
30   208.000000             0.000000                         
31   0.000000               0.000000                         
32   0.000000               0.000000                         
33   0.000000               0.000000                         
34   0.000000               0.000000                         
35   168.000000             0.000000                         
36   0.000000               0.000000                         
37   0.000000               0.000000                         
38   12.500000              0.000000                         
39   0.000000               0.000000                         
40   0.000000               0.000000                         
41   0.000000               0.000000                         
42   0.000000               0.000000                         
43   0.000000               0.000000                         
44   0.000000               0.000000                         
45   12.000000              0.000000                         
46   170.000000             0.000000                         
47   150.000000             0.000000                         
48   2.500000               0.000000                         
49   27.000000              0.000000                         
50   2.500000               0.000000                         
51   0.000000               0.000000                         
52   0.000000               0.000000                         
53   0.000000               0.000000                         
54   0.000000               0.000000                         
55   0.000000               0.000000                         
56   0.000000               2.000000                         
57   13.000000              0.000000                         
58   0.000000               0.000000                         
59   0.000000               0.000000                         
60   0.000000               0.000000                         
61   0.000000               0.000000                         
62   0.000000               0.000000                         
63   1.000000               1.000000 

In [148]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

Timestamp: 2019-07-25 17:09:13


In [149]:
# # Assigning weight to historical period
W_4mth=0.0
W_2mth=0.005
W_1mth=0.095
W_1wk=.3
W_1daylastwk=0.1
W_yesterday=.5

# tried: 0.1;0.2;0.2;0.5

CPDfunction(W_4mth,W_2mth,W_1mth,W_1wk,W_1daylastwk,W_yesterday)
CPDX=pd.DataFrame(CPDHolder)
# CPDX.head()

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:33: RuntimeWarning: invalid value encountered in true_divide


In [142]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

Timestamp: 2019-07-25 17:06:03


In [143]:
#Used for data check
# x1=np.multiply(np.full((df.shape[0],),W_yesterday),d_y)
# x2=np.multiply(np.full((df.shape[0],),W_1daylastwk),d_sdlw)
# x3=np.multiply(np.full((df.shape[0],),W_1wk),d_7d)
# x4=np.multiply(np.full((df.shape[0],),W_1mth),d_31d)
# x5=np.multiply(np.full((df.shape[0],),W_2mth),d_2m)
# Total=np.sum([x1,x2,x3,x4,x5],axis=0)

# x1
# x2
# x3
# x4
# x5
# Total

In [144]:
#Calculate numebr of counts has even shown on bank own placements.
#test with the following code using source of truth, but we can leverage historical data better if we use dfquniq
#sot_uniq is the same, but dfUniq has more old advertisers
#sot_uniq = source_of_truth_n.groupby(by=['ZoneName','AdvertiserName'], as_index=False).last()[['ZoneName','AdvertiserName']]
dfUniq=pd.DataFrame(df.groupby(['SiteName','ZoneName','AdvertiserName'],as_index=False)['ClickPerDay'].count())
dfUniq=dfUniq.rename(columns={'ClickPerDay':'UniqueProductShown'})
# dfUniq.head()

In [145]:
def fixCapOne(ProductName):
    """
    Update CapOne Product Name so the conditions for CD term length can be applied.
    """
    if '360' in ProductName:
        ProductName=ProductName.replace('360',' ')
    else:
        ProductName
    return ProductName

def termlength(Product,ProductName):
    """
    Create term for CD products
    """
    #Create CD Term
    if 'CD' in Product:
        if 'Month' in ProductName:
            #Moved up so it won't become 3 mo
            if '36' in ProductName:
                return '3yr CD'
            elif '12' in ProductName or '11' in ProductName or '13' in ProductName or '14' in ProductName:
                return '1yr CD'
            elif '3' in ProductName:
                return '3mo CD'
            #Moved up so it won't become 6 mo
            elif '60' in ProductName:
                return '5yr CD'
            elif '6' in ProductName or '9' in ProductName:
                return '6mo CD'
            elif '18' in ProductName:
                return '18mo CD'
            elif '24' in ProductName:
                return '2yr CD'
            elif '48' in ProductName:
                return '4yr CD'
        elif '1' in ProductName:
            return '1yr CD'
        elif '2' in ProductName:
            return '2yr CD'
        elif '3' in ProductName:
            return '3yr CD'
        elif '4' in ProductName:
            return '4yr CD'
        elif '5' in ProductName: 
            return '5yr CD'
        elif '6' in ProductName:
            return '6yr CD'
        else:
            return 'None'
        
    else:
        return 'None'

In [152]:
#Create this ranking to start optimizing
df['SiteZoneAdvertiserRank']=df.groupby(['SiteName','ZoneName','AdvertiserName'])['RevenuePerDay'].rank(method='dense',ascending=False)
##added to identify being used in Zone Placement
df['UsedInLoop']=0
# df.head()

In [153]:
#Adding CD terms below for LP CD placements name update 

#merge unique tables
df=pd.merge(df, dfUniq, how='inner', left_on=['SiteName', 'ZoneName', 'AdvertiserName'],right_on=['SiteName', 'ZoneName','AdvertiserName'])
df=df.sort_values(by=['SiteName','ZoneName','AdvertiserName','SiteZoneAdvertiserRank'], ascending=True).reset_index(drop=True)

#for LP placements
df.ProductName = df.apply(lambda df:fixCapOne(df['ProductName']),axis=1)
prior_d_pl.ProductName = prior_d_pl.apply(lambda prior_d_pl:fixCapOne(df['ProductName']),axis=1)
df['CDTerm']=df.apply(lambda df:termlength(df['ProductDetail'],df['ProductName']),axis=1)
prior_d_pl['CDTerm']=prior_d_pl.apply(lambda prior_d_pl:termlength(prior_d_pl['ProductDetail'],prior_d_pl['ProductName']),axis=1)

# Make Spot Available a float data type
df.SpotAvailable=df.SpotAvailable.astype(float)

In [154]:
# update all LP SEM abd LP Native zone name with term
prior_d_pl['ZoneName'] = np.where((prior_d_pl['ProductDetail']=='CDs'), np.where(prior_d_pl['ZoneName']=='LP - SEM (CD)','LP - SEM ('+prior_d_pl['CDTerm']+')',prior_d_pl['ZoneName']),prior_d_pl['ZoneName'])
prior_d_pl['ZoneName'] = np.where((prior_d_pl['ProductDetail']=='CDs'), np.where(prior_d_pl['ZoneName']=='LP - Native (CD)','LP - Native ('+prior_d_pl['CDTerm']+')',prior_d_pl['ZoneName']),prior_d_pl['ZoneName'])
df.ZoneName = np.where((df['ProductDetail']=='CDs'), np.where(df['ZoneName']=='LP - SEM (CD)','LP - SEM ('+df['CDTerm']+')',df['ZoneName']),df['ZoneName'])
df.ZoneName = np.where((df['ProductDetail']=='CDs'), np.where(df['ZoneName']=='LP - Native (CD)','LP - Native ('+df['CDTerm']+')',df['ZoneName']),df['ZoneName'])

In [155]:
#Display Placement

#Compute # of Display Spots to be assigned
display_ct = source_of_truth_n.loc[source_of_truth_n.ZoneName.str.contains('Display')].groupby('ZoneName', as_index = False).count()[['ZoneName','Priority']]

# Display placement count based on how many approved on source of truth
df.loc[(df.ZoneName == 'Display - BTF'), 'SpotAvailable'] =display_ct.Priority[0]
df.loc[(df.ZoneName == 'Display - ATF'), 'SpotAvailable'] =display_ct.Priority[1]
df.loc[(df.ZoneName == 'Display - Footer'), 'SpotAvailable'] =display_ct.Priority[2]

In [156]:
# Advertiser Product Mapping

# Adding CD Term 
advertiser_product['product_name']=advertiser_product.apply(lambda advertiser_product:fixCapOne(advertiser_product['product_name']),axis=1)
advertiser_product['CDTerm']=advertiser_product.apply\
(lambda advertiser_product:termlength(advertiser_product['ProductDetail'],advertiser_product['product_name']),axis=1)

In [157]:
#Aggregate Click per Day per Site, Zone, Advertiser
x=df.groupby(['SiteName','ZoneName','AdvertiserName'],as_index=False).sum()[['SiteName','ZoneName','AdvertiserName','ClickPerDay']]
# x.head()

#### need to import revenue needed from MOAT

In [158]:
Advertiser

AdvertiserMoat                      Advertiser   Product  \
0   Synchrony               Synchrony Bank                  Both       
1   Ally                    Ally Bank                       Savings    
2   Ally                    Ally Bank                       CDs        
3   Penfed                  Penfed Credit Union             CDs        
4   GS Bank                 Goldman Sachs Bank USA          Both       
5   Capital One             Capital One                     CDs        
6   Capital One             Capital One                     MMA        
7   Capital One             Capital One                     Business   
8   Barclays                Barclays                        Savings    
9   Barclays                Barclays                        CDs        
10  NBKC Bank               nbkc bank                       Checking   
11  NBKC Bank               nbkc bank                       Business   
12  American Express        American Express National Bank  Savings    
13  American Express        American Express National Bank  CDs        
14  Live Oak Bank           Live Oak Bank                   Business   
15  CIT                     CIT Bank                        Savings    
16  HSBC Direct             HSBC Direct                     Savings    
17  Vio Bank                Vio Bank                        Savings    
18  Vio Bank                Vio Bank                        CDs        
19  Simple                  Simple                          Checking   
20  UFB Direct (Axos Bank)  UFB Direct                      Savings    
21  UFB Direct (Axos Bank)  UFB Direct                      MMA        
22  Axos Bank               Axos Bank                       Checking   
23  Axos Bank               Axos Bank                       Business   
24  Citizens Access         Citizens Access                 Both       
25  Purepoint               PurePoint Financial             Savings    
26  Purepoint               PurePoint Financial             CDs        
27  First Internet Bank     First Internet Bank             Business   
28  First Internet Bank     First Internet Bank             MMA        
29  Earn.Bank               earn.bank                       MMA        
30  Discover                Discover Bank                   Both       
31  BBVA Compass            BBVA Compass                    Both       
32  NASB                    North American Savings Bank     Savings    
33  Aspiration              Aspiration                      Checking   
34  Citi                    Citi                            Savings    
35  PNC                     PNC Bank                        Savings    
36  CIBC                    CIBC USA                        Savings    
37  WebBank                 WebBank                         Savings    
38  Rising Bank             Rising Bank                     CDs        
39  Customers Bank          Customers Bank                  Savings    

    Product_business Placement        Budget      MTD  Optimal Pacing  \
0   NaN               All       0.000000      0.0      0.000000         
1   NaN               All       0.000000      1794.5   0.000000         
2   NaN               All       5056.000000   1794.5   3914.322581      
3   NaN               All      NaN           NaN      NaN               
4   NaN               All       40000.000000  27597.0  30967.741935     
5   NaN               All       12272.727273  3780.0   9501.466276      
6   NaN               All       6363.636364   5307.0   4926.686217      
7   Business Savings  All      NaN           NaN      NaN               
8   NaN               All       5727.272727   4260.0   4434.017595      
9   NaN               All      NaN            0.0     NaN               
10  NaN               All       100.000000    20.0     77.419355        
11  NaN               All       900.000000    754.0    696.774194       
12  NaN               All       11600.000000  8826.0   8980.645161      
13  NaN               All       0.000

In [601]:
##Bank Budget Day of Month Adjustment

##Look up matching week
DayOfWeekAdjusted=float(AdjustmentInWeek[AdjustmentInWeek['Day']==calendar.day_name[now.weekday()]]['Selected'])
##Looking up matching month
DayOfMonthAdjusted=float(AdjustmentInMonth[AdjustmentInMonth['dayOfMonth']==now.day]['Selected'])

##Adjustment
Advertiser['Adjusted Clicks']=Advertiser['Clicks needed per day']*DayOfWeekAdjusted*DayOfMonthAdjusted
Advertiser['Running Budget']=Advertiser['Clicks needed per day']*DayOfWeekAdjusted*DayOfMonthAdjusted

In [602]:
##To Manually Assign Advertiser order since saving spot is more important
def ManualAdvertiserAssignment(Advertiser):
    
    if 'American' in Advertiser:
        return 2
    elif 'Barclay' in Advertiser:
        return 1
    elif 'Synchrony' in Advertiser:
        return 1
    else:
        return 1

In [603]:
Advertiser['NewRank']=Advertiser.apply(lambda Advertiser: ManualAdvertiserAssignment(Advertiser['Advertiser']),axis=1)
Advertiser=Advertiser.sort_values(by=['NewRank','Adjusted Clicks'],ascending=False).reset_index(drop=True)

In [604]:
## could be eliminate after having source of truth
def ProductType(zone):
    
    if 'Bus' in zone:
        return 'Business'
    elif 'CD' in zone:
        return 'CDs'
    elif 'Sav' in zone:
        return 'Savings'
    elif 'Ch' in zone:
        return 'Checking'
    elif 'MM' in zone:
        return 'MMA'
    elif 'Money Market' in zone:
        return 'MMA'
    elif 'IRA' in zone:
        return 'IRAs'
    else:
        return 'Both'

In [605]:
#Obtain All Placements Availables
availablePlacement = source_of_truth_n.groupby(['ZoneName'], as_index= False).last()[['ZoneName','ZoneType','ZoneID','zonegroup','SpotAvailable']]

#Adding placement type **************** this could be elimitated since we have source of truth
#availablePlacement['ProductLookUp']=availablePlacement['ZoneName'].apply(ProductType)
##added to identify being used in Zone Placement
availablePlacement['SpotUsed']=0

In [606]:
zone_quality_sort

ZoneName  \
0   Account Comparison (1yr CD)                                    
1   Account Comparison (2yr CD)                                    
2   Account Comparison (3yr CD)                                    
3   Account Comparison (4yr CD)                                    
4   Account Comparison (5yr CD)                                    
5   Account Comparison (Savings)                                   
6   Bank Pages - Horizontal                                        
7   Bank Pages Sponsored - Most Popular Accounts                   
8   Bank Pages Sponsored - Open An Account                         
9   Bank Pages Sponsored - Popular Accounts Comparison (18mo CD)   
10  Bank Pages Sponsored - Popular Accounts Comparison (1yr CD)    
11  Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)    
12  Bank Pages Sponsored - Popular Accounts Comparison (3yr CD)    
13  Bank Pages Sponsored - Popular Accounts Comparison (4yr CD)    
14  Bank Pages Sponsored - Popular Accounts Comparison (5yr CD)    
15  Bank Pages Sponsored - Popular Accounts Comparison (MMA)       
16  Bank Pages Sponsored - Popular Accounts Comparison (Sav)       
17  Blog Best CD Accounts                                          
18  Blog Best Savings Accounts                                     
19  CC - Sidebar - Featured Accounts                               
20  Display - ATF                                                  
21  Display - BTF                                                  
22  Display - Footer                                               
23  HiatusApp - Recommended Accounts                               
24  KPGR - Sidebar - Featured Accounts                             
25  LP - Native (CD)                                               
26  LP - Native (Sav)                                              
27  LP - Native MSN Page (Savings)                                 
28  LP - SEM (CD)                                                  
29  LP - SEM (Sav)                                                 
30  LP - SEM B (Sav)                                               
31  LT - CRM Email                                                 
32  LT - Rate Table (18mo CD)                                      
33  LT - Rate Table (1yr CD)                                       
34  LT - Rate Table (2yr CD)                                       
35  LT - Rate Table (3yr CD)                                       
36  LT - Rate Table (4yr CD)                                       
37  LT - Rate Table (5yr CD)                                       
38  LT - Rate Table (MMA)                                          
39  LT - Rate Table (Savings)                                      
40  MagnifyMoney - Account Comparison                              
41  MagnifyMoney - BP - Most Popular Accounts                      
42  MagnifyMoney - Featured Accounts Sidebar                       
43  MagnifyMoney - LP (CD)                                         
44  MagnifyMoney - LP (Sav)                                        
45  MagnifyMoney - Rate table and Blogs (CD)                       
46  MagnifyMoney - Rate table and Blogs (Sav and MMA)              
47  Main Rate Table (18mo CD)                                      
48  Main Rate Table (1yr CD)                                       
49  Main Rate Table (2yr CD)                                       
50  Main Rate Table (3yr CD)                                       
51  Main Rate Table (4yr CD)                                       
52  Main Rate Table (5yr CD)                                       
53  Main Rate Table (Money Market)                                 
54  Main Rate Table (Savings)                                      
55  MyLT - Recommended Alert                                       
56  Sidebar - Featured Accounts                                    
57  Sidebar - Featured Rates (CD 1yr)                              
58  Sidebar - Featured Rates (Savings)      

In [607]:
zone_quality_lp_sem#.iloc[5]['open_rate']

ZoneName      Term zonegroup  open_rate
0  LP - SEM (CD)  1-year    zone_4    0.034    
1  LP - SEM (CD)  18-month  zone_4    0.000    
2  LP - SEM (CD)  2-year    zone_4    0.027    
3  LP - SEM (CD)  3-year    zone_4    0.004    
4  LP - SEM (CD)  4-year    zone_4    0.003    
5  LP - SEM (CD)  5-year    zone_4    0.007

In [608]:
# Create placements for LP

# max row index to be used
zone_q_sort_max=zone_quality_sort.index.max()

#Creating new palcement with the average open rate
zone_quality_sort.loc[zone_q_sort_max+1]=['LP - Native (18mo CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]#to be more convervative
zone_quality_sort.loc[zone_q_sort_max+2]=['LP - Native (1yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]
zone_quality_sort.loc[zone_q_sort_max+3]=['LP - Native (2yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]
zone_quality_sort.loc[zone_q_sort_max+4]=['LP - Native (3yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]
zone_quality_sort.loc[zone_q_sort_max+5]=['LP - Native (4yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]
zone_quality_sort.loc[zone_q_sort_max+6]=['LP - Native (5yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]
zone_quality_sort.loc[zone_q_sort_max+7]=['LP - Native (6yr CD)','Landing Page',155, 30, 'zone_4', zone_quality_sort.loc[zone_quality_sort.ZoneName == 'LP - Native (CD)']['open_rate'].values[0]]

zone_quality_sort.loc[zone_q_sort_max+8]=['LP - SEM (18mo CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[1]['open_rate']]#to be more convervative
zone_quality_sort.loc[zone_q_sort_max+9]=['LP - SEM (1yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[0]['open_rate']]
zone_quality_sort.loc[zone_q_sort_max+10]=['LP - SEM (2yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[2]['open_rate']]
zone_quality_sort.loc[zone_q_sort_max+11]=['LP - SEM (3yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[3]['open_rate']]
zone_quality_sort.loc[zone_q_sort_max+12]=['LP - SEM (4yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[4]['open_rate']]
zone_quality_sort.loc[zone_q_sort_max+13]=['LP - SEM (5yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[5]['open_rate']]
zone_quality_sort.loc[zone_q_sort_max+14]=['LP - SEM (6yr CD)','Landing Page',151, 30, 'zone_4', zone_quality_lp_sem.iloc[5]['open_rate']]

#remove the old one
zone_quality_sort=zone_quality_sort[zone_quality_sort.ZoneName!='LP - Native (CD)'].reset_index(drop=True)
zone_quality_sort=zone_quality_sort[zone_quality_sort.ZoneName!='LP - SEM (CD)'].reset_index(drop=True)

In [609]:
# max row index to be used
zone_cpd_sort_max=PlacementRanking.index.max()

#Creating new palcement with the average cpd
PlacementRanking.loc[zone_cpd_sort_max+1]=['DepositAccounts.com','LP - Native (18mo CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]#to be more convervative
PlacementRanking.loc[zone_cpd_sort_max+2]=['DepositAccounts.com','LP - Native (1yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+3]=['DepositAccounts.com','LP - Native (2yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+4]=['DepositAccounts.com','LP - Native (3yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+5]=['DepositAccounts.com','LP - Native (4yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+6]=['DepositAccounts.com','LP - Native (5yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+7]=['DepositAccounts.com','LP - Native (6yr CD)','Landing Page',155, PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]

PlacementRanking.loc[zone_cpd_sort_max+8]=['DepositAccounts.com','LP - SEM (18mo CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]#to be more convervative
PlacementRanking.loc[zone_cpd_sort_max+9]=['DepositAccounts.com','LP - SEM (1yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+10]=['DepositAccounts.com','LP - SEM (2yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+11]=['DepositAccounts.com','LP - SEM (3yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+12]=['DepositAccounts.com','LP - SEM (4yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+13]=['DepositAccounts.com','LP - SEM (5yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]
PlacementRanking.loc[zone_cpd_sort_max+14]=['DepositAccounts.com','LP - SEM (6yr CD)','Landing Page',151,PlacementRanking.loc[PlacementRanking.ZoneName == 'LP - SEM (CD)']['averageClicks'].values[0]]

#remove the old one
PlacementRanking=PlacementRanking[PlacementRanking.ZoneName!='LP - Native (CD)'].reset_index(drop=True)
PlacementRanking=PlacementRanking[PlacementRanking.ZoneName!='LP - SEM (CD)'].reset_index(drop=True)

In [610]:
#Putting together placement order by zonegroup, open rate, avg clicks

#join source of truth with open rate
zone_sort = pd.merge(zone_quality_sort, availablePlacement,how = 'right', left_on=['ZoneName','ZoneType','ZoneID','zonegroup','SpotAvailable'],right_on=['ZoneName','ZoneType','ZoneID','zonegroup','SpotAvailable'])

#join source of truth with avg clicks
zone_sort = pd.merge(PlacementRanking, zone_sort,how = 'right', left_on=['ZoneName','ZoneType','ZoneID'],right_on=['ZoneName','ZoneType','ZoneID'])

# drop site name since it is not needed
zone_sort.drop('SiteName', axis=1, inplace=True)

# fill na for open rate and avg clicks
zone_sort.update(zone_sort[['open_rate']].fillna(0.01))
zone_sort.update(zone_sort[['averageClicks']].fillna(0.0))

# compute account opens count for sorting
zone_sort['account_open'] = zone_sort.averageClicks * zone_sort.open_rate

# sort the zones the right way
zone_sort = zone_sort.sort_values(by = ['zonegroup','open_rate','account_open','averageClicks'],ascending=[True, False, False, False]).reset_index(drop = True)

In [611]:
##To Manually Assign placement order e.g. MagMoney, Business, others
def ManualPlacementAssignment(SiteNameNew,ZoneNameNew,ProductNew):
    
    if 'Mag' in SiteNameNew:
        return 5
    elif 'Bus' in ProductNew:
        return 2
    elif 'Most Popular Accounts' in ZoneNameNew or 'Open An Account' in ZoneNameNew:
        return 6
    elif 'Display' in ZoneNameNew:
        return 4
    elif 'Sidebar' in ZoneNameNew:
        return 3
    else:
        return 2

In [612]:
CPD_placement_all=CPD_placement_all[['SiteName','ZoneName','ZoneID','ProductDetail','averageClicks']]

CPD_placement_allMaxRow=CPD_placement_all.index.max()

#Adjust CPD_placement_all for LP
CPD_placement_all.loc[CPD_placement_allMaxRow+1]=['DepositAccounts.com','LP - Native (18mo CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+2]=['DepositAccounts.com','LP - Native (1yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+3]=['DepositAccounts.com','LP - Native (2yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+4]=['DepositAccounts.com','LP - Native (3yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+5]=['DepositAccounts.com','LP - Native (4yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+6]=['DepositAccounts.com','LP - Native (5yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+7]=['DepositAccounts.com','LP - Native (6yr CD)',155,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]

CPD_placement_all.loc[CPD_placement_allMaxRow+8]=['DepositAccounts.com','LP - SEM (18mo CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+9]=['DepositAccounts.com','LP - SEM (1yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+10]=['DepositAccounts.com','LP - SEM (2yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+11]=['DepositAccounts.com','LP - SEM (3yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+12]=['DepositAccounts.com','LP - SEM (4yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+13]=['DepositAccounts.com','LP - SEM (5yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]
CPD_placement_all.loc[CPD_placement_allMaxRow+14]=['DepositAccounts.com','LP - SEM (6yr CD)',151,'CDs', CPD_placement_all.loc[CPD_placement_all.ZoneName == 'LP - Native (CD)']['averageClicks'].values[0]]


CPD_placement_all=CPD_placement_all[CPD_placement_all.ZoneName!='LP - Native (CD)'].reset_index(drop=True)
CPD_placement_all=CPD_placement_all[CPD_placement_all.ZoneName!='LP - SEM (CD)'].reset_index(drop=True)

# Catch all product rank per placement
CPD_placement_all['SiteZoneProductRank']=CPD_placement_all.groupby(['SiteName','ZoneName'])['averageClicks'].rank(method='dense',ascending=False)
CPD_placement_all=CPD_placement_all.sort_values(by=['SiteName','ZoneName','SiteZoneProductRank'],ascending=True).reset_index(drop=True)


In [613]:
Advertiser=Advertiser.sort_values(by=['NewRank','Adjusted Clicks'],ascending=False).reset_index(drop=True)

# Clustering for Advertiser Grouping

In [614]:
df_sot = df[['ZoneName','ZoneType','ZoneID','AdvertiserName','ProductName','ProductDetail','ClickPerDay','ClickPerDay_yesterday','ClickPerDay_last_7_days']]

In [615]:
cluster = df_sot.groupby('AdvertiserName',as_index=False).sum()[['ClickPerDay_last_7_days']]

In [616]:
cluster_ad = df_sot.groupby('AdvertiserName',as_index=False).sum()[['AdvertiserName','ClickPerDay_last_7_days']]

In [617]:
# replace any inf
cluster.ClickPerDay_last_7_days.replace(np.inf,0.0,inplace=True)

In [618]:
from sklearn.cluster import KMeans

In [619]:
kmean = KMeans(n_clusters=3)

In [620]:
kmean.fit(cluster)

KMeans(algorithm='auto', copy_x=True, init='k-means++', max_iter=300,
    n_clusters=3, n_init=10, n_jobs=None, precompute_distances='auto',
    random_state=None, tol=0.0001, verbose=0)

In [621]:
cluster['clusters']=kmean.fit_predict(cluster)

In [622]:
cluster_ad['cluster'] = kmean.fit_predict(cluster)

In [623]:
cluster_ad

AdvertiserName  ClickPerDay_last_7_days  cluster
0   Ally Bank                       259.500000               2      
1   American Express National Bank  328.943414               2      
2   Aspiration                      68.800000                0      
3   Axos Bank                       0.000000                 0      
4   BBVA Compass                    17.704819                0      
5   Barclays                        873.636044               1      
6   CIT Bank                        0.000000                 0      
7   Capital One                     499.677011               2      
8   Citi                            0.000000                 0      
9   Citizens Access                 0.000000                 0      
10  Discover Bank                   180.100000               2      
11  Filler - Bank5 Connect          2.400000                 0      
12  Filler - FNBO DIrect            8.000000                 0      
13  Filler - Midfirst Direct        2.800000                 0      
14  Filler - Popular Direct         14.500000                0      
15  Filler - Radius Bank            2.200000                 0      
16  Filler - iGoBanking             4.500000                 0      
17  First Internet Bank             56.307317                0      
18  Goldman Sachs Bank USA          1261.482551              1      
19  HSBC Direct                     381.360462               2      
20  Live Oak Bank                   12.178723                0      
21  North American Savings Bank     0.000000                 0      
22  Penfed Credit Union             0.000000                 0      
23  PurePoint Financial             78.600000                0      
24  Simple                          19.400000                0      
25  Synchrony Bank                  0.000000                 0      
26  UFB Direct                      252.500000               2      
27  Vio Bank                        125.050000               0      
28  earn.bank                       0.000000                 0      
29  nbkc bank                       46.849057                0

In [624]:
#Initial thoughts to get it up, but actual data will converage to new data points
#cluster_ad['cluster']=np.where(cluster_ad.ClickPerDay_last_7_days==0,cluster_ad.cluster.max()+1,cluster_ad.cluster)

In [625]:
#Create CPD by Zone Product Cluster as catch all for new comers and SOT grid NAN
df_sot_cl = pd.merge(df_sot, cluster_ad[['AdvertiserName','cluster']], 'left', ['AdvertiserName'])

In [626]:
df_sot_cl.loc[df_sot_cl.ZoneName =="MagnifyMoney - Featured Accounts Sidebar" ]

ZoneName                      ZoneType  \
397  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
398  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
399  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
400  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
401  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
402  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
403  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
404  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
405  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
406  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
407  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
408  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
409  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
410  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
411  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   
412  MagnifyMoney - Featured Accounts Sidebar  Side Bar - Featured Accounts   

     ZoneID                  AdvertiserName  \
397  156     Ally Bank                        
398  156     American Express National Bank   
399  156     Aspiration                       
400  156     Barclays                         
401  156     Barclays                         
402  156     CIT Bank                         
403  156     Capital One                      
404  156     Goldman Sachs Bank USA           
405  156     Goldman Sachs Bank USA           
406  156     HSBC Direct                      
407  156     North American Savings Bank      
408  156     Penfed Credit Union              
409  156     PurePoint Financial              
410  156     Simple                           
411  156     Synchrony Bank                   
412  156     Synchrony Bank                   

                                     ProductName ProductDetail  ClickPerDay  \
397  High Yield 12-Month CD                       CDs           156.235000    
398  High Yield Savings Account                   Savings       36.864611     
399  Spend and Save Account                       Checking      10.978676     
400  12 Month Online CD                           CDs           53.004688     
401  Online Savings Account                       Savings       31.019328     
402  Savings Builder                              Savings       43.700000     
403  12 Month   CD                                CDs           72.238095     
404  High-yield 12 Month CD                       CDs           64.920417     
405  High-yield Online Savings Account            Savings       23.035000     
406  HSBC Direct Savings                          Savings       76.450121     
407  High Rate Savings                            Savings       13.500000     
408  12 Month Money Market Certificate            CDs           38.000000     
409  Online Savings                               Savings       61.725000     
410  Checking Account + Protected Goals Account*  Checking      17.283103     
411  12 Month CD                                  CDs           173.347826    
412  High Yield Savings                           Savings       10.571429     

     ClickPerDay_yesterday  ClickPerDay_last_7_days  cluster  
397  0.0                    0.0                      2        
398  40.0                   37.0                     2        
399  6.0                    11.6                     0        
400  0.0                    0.0                      1        
401  32.0                   33.3                     1        
402  0.0                    0.0                      0        
403  0.0                    0.0                      2        
404  0.0                    0.0              

In [627]:
#Create CPD by Zone Product Cluster as catch all for new comers and SOT grid NAN
df_sot_cl = pd.merge(df_sot, cluster_ad[['AdvertiserName','cluster']], 'left', ['AdvertiserName'])

# Step 1: mapping clusters by advertisers

#remove inf value
df_sot_cl.replace([np.Inf, -np.Inf], np.nan, inplace = True)
df_sot_cl.dropna(subset=["ClickPerDay"], how="any", axis = 0, inplace = True)
#Obtain CPD value by Zone Product Cluster
df_sot_cl = df_sot_cl.groupby(['ZoneName','ProductDetail','cluster'],as_index = False).mean()[['ZoneName','ProductDetail','cluster','ClickPerDay']]

In [628]:
# Adding Clusters to Advertiser Table
Advertiser = pd.merge(Advertiser, cluster_ad[['AdvertiserName','cluster']], 'left', left_on='Advertiser', right_on = ['AdvertiserName'])

In [629]:
# Step 2: fill in custers for new advertisers

# Identify new advertisers that don't have any clicks in the past 2 months
ad_na = Advertiser[Advertiser['cluster'].isnull()]

# Remove cluster column so can be merge later
ad_na.drop(ad_na.columns[-1],axis=1,inplace=True)
ad_na.sort_values(by=['Budget'],inplace=True)

# Create look up table
ad_cl_lookup = Advertiser[['Budget','cluster']]
ad_cl_lookup.sort_values(by='Budget',ascending=False,inplace=True)

# New Advertisers won't have clusters in the look up table. Will drop NA
ad_cl_lookup = ad_cl_lookup.dropna()

# Cluster lookup step
ad_append = pd.merge_asof(ad_na, ad_cl_lookup.sort_values('Budget'), on= 'Budget', direction='nearest')

# Remove NAN from Advertiser Table
Advertiser.dropna(axis = 0, subset = ['cluster'], how = 'any', inplace = True)

# Append the new column back to the Advertiser table
Advertiser = Advertiser.append(ad_append)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)
C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] == '':
C:\Users\ctam\AppData\Local\Continuum\

In [630]:
# Advertiser Grouping for easier cluster look up for SOT Grid below
cluster_ad = cluster_ad.append(ad_append[['Advertiser','Clicks needed per day','cluster']].rename(columns = {'Advertiser':'AdvertiserName',\
                                                                                               'Clicks needed per day':'ClickPerDay_last_7_days'}))

# Source of Truth Data Fill

In [631]:
# Step 1: Look up from df table for the zone, advertiser, product name
sot_grid = pd.merge(source_of_truth_n, df_sot, 'left', ['ZoneName','ZoneType','ZoneID','AdvertiserName','ProductName','ProductDetail'])

In [632]:
# Step 2: Create advertiser cluster look up for sot_grid, so that it can look up the related CPD from same cluster
#ad_cluster = Advertiser.groupby(['Advertiser'],as_index = False).last()[['Advertiser','cluster']]
sot_grid = pd.merge(sot_grid, cluster_ad[['AdvertiserName','cluster']], 'left', left_on=['AdvertiserName'], right_on= ['AdvertiserName'])

In [633]:
# identify null rows
sot_grid_temp = sot_grid.loc[sot_grid.ClickPerDay.isnull()]
# remove CPD columns to be added later
sot_grid_temp.drop(['ClickPerDay'], axis = 1, inplace=True)

In [634]:
# Step3: merge using Zone, Product Type, Clusters
sot_grid_temp = pd.merge(sot_grid_temp, df_sot_cl, how = 'left', on=['ZoneName','ProductDetail','cluster'])
sot_grid_temp2 = sot_grid_temp.loc[sot_grid_temp.ClickPerDay.isnull()]

In [635]:
sot_grid_temp2.drop(['ClickPerDay'], axis = 1, inplace=True)

In [636]:
sot_grid_catch_all = CPD_placement_all.groupby(['ZoneName','ProductDetail'],as_index= False).mean()[['ZoneName','ProductDetail','averageClicks']].rename(columns = {'averageClicks':'ClickPerDay'})

In [637]:
# Step4: merge using Zone, Product Type
sot_grid_temp2 = pd.merge(sot_grid_temp2, sot_grid_catch_all, how = 'left', on=['ZoneName','ProductDetail'])

In [638]:
sot_grid_temp3 = sot_grid_temp2.loc[sot_grid_temp2.ClickPerDay.isnull()]

In [639]:
sot_grid_catch_all_zone = CPD_placement_all.groupby(['ZoneName'],as_index= False).mean()[['ZoneName','averageClicks']].rename(columns = {'averageClicks':'ClickPerDay'})

In [640]:
#Step 4: merge using Zone
sot_grid_temp3.drop(['ClickPerDay'], axis = 1, inplace=True)
sot_grid_temp3 = pd.merge(sot_grid_temp3, sot_grid_catch_all_zone, how = 'left', on=['ZoneName'])

In [641]:
sot_grid_temp4 = sot_grid_temp3.loc[sot_grid_temp3.ClickPerDay.isnull()]

In [642]:
# Step 5: only 16 Null, so make them 1
sot_grid_temp4[['ClickPerDay']]=sot_grid_temp4[['ClickPerDay']].fillna(value=1)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3140: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[k1] = value[k2]


In [643]:
# Merge the Null row back

sot_grid.dropna(subset=['ClickPerDay'], inplace=True)
sot_grid_temp.dropna(subset=['ClickPerDay'], inplace=True)
sot_grid_temp2.dropna(subset=['ClickPerDay'], inplace=True)
sot_grid_temp3.dropna(subset=['ClickPerDay'], inplace=True)

In [644]:
####need to merge temp 1-3
sot_grid=sot_grid.append(sot_grid_temp, ignore_index=True)
sot_grid=sot_grid.append(sot_grid_temp2, ignore_index=True)
sot_grid=sot_grid.append(sot_grid_temp3, ignore_index=True)
sot_grid=sot_grid.append(sot_grid_temp4, ignore_index=True)

In [645]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

Timestamp: 2019-04-12 13:32:19


# Core Algorithm

## Allocating Clicks to Zone 1-3

In [646]:
################ joining the budget product type for later use
### have to use 'Advertiser' so it won't have NAs
budget_product = Advertiser[['Advertiser','Product']]
budget_product.rename(columns={'Advertiser':'AdvertiserName'}, inplace=True)
sot_grid = pd.merge(sot_grid, budget_product, how = 'left',left_on = ['AdvertiserName', 'ProductDetail'],right_on = ['AdvertiserName', 'Product']).fillna({'Product':'Both'})

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3781: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)


In [647]:
sot_grid

AdvertiserName   Apy  Archived  ClickPerDay  \
0    Discover Bank                   2.10  0         7.378148      
1    Discover Bank                   2.10  0         5.409716      
2    Discover Bank                   2.10  0         1.023615      
3    Discover Bank                   2.10  0         9.284778      
4    Discover Bank                   2.10  0         8.574074      
5    Discover Bank                   2.10  0         3.533148      
6    Discover Bank                   2.10  0         332.539500    
7    Discover Bank                   2.65  0         13.401056     
8    Discover Bank                   2.65  0         2.288254      
9    Discover Bank                   2.70  0         1.518000      
10   Discover Bank                   2.75  0         1.300417      
11   Discover Bank                   2.80  0         1.000000      
12   Discover Bank                   3.00  0         9.469944      
13   Discover Bank                   0.65  0         1.000000      
14   Discover Bank                   3.00  0         1.313019      
15   Discover Bank                   2.65  0         1.440286      
16   Discover Bank                   2.75  0         1.000000      
17   Discover Bank                   2.80  0         1.000000      
18   Discover Bank                   3.00  0         1.319432      
19   Discover Bank                   0.65  0         2.000000      
20   Discover Bank                   2.65  0         6.569944      
21   Discover Bank                   2.75  0         6.000000      
22   Discover Bank                   2.80  0         1.000000      
23   Discover Bank                   2.65  0         11.527698     
24   Discover Bank                   2.70  0         3.000000      
25   Discover Bank                   2.80  0         1.000000      
26   Discover Bank                   2.65  0         56.000000     
27   Discover Bank                   2.65  0         9.000000      
28   American Express National Bank  2.10  0         3.307357      
29   American Express National Bank  2.10  0         1.659992      
30   American Express National Bank  2.10  0         37.910391     
31   American Express National Bank  2.10  0         7.410724      
32   American Express National Bank  2.10  0         33.005749     
33   American Express National Bank  2.10  0         8.751286      
34   American Express National Bank  2.10  0         1.000000      
35   American Express National Bank  2.10  0         6.891563      
36   American Express National Bank  2.10  0         25.153428     
37   American Express National Bank  2.10  0         7.545130      
38   American Express National Bank  2.10  0         1.000000      
39   American Express National Bank  2.10  0         2.549929      
40   American Express National Bank  2.10  0         12.375481     
41   American Express National Bank  2.10  0         10.193964     
42   American Express National Bank  2.10  0         54.073638     
43   American Express National Bank  2.10  0         4.659475      
44   American Express National Bank  2.10  0         1.000000      
45   American Express National Bank  2.10  0         53.495429     
46   American Express National Bank  2.10  0         4.813953      
47   American Express National Bank  2.10  0         36.864611     
48   American Express National Bank  2.10  0         1.368015      
49   American Express National Bank  2.10  0         22.724500     
50   Barclays                        2.20  0         4.005286      
51   Barclays                        2.20  0         3.557643      
52   Barclays                        2.20  0         18.189110     
53   Barclays                        2.20  0         66.206500     
54   Barclays                        2.20  0         2.745968      
55   Barclays                        2.20  0         50.043857     
56   Barclays                        2.20  0         9.831875      
57   Barclays                        2.20  0         6.042515      
58   Barc

In [648]:
#Remove Priority and Deduplicates
sot_grid.drop(columns=['Priority','Paused','Status'],inplace=True)
sot_grid.drop_duplicates(inplace=True)

In [649]:
#Change to easily understandable name
sot_grid.rename(columns = {'Product':'budget_product'},inplace=True)

# make the order and assign rank
sot_grid.sort_values(by=['zonegroup','ZoneName','AdvertiserName','ClickPerDay','Term'],ascending=[True,True,True,False,True], inplace=True)
sot_grid.reset_index(drop = True, inplace = True)
sot_grid['sorted_idx']=sot_grid.index

In [650]:
#Adding Rank to the table by Advertiser, product, 7 days, CPD
sot_grid['zone_ad_rank']=sot_grid.groupby(['ZoneName','AdvertiserName'])['sorted_idx'].rank(method='dense',ascending=True)


In [651]:
# Zone2: calling out zone 2 and capping at 6
result_mpa = sot_grid.loc[(sot_grid.ZoneName == 'Bank Pages Sponsored - Most Popular Accounts')&(sot_grid.zone_ad_rank<=6)]\
[['ZoneName','ZoneID','zonegroup','AdvertiserName','ProductName','ProductDetail','budget_product','ClickPerDay','sorted_idx','Apy']]

# Zone2: Bank Pages Sponsored - Open An Account; capped at 1
result_ao = sot_grid.loc[(sot_grid.ZoneName == 'Bank Pages Sponsored - Open An Account')&(sot_grid.zone_ad_rank<=1)]\
[['ZoneName','ZoneID','zonegroup','AdvertiserName','ProductName','ProductDetail','budget_product','ClickPerDay','sorted_idx','Apy']]

# Zone 1: MagnifyMoney Placement excep sidebar: Use yesterday placement
result_mm = sot_grid.loc[(sot_grid.ZoneName.str.contains('MagnifyMoney'))
                         &(sot_grid.ZoneName!='MagnifyMoney - Featured Accounts Sidebar')
                         &(sot_grid.ClickPerDay_yesterday>0.0)]\
[['ZoneName','ZoneID','zonegroup','AdvertiserName','ProductName','ProductDetail','budget_product','ClickPerDay','sorted_idx','Apy']]

# Zone 3: Display placements **** will need to make it based on source of truth in the future; doesn't matter because we dont' determine that
result_dp = sot_grid.loc[(sot_grid.ZoneName.str.contains('Display'))]\
[['ZoneName','ZoneID','zonegroup','AdvertiserName','ProductName','ProductDetail','budget_product','ClickPerDay','sorted_idx','Apy']]

In [652]:
clicks_mm = pd.DataFrame(result_mm.groupby(by=['AdvertiserName','budget_product']).ClickPerDay.sum().reset_index())
clicks_mpa = pd.DataFrame(result_mpa.groupby(by=['AdvertiserName','budget_product']).ClickPerDay.sum().reset_index())
clicks_ao = pd.DataFrame(result_ao.groupby(by=['AdvertiserName','budget_product']).ClickPerDay.sum().reset_index())
clicks_dp = pd.DataFrame(result_dp.groupby(by=['AdvertiserName','budget_product']).ClickPerDay.sum().reset_index())

In [653]:
# get clicks into advertiser table for subtraction
Advertiser_running = pd.merge(Advertiser,clicks_mm,'left',left_on=['AdvertiserName','Product'], right_on=['AdvertiserName','budget_product'])
Advertiser_running.rename(columns = {'ClickPerDay':'ClickPerDay_mm'},inplace=True)
Advertiser_running.drop(columns=['budget_product'], inplace=True)
Advertiser_running.fillna({'ClickPerDay_mm':0},inplace=True)

In [654]:
Advertiser_running = pd.merge(Advertiser_running,clicks_mpa,'left',left_on=['AdvertiserName','Product'], right_on=['AdvertiserName','budget_product'])
Advertiser_running.rename(columns = {'ClickPerDay':'ClickPerDay_mpa'},inplace=True)
Advertiser_running.drop(columns=['budget_product'], inplace=True)
Advertiser_running.fillna({'ClickPerDay_mpa':0},inplace=True)

In [655]:
Advertiser_running = pd.merge(Advertiser_running,clicks_ao,'left',left_on=['AdvertiserName','Product'], right_on=['AdvertiserName','budget_product'])
Advertiser_running.rename(columns = {'ClickPerDay':'ClickPerDay_ao'},inplace=True)
Advertiser_running.drop(columns=['budget_product'], inplace=True)
Advertiser_running.fillna({'ClickPerDay_ao':0},inplace=True)

In [656]:
Advertiser_running = pd.merge(Advertiser_running,clicks_dp,'left',left_on=['AdvertiserName','Product'], right_on=['AdvertiserName','budget_product'])
Advertiser_running.rename(columns = {'ClickPerDay':'ClickPerDay_dp'},inplace=True)
Advertiser_running.drop(columns=['budget_product'], inplace=True)
Advertiser_running.fillna({'ClickPerDay_dp':0},inplace=True)

In [657]:
# Subtracting the expected clicks from zone 1-3
Advertiser_running['Running Budget_pre_d']=Advertiser_running['Running Budget']\
-Advertiser_running['ClickPerDay_mm']-Advertiser_running['ClickPerDay_mpa']\
-Advertiser_running['ClickPerDay_ao']-Advertiser_running['ClickPerDay_dp']

## Allocating Clicks to Zone 4

In [658]:
# what's left to be allocated
sot_grid_z4 = sot_grid.loc[(sot_grid.zonegroup == 'zone_4')]

In [659]:
#count the product type by zonename - actually may not needed, we just need the max by product details
zonename_product_ct = sot_grid_z4.groupby(by='ZoneName').nunique()[['ProductDetail']].reset_index()

In [660]:
# 1) or do the below by zone, advertiser, product term lowest, APY highest
#sot_grid_z4.sort_values(by=['ZoneName','AdvertiserName','ProductDetail','Term','Apy'],ascending=[True,True,True,True,False])

In [661]:
#2) Use the below to limit number of product in source of truth for open ended ones
# use the max Apy (use APY since ALly 11 mo has higher CPD so can't use it; beware that )
sot_grid_agg = sot_grid_z4.groupby(by=['ZoneName','AdvertiserName','ProductDetail','Term']).max()\
[['Apy']].reset_index()

In [662]:
sot_grid_clean = pd.merge(sot_grid_z4,sot_grid_agg,'inner',['ZoneName','AdvertiserName','ProductDetail','Term','Apy']).drop_duplicates()

In [663]:
# Spots to be allocated
zone_sort_z4 = zone_sort.loc[(zone_sort.zonegroup == 'zone_4')]

In [664]:
#Change to decide how to sort
zone_sort_z4.sort_values(by=['open_rate'], ascending=False,inplace=True)
zone_sort_z4.reset_index(drop=True,inplace=True)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [665]:
#Create a subset of table column for merging
Ad_ops = Advertiser_running[['Advertiser','Product','Running Budget','Running Budget_pre_d','Pacing to Optimal']]
#updating name
Ad_ops.rename(columns={'Running Budget_pre_d':'remain_budget','Advertiser':'AdvertiserName'},inplace=True)
#Remove if budget hit 0
#Ad_ops = Ad_ops[Ad_ops['remain_budget']>=0]

In [666]:
slab = 5
Ad_ops_slab_add_on =  Ad_ops[Ad_ops['remain_budget']<0].copy()
Ad_ops_slab =  Ad_ops[Ad_ops['remain_budget']>=0].copy()
#budget divide by slab
Ad_ops_slab[['slab_budget']] = Ad_ops_slab[['remain_budget']]/slab
# Define how many slabs left
Ad_ops_slab[['slab_running']] = Ad_ops_slab[['remain_budget']]

In [667]:
#For each placement:
#1) get existing budget from advertiser table (map from advertiser table)
#1.1) if no budget, no eligible for that placement - or the algorithm will figure it out??
#2) calculate who are placed in that placements
#3) subtract the expected CPD from running CPD (computer on advertiser table)
#4) if no budget, then no longer eligible for that placement

#if slab = 5
#1) total budget divide by 5
#2) total cpd available divide by 5
#3) placement % divide by 5
#4) some placement need to be cap at max 10

In [668]:
sot_loop = sot_grid_clean[['AdvertiserName','Apy','ProductDetail','ProductName','ZoneName','budget_product','ClickPerDay','zone_ad_rank']]

#### Put in rules to show only one product if they are same product type (e.g. no two CDs in one placements)

In [669]:
# sot_rank = sot_loop.loc[(sot_loop.ZoneName.str.contains('Main Rate Table'))
#             |(sot_loop.ZoneName.str.contains("1yr CD"))].groupby(by=['ZoneName','AdvertiserName','ProductDetail'])[['Apy']].rank(method='dense',ascending=False)

In [670]:
#ALready fixed from zone 4 adjustment above to keep the max Apy, what's left is just 5 year SEM placement for GS
# sot_rank2 = sot_loop.groupby(by=['ZoneName','AdvertiserName','ProductDetail'])[['Apy','ClickPerDay']].rank(method='dense',ascending=False)

In [671]:
# sot_rank2.rename(columns={'Apy':'new_rank','ClickPerDay':'new_rank2'},inplace=True)

In [672]:
# sot_rank.rename(columns={'Apy':'new_rank'},inplace=True)

In [673]:
# sot_loop = pd.merge(sot_loop, sot_rank2,how='left', left_index=True, right_index=True)

In [674]:
# sot_loop.fillna(1,inplace=True)
# sot_loop = sot_loop[sot_loop.new_rank == 1]

#### Pacing Index

In [675]:
Ad_ops_slab['Pacing to Optimal'].max()

3667.0

In [676]:
Ad_ops_slab['Pacing to Optimal'].min()

-312.33333333333303

In [677]:
Ad_ops_slab['pacing_indx'] = 1/np.exp(Ad_ops_slab['Pacing to Optimal']/(Ad_ops_slab['Pacing to Optimal'].max()\
                                                                      -Ad_ops_slab['Pacing to Optimal'].min()))

In [678]:
# sot_loop = sot_loop.merge(Ad_ops_slab[['AdvertiserName','Product','pacing_indx']],'left',\
#                left_on=['AdvertiserName','budget_product'], right_on = ['AdvertiserName','Product'])

In [679]:
# sot_loop.drop('Product',axis=1,inplace=True)

#### Continue to work on algo

In [680]:
#CPD divide by slab
sot_loop_slab = sot_loop.copy()
sot_loop_slab[['slab_cpd']] = sot_loop_slab[['ClickPerDay']]/slab

In [681]:
# ## Adding cpd column
# google_feed = pd.merge(sot_loop_slab.loc[(sot_loop_slab['ZoneName']=='Main Rate Table (1yr CD)')]\
#          ,Ad_ops_slab[Ad_ops_slab['slab_budget']>=0],'left',left_on = ['AdvertiserName','budget_product'],right_on=['AdvertiserName','Product'])

In [682]:
#drop lines that don't have budget line matched
# google_feed.dropna(subset=['remain_budget'], inplace=True)
# google_feed['spent_ratio'] = 1-np.divide(google_feed['slab_running'],google_feed['Running Budget'])
# # The Trade off Function: 1-np.exp(google_feed.budget_ratio-1)
# google_feed['algo_idx'] = np.multiply(google_feed['slab_cpd'],1-np.exp(google_feed.spent_ratio-1))
# google_feed.sort_values(by=['algo_idx'],ascending=False,inplace=True)
# google_feed.reset_index(drop=True,inplace=True)

In [683]:
# Version 1: apply trade off function, no optimization to split %
# Version 2: apply trade off function, use optimization to split %
# Version 3: use slab, apply trade off function, no optimization to split %

In [684]:
# # Version 2: include splits right away
# zone_sort_z4.loc[zone_sort_z4.ZoneName\
#                                 =='Main Rate Table (1yr CD)']

In [685]:
# # ready for optimization
# total_pm_pct = min(zone_sort_z4.loc[zone_sort_z4.ZoneName\
#                             =='Main Rate Table (1yr CD)']['SpotAvailable'].loc[1],google_feed.shape[0])
# if total_pm_pct <= 2:
#     max_entry = min(total_pm_pct,google_feed.shape[0])
# else:
#     max_entry = min(8,google_feed.shape[0])
# #cap # of entry to the max, and get the number for; also convert it to distribution that added up to # of spots
# total_idx = google_feed.algo_idx.head(max_entry)

# if sum(total_idx) < 0.0:
#     entries = total_idx/sum(total_idx)*total_pm_pct*(-1)
# else:
#     entries = total_idx/sum(total_idx)*total_pm_pct

In [686]:
# Optimization Begin
def objective(x):
    """
    Set up the aggregate function to be optimized. 
    """
    total_value = 0.0
    for i in range(max_entry):
        total_value += x[i]
    return total_value

def constraint(x):
    """
    All value adds to total percentage for each placement
    """
    max_value = total_pm_pct
    for i in range(max_entry):
        max_value -= x[i]
    return max_value

#define boundary
b = (0,1)
#defined constraint type
con = {'type':'eq','fun':constraint}

def boundlist(x):
    """
    return boundary depending on # of entries
    """
    bound = []
    for i in range(max_entry):
        bound.append(b)
    return bound

In [687]:
def optimization_rounding(solution, solution_rd,total_pct, max_entry):
    """
    Adjustments to arrive at total percentage
    """
    nlist=[]
    if max_entry <= total_pct:
        for i,row in enumerate(solution):
            nlist.append({"index":i,"value":row,"rd_value":solution_rd[i]})
        new_pd = pd.DataFrame(nlist)
        print('test0')
    elif solution_rd.sum() - total_pct > 0.001:
        for i,row in enumerate(solution):
            nlist.append({"index":i,"value":row,"rd_value":solution_rd[i]})
        new_pd = pd.DataFrame(nlist)
        # index of the min
        min_idx = new_pd.loc[new_pd['rd_value']>0.0]['value'].idxmin()
        # subtract the excess from the minimum
        new_pd.loc[min_idx,'rd_value'] = new_pd.loc[min_idx]['rd_value'] - (solution_rd.sum() - total_pct)
        print('test1')
    elif solution_rd.sum() - total_pct < -0.001:
        for i,row in enumerate(solution):
            nlist.append({"index":i,"value":row,"rd_value":solution_rd[i]})
        new_pd = pd.DataFrame(nlist)
        # index of the min
        min_idx = new_pd.loc[new_pd['rd_value']>0.0]['value'].idxmin()
        # add the difference back to the minimum one
        new_pd.loc[min_idx,'rd_value'] += (total_pct - solution_rd.sum())
        print('test2')
    else:
        for i,row in enumerate(solution):
            nlist.append({"index":i,"value":row,"rd_value":solution_rd[i]})
        new_pd = pd.DataFrame(nlist)
        print('test3')
    return new_pd

In [688]:
# replace value in cell for reference
#new_pd.loc[9,'rd_value'] = .1

In [689]:
# sol_mix
# split_pct = optimization_rounding(sol_mix_base,sol_mix,total_pm_pct,max_entry)
# split_pct.rd_value.sum()
# split_pct

In [690]:
# output_pm = pd.merge(google_feed, split_pct[['rd_value']],'inner',left_index=True, right_index=True)
# output_pm['prorated_clicks']=output_pm.rd_value*output_pm.slab_cpd
# output_pm.groupby(by=['AdvertiserName','Product'],as_index=False)\
#             ['AdvertiserName','Product','prorated_clicks'].sum()
# # can append to a table
# output_pm

In [691]:
# Ad_ops_slab = pd.merge(Ad_ops_slab, \
#                 output_pm[['AdvertiserName','Product','prorated_clicks']],\
#                'left',on=['AdvertiserName','Product'])
# Ad_ops_slab['prorated_clicks'] = Ad_ops_slab[['prorated_clicks']].fillna(value=0)
# Ad_ops_slab['slab_budget'] -= Ad_ops_slab['prorated_clicks']
# Ad_ops_slab['slab_running'] -= Ad_ops_slab['prorated_clicks']
# # Then need to remove the last two columns
# Ad_ops_slab.drop(['prorated_clicks'],axis=1,inplace=True)
# # Then add to the output_pm 
# #*************************** use append or concat
# # Remove negatives from Ad_ops
# # just merge on the positive rows and the right table
# # Ad_ops[Ad_ops['Running Budget_pre_d']>=0]

In [692]:
# 'Bank'
# 'Budget Product': Ad_ops['running budget']
# 'ZoneName':output_pm.ZoneName
# 'ZoneType':output_pm['ZoneType']
# 'ProductLookUp':output_pm.ProductDetails
# 'ProductUsed':output_pm.ProductName
# 'SpotAvailable':no needed
# 'ExpectedCPD':output_pm.final_clicks
# 'BankBudget':Ad_ops['Running Budget_pre_d']
# 'CumulatedClicks':running budget - running budget pre_d
# 'ClickPerDayNeeded': Advertiser_running['Clicks needed per day']
# 'ModifiedClickPerDayNeeded': Ad_ops['Running Budget']
# 'Slot Ratio':output_pm.spent_ratio
# 'Site_link':"http://core.depositaccounts.com/ads/zone.aspx?id="+str(zone_sort_z4['ZoneID'])

In [693]:
############## need to append output table

In [694]:
# manual overwrite
# just overwrite to the output and adjust the remaining spot and the advertiser product from SOT
manual_ow = placement_input.loc[placement_input.Active == 'Y'][['Placement','Bank','Product','ProductType','Split']]
# Update the column names to match the others
manual_ow.rename(columns={'Placement':'ZoneName','Bank':'AdvertiserName',\
                          'Product':'ProductName','ProductType':'ProductDetail'},inplace=True)
# identify rows from SOT that need to be removed, obtain the index value in array form
sot_ow = sot_loop_slab.reset_index().merge(manual_ow[['ZoneName','AdvertiserName','ProductName','Split']]\
                                  ,'inner',on=['ZoneName','AdvertiserName','ProductName']).set_index('index')

sot_ow_idx = sot_ow.index.values

# remove the rows from SOT
sot_loop_slab = sot_loop_slab.loc[~sot_loop_slab.index.isin(sot_ow_idx)]

# Create total split by zone from manual overwrite
manual_ow_split = manual_ow.groupby(by='ZoneName').sum().reset_index()[['ZoneName','Split']]

# Merge into Zone table 
zone_sort_z4 = zone_sort_z4.merge(manual_ow_split, 'left', on = 'ZoneName')
zone_sort_z4.fillna(0, inplace = True)

# Calculate new spot available for algo
zone_sort_z4['SpotAvailable'] = zone_sort_z4['SpotAvailable']-zone_sort_z4['Split']

# Adjust the Advertiser table
# need to compute the adjusted clicks from manual overwrite
sot_ow['Click_ow'] = sot_ow['ClickPerDay'] * sot_ow['Split']

#aggregate by advertiser to subtract from advertiser table
ad_ow = sot_ow.groupby(by=['AdvertiserName','budget_product']).sum().reset_index()\
[['AdvertiserName','budget_product','Click_ow']]

# rename column to match ad table
ad_ow.rename(columns={'budget_product':'Product'},inplace=True)

# Final merge and calc
Ad_ops_slab = Ad_ops_slab.merge(ad_ow, 'left', on=['AdvertiserName','Product'])
Ad_ops_slab.fillna(0, inplace=True)
Ad_ops_slab['slab_budget'] = Ad_ops_slab['slab_budget'] - Ad_ops_slab['Click_ow']
Ad_ops_slab['slab_running'] = Ad_ops_slab['slab_running'] - Ad_ops_slab['Click_ow']

Ad_ops_slab.drop(columns='Click_ow', inplace=True)
zone_sort_z4.drop(columns='Split', inplace=True)

In [695]:
# create table format to add back to bigger table 
# pick column from sot table
agg_sot_ow = sot_ow[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','Click_ow','Split']]

# Pick columne from ad table
agg_ad_ow = Ad_ops.merge(ad_ow, 'inner', on=['AdvertiserName','Product'])
agg_ad_ow.rename(columns={'Product':'budget_product'},inplace=True)

# aggregate
agg_ow = agg_sot_ow.merge(agg_ad_ow[['AdvertiserName','budget_product','Running Budget','Pacing to Optimal']], 'inner',\
                on = ['AdvertiserName','budget_product'])

# back out the rd_value in agg table just to have such dummy column
agg_ow['rd_value']=agg_ow['Split']*slab
agg_ow.rename(columns={'Click_ow':'prorated_clicks','Split':'Total_split'},inplace=True)

In [696]:
ow_zone = agg_sot_ow.ZoneName.unique()

In [697]:
sot_loop_slab

AdvertiserName   Apy ProductDetail  \
0    Discover Bank                   2.70  CDs            
1    Discover Bank                   2.75  CDs            
2    Discover Bank                   2.80  CDs            
3    UFB Direct                      2.45  MMA            
4    Ally Bank                       2.20  Savings        
5    American Express National Bank  2.10  Savings        
6    Barclays                        2.20  Savings        
7    Capital One                     2.00  MMA            
8    Goldman Sachs Bank USA          2.25  Savings        
9    Goldman Sachs Bank USA          2.70  CDs            
10   Discover Bank                   2.65  CDs            
11   Capital One                     2.70  CDs            
12   Discover Bank                   2.65  CDs            
13   Goldman Sachs Bank USA          2.70  CDs            
14   Capital One                     2.80  CDs            
15   Discover Bank                   2.75  CDs            
16   Discover Bank                   2.80  CDs            
17   Discover Bank                   3.00  CDs            
18   Goldman Sachs Bank USA          3.00  CDs            
19   nbkc bank                       1.01  Checking       
20   Ally Bank                       2.20  Savings        
21   American Express National Bank  2.10  Savings        
22   Barclays                        2.20  Savings        
23   Goldman Sachs Bank USA          2.25  Savings        
24   Ally Bank                       2.20  Savings        
25   American Express National Bank  2.10  Savings        
26   Barclays                        2.20  Savings        
27   Goldman Sachs Bank USA          2.25  Savings        
28   Capital One                     2.70  CDs            
29   Goldman Sachs Bank USA          2.70  CDs            
30   American Express National Bank  2.10  Savings        
31   Barclays                        2.20  Savings        
32   Goldman Sachs Bank USA          2.25  Savings        
33   Discover Bank                   2.10  Savings        
34   Ally Bank                       2.20  Savings        
35   American Express National Bank  2.10  Savings        
36   Barclays                        2.20  Savings        
37   Ally Bank                       2.20  Savings        
38   American Express National Bank  2.10  Savings        
39   Barclays                        2.20  Savings        
40   Filler - FNBO DIrect            2.25  Savings        
41   Filler - Radius Bank            2.05  Savings        
42   American Express National Bank  2.10  Savings        
43   Barclays                        2.20  Savings        
44   Goldman Sachs Bank USA          2.25  Savings        
45   Capital One                     2.70  CDs            
46   Goldman Sachs Bank USA          2.70  CDs            
47   Capital One                     2.80  CDs            
48   Goldman Sachs Bank USA          3.00  CDs            
49   Ally Bank                       2.20  Savings        
50   American Express National Bank  2.10  Savings        
51   Barclays                        2.20  Savings        
52   Capital One                     2.00  MMA            
53   Citizens Access                 2.35  Savings        
54   Discover Bank                   2.10  Savings        
55   Goldman Sachs Bank USA          2.25  Savings        
56   HSBC Direct                     2.25  Savings        
57   UFB Direct                      2.45  Savings        
58   Capital One                     2.70  CDs            
59   Capital One                     2.80  CDs            
60   Goldman Sachs Bank USA          2.70  CDs            
61   Goldman Sachs Bank USA          3.00  CDs            
62   Ally Bank                       2.20  Savings        
63   American Express National Bank  2.10  Savings        
64   Barclays                        2.20  Savings        
65   Capital One                     2.00  MMA            
66   Goldman Sachs Bank USA          2.25  Savings        
67   HSBC

In [698]:
manual_ow

ZoneName               AdvertiserName  \
4   Sidebar - Featured Accounts               Capital One                   
5   Main Rate Table (Savings)                 North American Savings Bank   
6   Sidebar - Featured Rates (CD 1yr)         Capital One                   
9   MagnifyMoney - Featured Accounts Sidebar  Capital One                   
11  Main Rate Table (IRA 18m)                 Discover Bank                 
12  Main Rate Table (IRA 1yr)                 Discover Bank                 
13  Main Rate Table (IRA 2yr)                 Discover Bank                 
14  Main Rate Table (IRA 3m)                  Discover Bank                 
15  Main Rate Table (IRA 3yr)                 Discover Bank                 
16  Main Rate Table (IRA 4yr)                 Discover Bank                 
17  Main Rate Table (IRA 5yr)                 Discover Bank                 
18  Main Rate Table (IRA 6mo)                 Discover Bank                 
25  Main Rate Table (1yr CD)                  Capital One                   
28  LP - SEM (2yr CD)                         Capital One                   
32  Main Rate Table (1yr CD)                  Goldman Sachs Bank USA        
34  Main Rate Table (2yr CD)                  Capital One                   
46  LP - SEM (1yr CD)                         Goldman Sachs Bank USA        
47  MagnifyMoney - Featured Accounts Sidebar  Aspiration                    
48  Sidebar - Featured Accounts               Aspiration                    
49  Main Rate Table (Checking Regular)        Aspiration                    
50  MagnifyMoney - Featured Accounts Sidebar  HSBC Direct                   

               ProductName ProductDetail  Split  
4   12 Month 360 CD         CDs           0.0    
5   High Rate Savings       Savings       0.0    
6   12 Month 360 CD         CDs           0.0    
9   12 Month 360 CD         CDs           0.0    
11  18 Month IRA            Both          1.0    
12  12 Month IRA            Both          1.0    
13  24 Month IRA            Both          1.0    
14  3 Month IRA             Both          1.0    
15  3 Year IRA              Both          1.0    
16  4 Year IRA              Both          1.0    
17  5 Year IRA              Both          1.0    
18  6 Month IRA             Both          1.0    
25  12 Month 360 CD         CDs           0.0    
28  24 Month 360 CD         CDs           0.0    
32  High-yield 12 Month CD  CDs           0.5    
34  24 Month 360 CD         CDs           1.0    
46  High Yield 12-Month CD  CDs           0.5    
47  Spend and Save Account  Checking      1.0    
48  Spend and Save Account  Checking      1.0    
49  Spend and Save Account  Checking      1.0    
50  HSBC Direct Savings     Savings       1.0

In [699]:
agg_ow

AdvertiserName   Apy budget_product             ProductName  \
0   Capital One             2.80  CDs            24 Month 360 CD          
1   Capital One             2.70  CDs            12 Month 360 CD          
2   Capital One             2.70  CDs            12 Month 360 CD          
3   Capital One             2.80  CDs            24 Month 360 CD          
4   Capital One             2.70  CDs            12 Month 360 CD          
5   Capital One             2.70  CDs            12 Month 360 CD          
6   Aspiration              2.00  Checking       Spend and Save Account   
7   Aspiration              2.00  Checking       Spend and Save Account   
8   Aspiration              2.00  Checking       Spend and Save Account   
9   HSBC Direct             2.25  Savings        HSBC Direct Savings      
10  Goldman Sachs Bank USA  2.70  Both           High-yield 12 Month CD   
11  Discover Bank           2.65  Both           18 Month IRA             
12  Discover Bank           2.65  Both           12 Month IRA             
13  Discover Bank           2.70  Both           24 Month IRA             
14  Discover Bank           2.75  Both           3 Year IRA               
15  Discover Bank           2.80  Both           4 Year IRA               
16  Discover Bank           3.00  Both           5 Year IRA               
17  Discover Bank           0.65  Both           6 Month IRA              

                                    ZoneName  prorated_clicks  Total_split  \
0   LP - SEM (2yr CD)                         0.000000         0.0           
1   MagnifyMoney - Featured Accounts Sidebar  0.000000         0.0           
2   Main Rate Table (1yr CD)                  0.000000         0.0           
3   Main Rate Table (2yr CD)                  2.932097         1.0           
4   Sidebar - Featured Accounts               0.000000         0.0           
5   Sidebar - Featured Rates (CD 1yr)         0.000000         0.0           
6   MagnifyMoney - Featured Accounts Sidebar  10.978676        1.0           
7   Main Rate Table (Checking Regular)        6.912709         1.0           
8   Sidebar - Featured Accounts               26.413731        1.0           
9   MagnifyMoney - Featured Accounts Sidebar  76.450121        1.0           
10  Main Rate Table (1yr CD)                  2.665150         0.5           
11  Main Rate Table (IRA 18m)                 2.288254         1.0           
12  Main Rate Table (IRA 1yr)                 13.401056        1.0           
13  Main Rate Table (IRA 2yr)                 1.518000         1.0           
14  Main Rate Table (IRA 3yr)                 1.300417         1.0           
15  Main Rate Table (IRA 4yr)                 1.000000         1.0           
16  Main Rate Table (IRA 5yr)                 1.313019         1.0           
17  Main Rate Table (IRA 6mo)                 1.000000         1.0           

    Running Budget  Pacing to Optimal  rd_value  
0   34.129818       2323.333333        0.0       
1   34.129818       2323.333333        0.0       
2   34.129818       2323.333333        0.0       
3   34.129818       2323.333333        5.0       
4   34.129818       2323.333333        0.0       
5   34.129818       2323.333333        0.0       
6   12.186561      -66.388889          5.0       
7   12.186561      -66.388889          5.0       
8   12.186561      -66.388889          5.0       
9   229.742270      314.333333         5.0       
10  708.643380      3667.000000        2.5       
11  0.000000        38.000000          5.0       
12  0.000000        38.000000          5.0       
13  0.000000        38.000000          5.0       
14  0.000000        38.000000          5.0       
15  0.000000        38.000000          5.0       
16  0.000000        38.000000          5.0       
17  0.000000        38.000000          5.0

In [700]:
def rank_ow(x):
    if x == 'Sidebar - Featured Rates (Savings)' or x =='Sidebar - Featured Accounts' or x =='Sidebar - Featured Rates (CD 1yr)':
        return 2
    else:
        return 1

In [701]:
zone_sort_z4['org_inx'] = zone_sort_z4.index

In [702]:
zone_sort_z4['new_rank']=zone_sort_z4.ZoneName.apply(rank_ow)


In [703]:
Ad_ops_slab

AdvertiserName   Product  Running Budget  remain_budget  \
0   American Express National Bank  Savings   345.258576      259.257345      
1   American Express National Bank  CDs       0.000000        0.000000        
2   North American Savings Bank     Savings   0.000000        0.000000        
3   Goldman Sachs Bank USA          Both      708.643380      259.406701      
4   Capital One                     MMA       276.809020      269.822578      
5   HSBC Direct                     Savings   229.742270      174.807743      
6   Barclays                        Savings   141.730910      67.961482       
7   nbkc bank                       Checking  51.675113       36.517335       
8   UFB Direct                      Savings   26.974286       21.885583       
9   First Internet Bank             Business  23.840599       7.171650        
10  Barclays                        CDs       15.869527       15.869527       
11  Live Oak Bank                   Business  10.261289       2.311719        
12  nbkc bank                       Business  6.267374        4.396124        
13  Synchrony Bank                  Both      0.000000        0.000000        
14  Ally Bank                       CDs       0.000000        0.000000        
15  Capital One                     Business  0.000000        0.000000        
16  CIT Bank                        Savings   0.000000        0.000000        
17  Vio Bank                        CDs       0.000000        0.000000        
18  Axos Bank                       Checking  0.000000        0.000000        
19  Axos Bank                       Business  0.000000        0.000000        
20  Citizens Access                 Both      0.000000        0.000000        
21  PurePoint Financial             Savings   0.000000        0.000000        
22  First Internet Bank             MMA       0.000000        0.000000        
23  earn.bank                       MMA       0.000000        0.000000        
24  Citi                            Savings   0.000000        0.000000        

    Pacing to Optimal  slab_budget  slab_running  pacing_indx  
0   207.666667         51.851469    259.257345    0.949152     
1   0.000000           0.000000     0.000000      1.000000     
2   0.000000           0.000000     0.000000      1.000000     
3   3667.000000        49.216190    256.741551    0.397917     
4  -312.333333         53.964516    269.822578    1.081651     
5   314.333333        -41.488572    98.357623     0.924048     
6   2167.000000        13.592296    67.961482     0.580095     
7  -81.000000          7.303467     36.517335     1.020564     
8  -59.000000          4.377117     21.885583     1.014937     
9  -134.666667         1.434330     7.171650      1.034421     
10  1659.000000        3.173905     15.869527     0.659084     
11 -15.000000          0.462344     2.311719      1.003777     
12 -26.000000          0.879225     4.396124      1.006555     
13  0.000000           0.000000     0.000000      1.000000     
14  2670.000000        0.000000     0.000000      0.511214     
15  0.000000           0.000000     0.000000      1.000000     
16  0.000000           0.000000     0.000000      1.000000     
17  0.000000           0.000000     0.000000      1.000000     
18  0.000000           0.000000     0.000000      1.000000     
19  0.000000           0.000000     0.000000      1.000000     
20  0.000000           0.000000     0.000000      1.000000     
21  0.000000           0.000000     0.000000      1.000000     
22  12.000000          0.000000     0.000000      0.996989     
23  0.000000           0.000000     0.000000      1.000000     
24  0.000000           0.000000     0.000000      1.000000

In [704]:

#maximum entry (product, advertiser) allowed to enter placement optimization
max_to_opt = 8

for i in range(slab):
    print(20000+i)
    if i > 2:
        zone_sort_z4 = zone_sort_z4.sort_values(by=['new_rank','open_rate'], ascending=False).reset_index(drop=True)
    for z_index in range(zone_sort_z4.shape[0]):
        # resetting variables
        max_entry = 0
        entries = 0
        print(zone_sort_z4.iloc[z_index]['ZoneName'])
        # merge the clean table with Ad ops; use running slab running total in the first run
        if z_index == 0:
            Ad_ops_slab['slab_budget'] = Ad_ops_slab.slab_running/(slab-i)
            google_feed = pd.merge(sot_loop_slab.loc[(sot_loop_slab['ZoneName'] == \
                                                 zone_sort_z4.iloc[z_index]['ZoneName'])]\
                                   ,Ad_ops_slab[Ad_ops_slab['slab_running']>0], 'left',\
                                   left_on = ['AdvertiserName','budget_product'],\
                                   right_on=['AdvertiserName','Product'])
            #google_feed['slab_budget'] = google_feed.remain_budget/slab
            
        else:
            ## need to be > instead of >=; otherwise optimization will have error
            google_feed = pd.merge(sot_loop_slab.loc[(sot_loop_slab['ZoneName'] == \
                                                     zone_sort_z4.iloc[z_index]['ZoneName'])]\
                                       ,Ad_ops_slab[Ad_ops_slab['slab_budget']>0], 'left',\
                                       left_on = ['AdvertiserName','budget_product'],\
                                       right_on=['AdvertiserName','Product'])
        #drop lines that don't have budget line matched
        google_feed.dropna(subset=['remain_budget'], inplace=True)
        #get how much we get spent until this point
        google_feed['spent_ratio'] = 1-np.divide(google_feed['slab_running'],google_feed['Running Budget'])
        # The Trade off Function: 1-np.exp(google_feed.budget_ratio-1)
        # testing mutiply to pacing index impact on Simple and other advertisers
        google_feed['algo_idx'] = np.multiply(google_feed['slab_cpd'],1-np.exp(google_feed.spent_ratio-1))
        ## trying to use pacing ^2
        google_feed['algo_idx'] = np.multiply(google_feed['algo_idx'],np.exp(google_feed.pacing_indx))
        # Arranging algo idx for optimization
        google_feed.sort_values(by=['algo_idx'],ascending=False,inplace=True)
        google_feed.reset_index(drop=True,inplace=True)
        print(google_feed)
        #If no rows returns, go to the next placements - loop stopped because minimize function shows error
        if google_feed.empty:
            print (1111)
            del google_feed
            continue
        # if min is 0, no more to fill, then skip
        elif min(zone_sort_z4.loc[zone_sort_z4.ZoneName\
                                ==zone_sort_z4.iloc[z_index]['ZoneName']]['SpotAvailable'].loc[z_index],google_feed.shape[0]) == 0.0:
            pass
        else:
            # ready for optimization
            total_pm_pct = min(zone_sort_z4.loc[zone_sort_z4.ZoneName\
                                        ==zone_sort_z4.iloc[z_index]['ZoneName']]['SpotAvailable'].loc[z_index],google_feed.shape[0])
            # use ceiling to convert to int and preserve the number of steps in the optimization function
            if total_pm_pct <= 2:
                max_entry = math.ceil(min(total_pm_pct,google_feed.shape[0]))
            else:
                #max_entry = min(max_to_opt,google_feed.shape[0])
                max_entry = math.ceil(min(total_pm_pct,google_feed.shape[0]))
            #cap # of entry to the max, and get the number for; also convert it to distribution that added up to # of spots
            total_idx = google_feed.algo_idx.head(max_entry) # make it an integer
            # take care of infinite
            total_idx_mean = total_idx.copy()
            total_idx_mean_rest = np.mean(total_idx_mean.loc[np.isfinite(total_idx_mean)])
            total_idx = total_idx_mean.replace([np.inf, -np.inf], total_idx_mean_rest)

            if sum(total_idx) < 0.0:
                entries = total_idx/sum(total_idx)*total_pm_pct*(-1)
            else:
                entries = total_idx/sum(total_idx)*total_pm_pct
            print(total_pm_pct, max_entry,total_idx,entries)
            #print(google_feed.info(memory_usage='deep'))

            #Optimization begin - Core Algorithm
            sol = minimize(objective, entries, \
                           method = 'SLSQP', bounds = boundlist(max_entry), \
                           constraints=con)
            #output array - not rounded
            sol_mix_base = sol['x']
            #rounding to the nearest 0.5
            sol_mix = np.divide((sol_mix_base*2).round(1),2)
            #Calculate the exact splits
            split_pct = optimization_rounding(sol_mix_base,sol_mix,total_pm_pct, max_entry)
            # getting the output split back to the google feed
            output_pm = pd.merge(google_feed, split_pct[['rd_value']],'inner',\
                                 left_index=True, right_index=True)
            # calculating the prorated clicks knowing the splits pct
            output_pm['prorated_clicks']=output_pm.rd_value*output_pm.slab_cpd
            output_merge = output_pm.groupby(by=['AdvertiserName','Product'],as_index=False)\
            ['AdvertiserName','Product','prorated_clicks'].sum()
            if i == 0 and z_index == 0:
                rotation_table = output_pm.copy()
            else:
                rotation_table = rotation_table.append(output_pm, ignore_index = True)

            #print('test2')

            #updating the Ad_ops for next iteration
            Ad_ops_slab = pd.merge(Ad_ops_slab, \
                    output_merge,\
                   'left',on=['AdvertiserName','Product'])
            print(Ad_ops_slab)
            # Filling NA with 0
            Ad_ops_slab['prorated_clicks'] = Ad_ops_slab[['prorated_clicks']].fillna(value=0)
            # update remaining budget
            Ad_ops_slab['slab_budget'] -= Ad_ops_slab['prorated_clicks']
            Ad_ops_slab['slab_running'] -= Ad_ops_slab['prorated_clicks']
            # Then need to remove the last two columns
            Ad_ops_slab.drop(['prorated_clicks'],axis=1,inplace=True)
            df_list = [google_feed, total_pm_pct, total_idx, output_pm]
            del df_list
    


20000
LP - SEM B (Sav)
                   AdvertiserName   Apy ProductDetail  \
0  Capital One                     2.00  MMA            
1  American Express National Bank  2.10  Savings        
2  Goldman Sachs Bank USA          2.25  Savings        

                         ProductName          ZoneName budget_product  \
0  360 Money Market                   LP - SEM B (Sav)  MMA             
1  High Yield Savings Account         LP - SEM B (Sav)  Savings         
2  High-yield Online Savings Account  LP - SEM B (Sav)  Both            

   ClickPerDay  zone_ad_rank  slab_cpd  Product  Running Budget  \
0  1.0          1.0           0.2       MMA      276.809020       
1  1.0          1.0           0.2       Savings  345.258576       
2  1.0          1.0           0.2       Both     708.643380       

   remain_budget  Pacing to Optimal  slab_budget  slab_running  pacing_indx  \
0  269.822578    -312.333333         53.964516    269.822578    1.081651      
1  259.257345     207.666667

                   AdvertiserName   Apy ProductDetail  \
0  Capital One                     2.00  MMA            
1  American Express National Bank  2.10  Savings        
2  Barclays                        2.20  Savings        
3  Goldman Sachs Bank USA          2.25  Savings        
4  HSBC Direct                     2.25  Savings        

                         ProductName                         ZoneName  \
0  360 Money Market                   LP - Native MSN Page (Savings)    
1  High Yield Savings Account         LP - Native MSN Page (Savings)    
2  Online Savings Account             LP - Native MSN Page (Savings)    
3  High-yield Online Savings Account  LP - Native MSN Page (Savings)    
4  HSBC Direct Savings                LP - Native MSN Page (Savings)    

  budget_product  ClickPerDay  zone_ad_rank  slab_cpd  Product  \
0  MMA            8.029096     1.0           1.605819  MMA       
1  Savings        4.659475     1.0           0.931895  Savings   
2  Savings        9.

1 1 0    0.642357
Name: algo_idx, dtype: float64 0    1.0
Name: algo_idx, dtype: float64
test0
                    AdvertiserName   Product  Running Budget  remain_budget  \
0   American Express National Bank  Savings   345.258576      259.257345      
1   American Express National Bank  CDs       0.000000        0.000000        
2   North American Savings Bank     Savings   0.000000        0.000000        
3   Goldman Sachs Bank USA          Both      708.643380      259.406701      
4   Capital One                     MMA       276.809020      269.822578      
5   HSBC Direct                     Savings   229.742270      174.807743      
6   Barclays                        Savings   141.730910      67.961482       
7   nbkc bank                       Checking  51.675113       36.517335       
8   UFB Direct                      Savings   26.974286       21.885583       
9   First Internet Bank             Business  23.840599       7.171650        
10  Barclays                        

Empty DataFrame
Columns: [AdvertiserName, Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
VP - Sidebar - Featured Checking Accounts
  AdvertiserName   Apy ProductDetail       ProductName  \
0  nbkc bank      1.01  Checking      Personal Account   

                                    ZoneName budget_product  ClickPerDay  \
0  VP - Sidebar - Featured Checking Accounts  Checking       1.0           

   zone_ad_rank  slab_cpd   Product  Running Budget  remain_budget  \
0  1.0           0.2       Checking  51.675113       36.517335       

   Pacing to Optimal  slab_budget  slab_running  pacing_indx  spent_ratio  \
0 -81.0               4.651312     33.86518      1.020564     0.344652      

   algo_idx  
0  0.266787  
1 1 0    0.266787
Name: algo_idx, dtype: float64 0    1.0
Name: algo_idx, dtype: float64


Empty DataFrame
Columns: [Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, AdvertiserName, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
Sidebar - Featured Rates (CD 1yr)
Empty DataFrame
Columns: [AdvertiserName, Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
Main Rate Table (Checking Regular)
  AdvertiserName   Apy ProductDetail       ProductName  \
0  nbkc bank      1.01  Checking      Personal Account   

                             ZoneName budget_product  ClickPerDay  \
0  Main Rate Table (Checking Regular)  Checking       1.77175       

   zone_ad_rank  slab_cpd   Product  Running Budget  remain_budget  \
0  1.0           0.35435   Checking  51.675113       36

...

24  0.000000           0.000000     0.000000      1.000000    NaN               
LP - Native (Sav)
                   AdvertiserName  Apy ProductDetail  \
0  Capital One                     2.0  MMA            
1  American Express National Bank  2.1  Savings        

                  ProductName           ZoneName budget_product  ClickPerDay  \
0  360 Money Market            LP - Native (Sav)  MMA            15.943574     
1  High Yield Savings Account  LP - Native (Sav)  Savings        33.005749     

   zone_ad_rank  slab_cpd  Product  Running Budget  remain_budget  \
0  1.0           3.188715  MMA      276.809020      269.822578      
1  1.0           6.601150  Savings  345.258576      259.257345      

   Pacing to Optimal  slab_budget  slab_running  pacing_indx  spent_ratio  \
0 -312.333333         105.080525   105.080525    1.081651     0.620386      
1  207.666667         30.944164    30.944164     0.949152     0.910374      

   algo_idx  
0  2.970882  
1  1.462004  
2 2 0    

                    AdvertiserName   Product  Running Budget  remain_budget  \
0   American Express National Bank  Savings   345.258576      259.257345      
1   American Express National Bank  CDs       0.000000        0.000000        
2   North American Savings Bank     Savings   0.000000        0.000000        
3   Goldman Sachs Bank USA          Both      708.643380      259.406701      
4   Capital One                     MMA       276.809020      269.822578      
5   HSBC Direct                     Savings   229.742270      174.807743      
6   Barclays                        Savings   141.730910      67.961482       
7   nbkc bank                       Checking  51.675113       36.517335       
8   UFB Direct                      Savings   26.974286       21.885583       
9   First Internet Bank             Business  23.840599       7.171650        
10  Barclays                        CDs       15.869527       15.869527       
11  Live Oak Bank                   Business  10.261

                    AdvertiserName   Product  Running Budget  remain_budget  \
0   American Express National Bank  Savings   345.258576      259.257345      
1   American Express National Bank  CDs       0.000000        0.000000        
2   North American Savings Bank     Savings   0.000000        0.000000        
3   Goldman Sachs Bank USA          Both      708.643380      259.406701      
4   Capital One                     MMA       276.809020      269.822578      
5   HSBC Direct                     Savings   229.742270      174.807743      
6   Barclays                        Savings   141.730910      67.961482       
7   nbkc bank                       Checking  51.675113       36.517335       
8   UFB Direct                      Savings   26.974286       21.885583       
9   First Internet Bank             Business  23.840599       7.171650        
10  Barclays                        CDs       15.869527       15.869527       
11  Live Oak Bank                   Business  10.261

24  0.000000           0.000000     0.000000      1.000000    NaN               
LP - Native (1yr CD)
Empty DataFrame
Columns: [AdvertiserName, Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
LP - Native (2yr CD)
Empty DataFrame
Columns: [AdvertiserName, Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
LP - Native (5yr CD)
Empty DataFrame
Columns: [AdvertiserName, Apy, ProductDetail, ProductName, ZoneName, budget_product, ClickPerDay, zone_ad_rank, slab_cpd, Product, Running Budget, remain_budget, Pacing to Optimal, slab_budget, slab_running, pacing_indx, spent_ratio, algo_idx]
Index: []
1111
MyLT - Recommended Alert
      

0  0.640139     0.232069  
1 1 0    0.232069
Name: algo_idx, dtype: float64 0    1.0
Name: algo_idx, dtype: float64
test0
                    AdvertiserName   Product  Running Budget  remain_budget  \
0   American Express National Bank  Savings   345.258576      259.257345      
1   American Express National Bank  CDs       0.000000        0.000000        
2   North American Savings Bank     Savings   0.000000        0.000000        
3   Goldman Sachs Bank USA          Both      708.643380      259.406701      
4   Capital One                     MMA       276.809020      269.822578      
5   HSBC Direct                     Savings   229.742270      174.807743      
6   Barclays                        Savings   141.730910      67.961482       
7   nbkc bank                       Checking  51.675113       36.517335       
8   UFB Direct                      Savings   26.974286       21.885583       
9   First Internet Bank             Business  23.840599       7.171650        
10  Barcl

In [705]:
## Resort it back to based on quality
zone_sort_z4 = zone_sort_z4.sort_values(by=['org_inx','open_rate'], ascending=False).reset_index(drop=True)

In [706]:

# #maximum entry (product, advertiser) allowed to enter placement optimization
# max_to_opt = 8

# i=1
# print(20000+i)
# #for z_index in range(zone_sort_z4.shape[0]):
# z_index = 4
#     # resetting variables
# max_entry = 0
# entries = 0
# print(zone_sort_z4.iloc[z_index]['ZoneName'])
# # merge the clean table with Ad ops; use running slab running total in the first run
# if z_index == 0:
#     Ad_ops_slab['slab_budget'] = Ad_ops_slab.slab_running/slab
#     google_feed = pd.merge(sot_loop_slab.loc[(sot_loop_slab['ZoneName'] == \
#                                          zone_sort_z4.iloc[z_index]['ZoneName'])]\
#                            ,Ad_ops_slab[Ad_ops_slab['slab_running']>0], 'left',\
#                            left_on = ['AdvertiserName','budget_product'],\
#                            right_on=['AdvertiserName','Product'])
#     google_feed['slab_budget'] = google_feed.remain_budget/slab

# else:
#     google_feed = pd.merge(sot_loop_slab.loc[(sot_loop_slab['ZoneName'] == \
#                                              zone_sort_z4.iloc[z_index]['ZoneName'])]\
#                                ,Ad_ops_slab[Ad_ops_slab['slab_budget']>0], 'left',\
#                                left_on = ['AdvertiserName','budget_product'],\
#                                right_on=['AdvertiserName','Product'])
# #drop lines that don't have budget line matched
# google_feed.dropna(subset=['remain_budget'], inplace=True)
# #drop line when spent ratio is NA
# #google_feed.dropna(subset=['spent_ratio'], inplace=True)
# #get how much we get spent until this point
# google_feed['spent_ratio'] = 1-np.divide(google_feed['slab_running'],google_feed['Running Budget'])
# # The Trade off Function: 1-np.exp(google_feed.budget_ratio-1)
# # testing mutiply to pacing index impact on Simple and other advertisers
# google_feed['algo_idx'] = np.multiply(google_feed['slab_cpd'],1-np.exp(google_feed.spent_ratio-1))
# ## trying to use pacing ^2
# google_feed['algo_idx'] = np.multiply(google_feed['algo_idx'],np.exp(google_feed.pacing_indx))
# # Arranging algo idx for optimization
# google_feed.sort_values(by=['algo_idx'],ascending=False,inplace=True)
# google_feed.reset_index(drop=True,inplace=True)
# print(google_feed)
# #If no rows returns, go to the next placements - loop stopped because minimize function shows error
# if google_feed.empty:
#     print (1111)
#     del google_feed
#     pass
# # if min is 0, no more to fill, then skip
# elif min(zone_sort_z4.loc[zone_sort_z4.ZoneName\
#                                 ==zone_sort_z4.iloc[z_index]['ZoneName']]['SpotAvailable'].loc[z_index],google_feed.shape[0]) == 0.0:
#         pass

# else:
#     # ready for optimization
#     total_pm_pct = min(zone_sort_z4.loc[zone_sort_z4.ZoneName\
#                                 ==zone_sort_z4.iloc[z_index]['ZoneName']]['SpotAvailable'].loc[z_index],google_feed.shape[0])


#     # use ceiling to convert to int and preserve the number of steps in the optimization function
#     if total_pm_pct <= 2:
#         max_entry = math.ceil(min(total_pm_pct,google_feed.shape[0]))
#     else:
#         #max_entry = min(max_to_opt,google_feed.shape[0])
#         max_entry = math.ceil(min(total_pm_pct,google_feed.shape[0]))
#     #cap # of entry to the max, and get the number for; also convert it to distribution that added up to # of spots
#     total_idx = google_feed.algo_idx.head(max_entry) # make it an integer
#     # take care of infinite
#     total_idx_mean = total_idx.copy()
#     total_idx_mean_rest = np.mean(total_idx_mean.loc[np.isfinite(total_idx_mean)])
#     total_idx = total_idx_mean.replace([np.inf, -np.inf], total_idx_mean_rest)


#     if sum(total_idx) < 0.0:
#         entries = total_idx/sum(total_idx)*total_pm_pct*(-1)
#     else:
#         entries = total_idx/sum(total_idx)*total_pm_pct
#     print(total_pm_pct, max_entry,total_idx,entries)
#     #print(google_feed.info(memory_usage='deep'))

#     #Optimization begin - Core Algorithm
#     sol = minimize(objective, entries, \
#                    method = 'SLSQP', bounds = boundlist(max_entry), \
#                    constraints=con)
#     #output array - not rounded
#     sol_mix_base = sol['x']
#     #rounding to the nearest 0.5
#     sol_mix = np.divide((sol_mix_base*2).round(1),2)
#     #Calculate the exact splits
#     split_pct = optimization_rounding(sol_mix_base,sol_mix,total_pm_pct, max_entry)
#     # getting the output split back to the google feed
#     output_pm = pd.merge(google_feed, split_pct[['rd_value']],'inner',\
#                          left_index=True, right_index=True)
#     # calculating the prorated clicks knowing the splits pct
#     output_pm['prorated_clicks']=output_pm.rd_value*output_pm.slab_cpd
#     output_merge = output_pm.groupby(by=['AdvertiserName','Product'],as_index=False)\
#     ['AdvertiserName','Product','prorated_clicks'].sum()
#     if i == 0 and z_index == 0:
#         rotation_table = output_pm.copy()
#     else:
#         rotation_table = rotation_table.append(output_pm, ignore_index = True)

#     #print('test2')

#     #updating the Ad_ops for next iteration
#     Ad_ops_slab = pd.merge(Ad_ops_slab, \
#             output_merge,\
#            'left',on=['AdvertiserName','Product'])
#     print(Ad_ops_slab)
#     # Filling NA with 0
#     Ad_ops_slab['prorated_clicks'] = Ad_ops_slab[['prorated_clicks']].fillna(value=0)
#     # update remaining budget
#     Ad_ops_slab['slab_budget'] -= Ad_ops_slab['prorated_clicks']
#     Ad_ops_slab['slab_running'] -= Ad_ops_slab['prorated_clicks']
#     # Then need to remove the last two columns
#     Ad_ops_slab.drop(['prorated_clicks'],axis=1,inplace=True)
#     df_list = [google_feed, total_pm_pct, total_idx, output_pm]
#     del df_list



In [707]:
# total_idx_mean = total_idx.copy()

In [708]:
# total_idx_mean_rest = np.mean(total_idx_mean.loc[np.isfinite(total_idx_mean)])

In [709]:
# total_idx_mean.replace([np.inf, -np.inf], total_idx_mean_rest)

In [710]:
Ad_ops_slab_add_on['slab_budget'] = 0.0
Ad_ops_slab_add_on['slab_running'] = Ad_ops_slab_add_on['remain_budget']

In [711]:
Ad_ops_slab = Ad_ops_slab.append(Ad_ops_slab_add_on)

In [712]:
Ad_ops_slab

AdvertiserName  Pacing to Optimal   Product  \
0   American Express National Bank  207.666667         Savings    
1   American Express National Bank  0.000000           CDs        
2   North American Savings Bank     0.000000           Savings    
3   Goldman Sachs Bank USA          3667.000000        Both       
4   Capital One                    -312.333333         MMA        
5   HSBC Direct                     314.333333         Savings    
6   Barclays                        2167.000000        Savings    
7   nbkc bank                      -81.000000          Checking   
8   UFB Direct                     -59.000000          Savings    
9   First Internet Bank            -134.666667         Business   
10  Barclays                        1659.000000        CDs        
11  Live Oak Bank                  -15.000000          Business   
12  nbkc bank                      -26.000000          Business   
13  Synchrony Bank                  0.000000           Both       
14  Ally Bank                       2670.000000        CDs        
15  Capital One                     0.000000           Business   
16  CIT Bank                        0.000000           Savings    
17  Vio Bank                        0.000000           CDs        
18  Axos Bank                       0.000000           Checking   
19  Axos Bank                       0.000000           Business   
20  Citizens Access                 0.000000           Both       
21  PurePoint Financial             0.000000           Savings    
22  First Internet Bank             12.000000          MMA        
23  earn.bank                       0.000000           MMA        
24  Citi                            0.000000           Savings    
6   Ally Bank                       569.366667         Savings    
9   Vio Bank                        330.333333         Savings    
10  Capital One                     2323.333333        CDs        
14  Aspiration                     -66.388889          Checking   
17  BBVA Compass                   -0.488889           Checking   
27  PurePoint Financial             0.000000           CDs        
30  Discover Bank                   38.000000          Both       

    Running Budget  pacing_indx  remain_budget  slab_budget  slab_running  
0   345.258576      0.949152     259.257345     3.716728     3.716728      
1   0.000000        1.000000     0.000000       0.000000     0.000000      
2   0.000000        1.000000     0.000000       0.000000     0.000000      
3   708.643380      0.397917     259.406701    -5.755169    -5.755169      
4   276.809020      1.081651     269.822578     99.352333    99.352333     
5   229.742270      0.924048     174.807743    -0.288291    -0.288291      
6   141.730910      0.580095     67.961482     -4.662646    -4.662646      
7   51.675113       1.020564     36.517335      20.306957    20.306957     
8   26.974286       1.014937     21.885583     -0.644229    -0.644229      
9   23.840599       1.034421     7.171650      -3.942319    -3.942319      
10  15.869527       0.659084     15.869527      15.869527    15.869527     
11  10.261289       1.003777     2.311719      -0.180475    -0.180475      
12  6.267374        1.006555     4.396124       1.276660     1.276660      
13  0.000000        1.000000     0.000000       0.000000     0.000000      
14  0.000000        0.511214     0.000000       0.000000     0.000000      
15  0.000000        1.000000     0.000000       0.000000     0.000000      
16  0.000000        1.000000     0.000000       0.000000     0.000000      
17  0.000000        1.000000     0.000000       0.000000     0.000000      
18  0.000000        1.000000     0.000000       0.000000     0.000000      
19  0.000000        1.000000     0.000000       0.000000     0.000000      
20  0.000000        1.000000     0.000000       0.000000     0.000000      
21  0.000000        1.000000     0.000000       0.000000     0.000000      
22  0.000000        0.996989     0.000000       0.000000    

In [713]:
agg_table = rotation_table.groupby(by = ['AdvertiserName','Apy','budget_product','ProductName', 'ZoneName','Running Budget','Pacing to Optimal'],as_index=False).sum()[['AdvertiserName','Apy','budget_product','ProductName', 'ZoneName','Running Budget','Pacing to Optimal','rd_value','prorated_clicks']]

In [714]:
agg_table['Total_split'] = agg_table['rd_value']/slab

In [715]:
agg_tb_rows_pre_ow = agg_table.shape[0]

In [716]:
agg_table = agg_table.append(agg_ow,ignore_index=True)

In [717]:
# add new column based on row numbers: https://stackoverflow.com/questions/46113078/pandas-add-value-at-specific-iloc-into-new-dataframe-column
agg_table.loc[0:agg_tb_rows_pre_ow-1,'overwrite'] = 0
#agg_table.loc[agg_tb_rows_pre_ow,'overwrite'] = 1
agg_table.overwrite.fillna(1,inplace=True)

In [718]:
agg_table

AdvertiserName   Apy  Pacing to Optimal  \
0   American Express National Bank  2.10  207.666667          
1   American Express National Bank  2.10  207.666667          
2   American Express National Bank  2.10  207.666667          
3   American Express National Bank  2.10  207.666667          
4   American Express National Bank  2.10  207.666667          
5   American Express National Bank  2.10  207.666667          
6   American Express National Bank  2.10  207.666667          
7   American Express National Bank  2.10  207.666667          
8   American Express National Bank  2.10  207.666667          
9   American Express National Bank  2.10  207.666667          
10  American Express National Bank  2.10  207.666667          
11  American Express National Bank  2.10  207.666667          
12  American Express National Bank  2.10  207.666667          
13  American Express National Bank  2.10  207.666667          
14  American Express National Bank  2.10  207.666667          
15  American Express National Bank  2.10  207.666667          
16  American Express National Bank  2.10  207.666667          
17  American Express National Bank  2.10  207.666667          
18  American Express National Bank  2.10  207.666667          
19  Barclays                        2.20  2167.000000         
20  Barclays                        2.20  2167.000000         
21  Barclays                        2.20  2167.000000         
22  Barclays                        2.20  2167.000000         
23  Barclays                        2.20  2167.000000         
24  Barclays                        2.20  2167.000000         
25  Capital One                     2.00 -312.333333          
26  Capital One                     2.00 -312.333333          
27  Capital One                     2.00 -312.333333          
28  Capital One                     2.00 -312.333333          
29  Capital One                     2.00 -312.333333          
30  Capital One                     2.00 -312.333333          
31  Capital One                     2.00 -312.333333          
32  Capital One                     2.00 -312.333333          
33  Capital One                     2.00 -312.333333          
34  First Internet Bank             2.02 -134.666667          
35  First Internet Bank             2.02 -134.666667          
36  Goldman Sachs Bank USA          2.25  3667.000000         
37  Goldman Sachs Bank USA          2.25  3667.000000         
38  Goldman Sachs Bank USA          2.25  3667.000000         
39  Goldman Sachs Bank USA          2.25  3667.000000         
40  Goldman Sachs Bank USA          2.25  3667.000000         
41  Goldman Sachs Bank USA          2.25  3667.000000         
42  Goldman Sachs Bank USA          2.25  3667.000000         
43  Goldman Sachs Bank USA          2.25  3667.000000         
44  Goldman Sachs Bank USA          2.70  3667.000000         
45  Goldman Sachs Bank USA          2.70  3667.000000         
46  HSBC Direct                     2.25  314.333333          
47  HSBC Direct                     2.25  314.333333          
48  HSBC Direct                     2.25  314.333333          
49  HSBC Direct                     2.25  314.333333          
50  HSBC Direct                     2.25  314.333333          
51  HSBC Direct                     2.25  314.333333          
52  HSBC Direct                     2.25  314.333333          
53  Live Oak Bank                   1.10 -15.000000           
54  Live Oak Bank                   1.10 -15.000000           
55  UFB Direct                      2.45 -59.000000           
56  UFB Direct                      2.45 -59.000000           
57  UFB Direct                      2.45 -59.000000           
58  nbkc bank                       0.00 -26.000000           
59  nbkc bank                       0.00 -26.000000           
60  nbkc bank                       1.01 -81.000000           
61  nbkc bank                       1.01 -81.000000           
62  nbkc bank                       1.01 -81.000000

In [719]:
agg_table.sort_values(by=['ZoneName'],inplace=True)

In [720]:
Advertiser_running['remain_budget_mm']=Advertiser_running['Running Budget']-Advertiser_running['ClickPerDay_mm']
temp_mm = result_mm[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay']]\
.merge(Advertiser_running[['AdvertiserName','Product','Running Budget','Pacing to Optimal','remain_budget_mm']]\
       ,'left',left_on=['AdvertiserName','budget_product'],right_on=['AdvertiserName','Product'])

temp_mm.drop(columns=['Product'],axis=1,inplace=True)
temp_mm.rename(columns={'ClickPerDay':'prorated_clicks','remain_budget_mm':'remain_budget'},inplace=True)
temp_mm['rd_value'] = 1.0

In [721]:
Advertiser_running['remain_budget_ao']=Advertiser_running['remain_budget_mm']-Advertiser_running['ClickPerDay_ao']
temp_ao = result_ao[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay']]\
.merge(Advertiser_running[['AdvertiserName','Product','Running Budget','Pacing to Optimal','remain_budget_ao']]\
       ,'left',left_on=['AdvertiserName','budget_product'],right_on=['AdvertiserName','Product'])

temp_ao.drop(columns=['Product'],axis=1,inplace=True)
temp_ao.rename(columns={'ClickPerDay':'prorated_clicks','remain_budget_ao':'remain_budget'},inplace=True)
temp_ao['rd_value'] = 1.0

In [722]:
Advertiser_running['remain_budget_mpa']=Advertiser_running['remain_budget_ao']-Advertiser_running['ClickPerDay_mpa']
temp_mpa = result_mpa[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay']]\
.merge(Advertiser_running[['AdvertiserName','Product','Running Budget','Pacing to Optimal','remain_budget_mpa']]\
       ,'left',left_on=['AdvertiserName','budget_product'],right_on=['AdvertiserName','Product'])

temp_mpa.drop(columns=['Product'],axis=1,inplace=True)
temp_mpa.rename(columns={'ClickPerDay':'prorated_clicks','remain_budget_mpa':'remain_budget'},inplace=True)
temp_mpa['rd_value'] = 1.0

In [723]:
# making output table

# make the zone 1-3 output the same as others
Advertiser_running['remain_budget_dp']=Advertiser_running['remain_budget_mpa']-Advertiser_running['ClickPerDay_dp']
temp_dp = result_dp[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay']]\
.merge(Advertiser_running[['AdvertiserName','Product','Running Budget','Pacing to Optimal','remain_budget_dp']]\
       ,'left',left_on=['AdvertiserName','budget_product'],right_on=['AdvertiserName','Product'])

# remove product since it's the same as budget product
temp_dp.drop(columns=['Product'],axis=1,inplace=True)
temp_dp.rename(columns={'ClickPerDay':'prorated_clicks','remain_budget_dp':'remain_budget'},inplace=True)
temp_dp['rd_value'] = 1.0

In [724]:
output_table = temp_mm.copy()
output_table = output_table.append(temp_ao,ignore_index=True)
output_table = output_table.append(temp_mpa,ignore_index=True)
output_table = output_table.append(temp_dp,ignore_index=True)

In [725]:
#Summary 1: recording clicks summing over zone name
#Drop remain budget for summary table because can't have it when aggregate lines
output_slab_sum = output_table.drop('remain_budget', axis = 1)
output_slab_sum.rename(columns={'rd_value':'Total_split'},inplace=True)
output_slab_sum['overwrite'] = 0
output_slab_sum_agg = output_slab_sum.append\
(agg_table[['AdvertiserName','Apy','budget_product','ProductName','ZoneName',\
                 'prorated_clicks','Running Budget','Pacing to Optimal','Total_split','overwrite']], ignore_index=True)

In [726]:
#summary 2: recording each line of actions
output_table_granular = output_table.append\
(rotation_table[['AdvertiserName','Apy','budget_product','ProductName','ZoneName',\
                 'prorated_clicks','Running Budget','remain_budget','rd_value']], ignore_index=True)
# need to change data type
output_table_granular[['prorated_clicks','rd_value']] = output_table_granular[['prorated_clicks','rd_value']].round(2)
# show total clicks per budget item
output_table_granular.groupby(by=['AdvertiserName','budget_product'], as_index=False)['AdvertiserName','budget_product','prorated_clicks'].sum()

AdvertiserName budget_product  prorated_clicks
0   Ally Bank                       Savings        242.07         
1   American Express National Bank  Savings        341.50         
2   Aspiration                      Checking       27.23          
3   BBVA Compass                    Both           3.72           
4   BBVA Compass                    Checking       5.94           
5   Barclays                        Savings        146.43         
6   Capital One                     CDs            47.34          
7   Capital One                     MMA            177.49         
8   Discover Bank                   Both           30.73          
9   First Internet Bank             Business       27.77          
10  Goldman Sachs Bank USA          Both           711.73         
11  HSBC Direct                     Savings        153.58         
12  Live Oak Bank                   Business       10.43          
13  PurePoint Financial             CDs            122.65         
14  Simple                          Checking       22.71          
15  UFB Direct                      Savings        27.62          
16  Vio Bank                        Savings        63.06          
17  nbkc bank                       Business       4.97           
18  nbkc bank                       Checking       31.36

In [727]:
zone_sort.head(5)

ZoneName         ZoneType  ZoneID  \
0  MagnifyMoney - Rate table and Blogs (Sav and MMA)  Rate Tables      116      
1  MagnifyMoney - LP (Sav)                            Landing Page     148      
2  MagnifyMoney - LP (CD)                             Landing Page     149      
3  MagnifyMoney - Rate table and Blogs (CD)           Rate Tables      117      
4  MagnifyMoney - BP - Most Popular Accounts          Bank Page - Own  158      

   averageClicks  SpotAvailable zonegroup  open_rate  SpotUsed  account_open  
0  78.212817      20             zone_1    0.087      0         6.804515      
1  8.465608       20             zone_1    0.046      0         0.389418      
2  9.687878       30             zone_1    0.040      0         0.387515      
3  28.173652      20             zone_1    0.027      0         0.760689      
4  7.215324       20             zone_1    0.020      0         0.144306

In [728]:
# To Create Remaining Inventory Tracking
# need to use the original spots available for rounding
#Find total used by Zone
spot_usage = agg_table.groupby(by=['ZoneName'],as_index=False).sum()[['ZoneName','Total_split']]

def ProductType(zone):
    if 'Bus' in zone:
        return 'Business'
    elif 'CD' in zone:
        return 'CDs'
    elif 'Sav' in zone:
        return 'Savings'
    elif 'Ch' in zone:
        return 'Checking'
    elif 'MM' in zone:
        return 'MMA'
    elif 'Money Market' in zone:
        return 'MMA'
    elif 'IRA' in zone:
        return 'IRAs'
    else:
        return 'Both'

    ## use zone_sort instead, so it will has the right spots available for rounding
inventory_1 = pd.merge(spot_usage, zone_sort[['ZoneName','SpotAvailable','averageClicks','open_rate']], how = 'right',\
        on='ZoneName')

inventory_1['product_type'] = inventory_1.ZoneName.apply(ProductType)

## Adding total advertiser count on SOT
inventory_1 = pd.merge(inventory_1, sot_loop_slab.groupby(by=['ZoneName']).nunique()[['AdvertiserName']], 'inner', on='ZoneName')

#Cap available spots, compare both and find the min
inventory_1.SpotAvailable = np.minimum(inventory_1.SpotAvailable,10)

#coming up with remaining inventory
inventory_1.rename(columns={'AdvertiserName':'elig_adv_ct'},inplace=True)
inventory_1.fillna(0.0,inplace=True)
inventory_1['remain_inv'] = round(inventory_1.SpotAvailable - inventory_1.Total_split,2)
inventory_1['potential_clicks'] = round(inventory_1.remain_inv * inventory_1.averageClicks,2)


In [729]:
# Compute the amount added back to original output to round it up
inventory_1['second_round_to_add'] = inventory_1.remain_inv*10%10/10

In [730]:
# can i add % to pacing?
output_slab_sum_agg['pacing_rank']=output_slab_sum_agg.groupby(by=['ZoneName'])['Pacing to Optimal'].rank(method='dense',ascending=True)

In [731]:
output_slab_sum_agg['budget_rank']=output_slab_sum_agg.groupby(by=['ZoneName'])['Running Budget'].rank(method='dense',ascending=False)

In [732]:
decimal_working = output_slab_sum_agg.loc[(output_slab_sum_agg['Total_split']!=1)&(output_slab_sum_agg.overwrite == 0.0)]\
.reset_index().merge(inventory_1[['ZoneName','second_round_to_add']][inventory_1['remain_inv']>0],'inner',on='ZoneName').set_index('index')

decimal_working_ct = decimal_working.groupby(by='ZoneName',as_index=False).count()[['ZoneName','AdvertiserName']]

decimal_working_ct.rename(columns={'AdvertiserName':'ad_ct'}, inplace=True)

decimal_working = decimal_working.reset_index().merge(decimal_working_ct, 'left', on='ZoneName').set_index('index')

decimal_working['final_to_add'] = decimal_working['second_round_to_add']/decimal_working['ad_ct']

# decimal_working['room_to_add'] = 1 - decimal_working['Total_split']

decimal_working['Temp_split_update'] = np.minimum(decimal_working['Total_split'] + decimal_working['final_to_add'],1)

In [733]:
# third round: Find out remaining 
decimal_rd_working = decimal_working.groupby(['ZoneName'],as_index=False)['ZoneName','Total_split','final_to_add','Temp_split_update'].sum()

# find out that goes above 1 that didn't get added
decimal_rd_working['third_rd_add'] = decimal_rd_working['Total_split'] + decimal_rd_working['final_to_add'] - decimal_rd_working['Temp_split_update']

# find the number of non-1 advertisers to add the remaining splits
decimal_rd_working_ct = decimal_working[decimal_working.Temp_split_update < 1.0].groupby(by='ZoneName',as_index=False).count()[['ZoneName','AdvertiserName']]

decimal_rd_working_ct.rename(columns={'AdvertiserName':'ad_ct_2nd'}, inplace=True)

# add the counts into decimal table
decimal_working = decimal_working.reset_index().merge(decimal_rd_working_ct, 'left', on='ZoneName').set_index('index')

#Add the excess back to the table
decimal_working = decimal_working.merge(decimal_rd_working[['ZoneName','third_rd_add']],'left',on='ZoneName')

decimal_working['final_to_add_2'] = decimal_working['third_rd_add']/decimal_working['ad_ct_2nd']

# Get the amount
decimal_working['Total_split_update'] = np.minimum(decimal_working['Temp_split_update']+decimal_working['final_to_add_2'],1)

# fill total split update NA with temp split update
decimal_working['Total_split_update'].fillna(decimal_working['Temp_split_update'],inplace=True)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:21: RuntimeWarning: invalid value encountered in minimum


In [734]:
#merge the two table to have the split update column
final_output = pd.merge(output_slab_sum_agg, decimal_working[['AdvertiserName','ZoneName','ProductName','Total_split','Total_split_update']], 'left', on= ['AdvertiserName','ZoneName','ProductName','Total_split'])

In [735]:
#fill that split update column NA to 0
final_output.fillna(0.0,inplace=True)

In [736]:
# add a final column to take the max of both
final_output['final_split'] = np.max(final_output[['Total_split','Total_split_update']], axis = 1)

In [737]:
final_output.drop(['Total_split','Total_split_update','Running Budget','Pacing to Optimal'],axis=1,inplace=True)

In [738]:
##########################Now just need to add capOne back onto the placement and round the numbers. Explore Optimization Rounding function

In [739]:
final_output.sort_values(by=['ZoneName','Apy','pacing_rank'],ascending=[True,False,True])

AdvertiserName   Apy budget_product  \
65   American Express National Bank  2.10  Savings         
66   Capital One                     2.00  MMA             
48   Goldman Sachs Bank USA          3.00  Both            
42   Capital One                     2.80  CDs             
41   Capital One                     2.70  CDs             
47   Goldman Sachs Bank USA          2.70  Both            
44   Discover Bank                   2.65  Both            
53   Vio Bank                        2.46  Savings         
52   UFB Direct                      2.45  Savings         
50   HSBC Direct                     2.25  Savings         
49   Goldman Sachs Bank USA          2.25  Both            
35   Ally Bank                       2.20  Savings         
40   Barclays                        2.20  Savings         
45   Discover Bank                   2.10  Both            
36   American Express National Bank  2.10  Savings         
46   First Internet Bank             2.02  Business        
38   BBVA Compass                    2.00  Both            
43   Capital One                     2.00  MMA             
37   Aspiration                      2.00  Checking        
51   Live Oak Bank                   1.10  Business        
55   nbkc bank                       1.01  Checking        
54   nbkc bank                       0.00  Business        
39   BBVA Compass                    0.00  Checking        
28   Discover Bank                   3.00  Both            
27   Capital One                     2.70  CDs             
33   Vio Bank                        2.46  Savings         
32   UFB Direct                      2.45  Savings         
30   HSBC Direct                     2.25  Savings         
29   Goldman Sachs Bank USA          2.25  Both            
22   Ally Bank                       2.20  Savings         
26   Barclays                        2.20  Savings         
23   American Express National Bank  2.10  Savings         
24   Aspiration                      2.00  Checking        
31   Live Oak Bank                   1.10  Business        
34   nbkc bank                       1.01  Checking        
25   BBVA Compass                    0.00  Checking        
67   nbkc bank                       1.01  Checking        
68   American Express National Bank  2.10  Savings         
69   American Express National Bank  2.10  Savings         
72   Goldman Sachs Bank USA          2.25  Both            
71   Barclays                        2.20  Savings         
70   American Express National Bank  2.10  Savings         
73   American Express National Bank  2.10  Savings         
57   PurePoint Financial             2.80  CDs             
58   PurePoint Financial             2.50  CDs             
56   Goldman Sachs Bank USA          2.35  Both            
60   PurePoint Financial             2.80  CDs             
61   PurePoint Financial             2.50  CDs             
59   Goldman Sachs Bank USA          2.35  Both            
64   PurePoint Financial             2.80  CDs             
63   PurePoint Financial             2.50  CDs             
62   Goldman Sachs Bank USA          2.35  Both            
74   American Express National Bank  2.10  Savings         
75   American Express National Bank  2.10  Savings         
76   HSBC Direct                     2.25  Savings         
79   Goldman Sachs Bank USA          2.25  Both            
77   Barclays                        2.20  Savings         
80   American Express National Bank  2.10  Savings         
78   Capital One                     2.00  MMA             
83   HSBC Direct                     2.25  Savings         
82   Goldman Sachs Bank USA          2.25  Both            
81   Barclays                        2.20  Savings         
85   American Express National Bank  2.10  Savings         
84   Capital One                     2.00  MMA             
86   Goldman Sachs Bank USA          2.70  Both            
87   Capital One                     2.80  CDs             
9

In [740]:
# To Create Remaining Inventory Tracking
#Find total used by Zone
spot_usage = final_output.groupby(by=['ZoneName'],as_index=False).sum()[['ZoneName','final_split']]

inventory_2 = pd.merge(spot_usage, zone_sort[['ZoneName','SpotAvailable','averageClicks','open_rate']], how = 'right',\
        on='ZoneName')

inventory_2['product_type'] = inventory_2.ZoneName.apply(ProductType)

In [741]:
## Adding total advertiser count on SOT
inventory_2 = pd.merge(inventory_2, sot_loop_slab.groupby(by=['ZoneName']).nunique()[['AdvertiserName']], 'inner', on='ZoneName')

#Cap available spots, compare both and find the min
inventory_2.SpotAvailable = np.minimum(inventory_2.SpotAvailable,10)

#coming up with remaining inventory
inventory_2.rename(columns={'AdvertiserName':'elig_adv_ct'},inplace=True)
inventory_2.fillna(0.0,inplace=True)
inventory_2['remain_inv'] = round(inventory_2.SpotAvailable - inventory_2.final_split,2)
inventory_2['potential_clicks'] = round(inventory_2.remain_inv * inventory_2.averageClicks,2)


In [742]:
inventory_2.sort_values('ZoneName')

ZoneName  final_split  \
31  Account Comparison (2yr CD)                                   0.0           
54  Account Comparison (3yr CD)                                   0.0           
56  Account Comparison (4yr CD)                                   0.0           
38  Account Comparison (Savings)                                  0.0           
0   Bank Pages - Horizontal                                       2.0           
50  Bank Pages Sponsored - Popular Accounts Comparison (18mo CD)  0.0           
39  Bank Pages Sponsored - Popular Accounts Comparison (1yr CD)   0.0           
32  Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)   0.0           
49  Bank Pages Sponsored - Popular Accounts Comparison (3yr CD)   0.0           
51  Bank Pages Sponsored - Popular Accounts Comparison (4yr CD)   0.0           
45  Bank Pages Sponsored - Popular Accounts Comparison (5yr CD)   0.0           
1   Bank Pages Sponsored - Popular Accounts Comparison (Chk)      1.0           
2   Bank Pages Sponsored - Popular Accounts Comparison (MMA)      1.0           
3   Bank Pages Sponsored - Popular Accounts Comparison (Sav)      1.0           
52  Blog Best CD Accounts                                         0.0           
4   Blog Best Savings Accounts                                    2.0           
35  Bonus Offers Page - Savings                                   0.0           
5   CC - Sidebar - Featured Accounts                              1.0           
6   HiatusApp - Recommended Accounts                              1.0           
7   KPGR - Sidebar - Featured Accounts                            1.0           
41  LP - Native (1yr CD)                                          0.0           
42  LP - Native (2yr CD)                                          0.0           
43  LP - Native (5yr CD)                                          0.0           
8   LP - Native (Sav)                                             4.0           
36  LP - Native MSN Page (CDs)                                    0.0           
9   LP - Native MSN Page (Savings)                                4.0           
10  LP - SEM (1yr CD)                                             1.0           
11  LP - SEM (2yr CD)                                             0.0           
44  LP - SEM (3yr CD)                                             0.0           
46  LP - SEM (4yr CD)                                             0.0           
40  LP - SEM (5yr CD)                                             0.0           
12  LP - SEM (Sav)                                                5.0           
13  LP - SEM B (Sav)                                              3.0           
30  LT - CRM Email                                                0.0           
55  LT - Rate Table (1yr CD)                                      0.0           
57  LT - Rate Table (2yr CD)                                      0.0           
59  LT - Rate Table (5yr CD)                                      0.0           
37  LT - Rate Table (Chk)                                         0.0           
14  LT - Rate Table (MMA)                                         1.0           
15  LT - Rate Table (Savings)                                     5.0           
16  LT - Sidebar - Featured Accounts                              1.0           
17  MagnifyMoney - Featured Accounts Sidebar                      3.0           
48  Main Rate Table (18mo CD)                                     0.0           
18  Main Rate Table (2yr CD)                                      1.0           
53  Main Rate Table (3yr CD)                                      0.0           
58  Main Rate Table (4yr CD)                                      0.0           
47  Main Rate Table (5yr CD)                                      0.0           
34  Main Rate Table (6mo CD)                                      0.0           
19  Main Rate Table (Bus. Checking)                               1.0           
33  Ma

#### Second Round Fill-in

In [744]:
#Find eligible placements for 2nd round, remove restriction on native
df_sec_rotation = inventory_2.loc[(inventory_2.remain_inv>0)]# & (~inventory_2.ZoneName.str.contains("LP - Native"))]

In [745]:
# to find rows that are not in final output
sot_sec = sot_loop.merge(final_output[['AdvertiserName','ProductName','ZoneName','final_split']], how = 'left', on=['AdvertiserName','ProductName','ZoneName'])

In [746]:
# if 0, then it's not in final table
sot_sec.fillna(0.0,inplace=True)

In [747]:
# Eligible SOT Zone --> in zones that has spots left and if the advertisers have not been picked in this zone
# sot_sec = sot_sec[sot_sec.ZoneName.isin(df_sec_rotation.ZoneName) & (sot_sec.final_split == 0.0)]

# *******************************what if I open up for anyone that has % below 1.0; but not overwrite zone
sot_sec = sot_sec[sot_sec.ZoneName.isin(df_sec_rotation.ZoneName) & (sot_sec.final_split < 1.0) \
                 & ~sot_sec.ZoneName.isin(ow_zone)]

In [748]:
sot_sec = sot_sec.merge(df_sec_rotation[['ZoneName','remain_inv']],'left', on='ZoneName')

In [749]:
# Find the expected clicks from Magnify and Bank Page; will wait on display until it's fixed.
# Advertiser_running[['Advertiser','Product','ClickPerDay_mm','ClickPerDay_mpa','ClickPerDay_ao']]

In [750]:
Ad_ops_slab = Ad_ops_slab.merge(Advertiser_running[['Advertiser','Product','ClickPerDay_mm','ClickPerDay_mpa','ClickPerDay_ao']]\
                  , how='inner', right_on = ['Advertiser','Product'], left_on = ['AdvertiserName','Product'])

In [751]:
Ad_ops_slab.drop('Advertiser',axis = 1, inplace=True)

In [752]:
# monthly budget
Ad_ops_slab['mth_budget_no_organic'] = (Ad_ops_slab['Running Budget']-\
                                        Ad_ops_slab['ClickPerDay_mm']-\
                                        Ad_ops_slab['ClickPerDay_mpa']-\
                                        Ad_ops_slab['ClickPerDay_ao'])*days_cur_mth

In [753]:
# clean up table
Ad_ops_slab.drop(['ClickPerDay_mm','ClickPerDay_mpa','ClickPerDay_ao'],axis = 1, inplace=True)

In [754]:
Ad_ops_slab['mth_budget'] = Ad_ops_slab['Running Budget']*days_cur_mth

In [755]:
Ad_ops_slab['mth_pacing_budget'] = Ad_ops_slab['Running Budget']*days_left_cur_mth

In [756]:
#### Qualifying for back fill (50% of pacing budget then no)
Ad_ops_sec_rd = Ad_ops_slab[Ad_ops_slab.mth_budget_no_organic > Ad_ops_slab.mth_pacing_budget*0.5]

In [757]:
## eliminate ineligible advertisers based on budget
sot_sec = sot_sec.merge(Ad_ops_sec_rd[['AdvertiserName','Product']],'inner', right_on=['AdvertiserName','Product'], left_on=['AdvertiserName','budget_product'])

In [758]:
Ad_ops_sec_rd

AdvertiserName  Pacing to Optimal   Product  \
0   American Express National Bank  207.666667         Savings    
3   Goldman Sachs Bank USA          3667.000000        Both       
4   Capital One                    -312.333333         MMA        
5   HSBC Direct                     314.333333         Savings    
6   Barclays                        2167.000000        Savings    
7   nbkc bank                      -81.000000          Checking   
8   UFB Direct                     -59.000000          Savings    
9   First Internet Bank            -134.666667         Business   
10  Barclays                        1659.000000        CDs        
12  nbkc bank                      -26.000000          Business   

    Running Budget  pacing_indx  remain_budget  slab_budget  slab_running  \
0   345.258576      0.949152     259.257345     3.716728     3.716728       
3   708.643380      0.397917     259.406701    -5.755169    -5.755169       
4   276.809020      1.081651     269.822578     99.352333    99.352333      
5   229.742270      0.924048     174.807743    -0.288291    -0.288291       
6   141.730910      0.580095     67.961482     -4.662646    -4.662646       
7   51.675113       1.020564     36.517335      20.306957    20.306957      
8   26.974286       1.014937     21.885583     -0.644229    -0.644229       
9   23.840599       1.034421     7.171650      -3.942319    -3.942319       
10  15.869527       0.659084     15.869527      15.869527    15.869527      
12  6.267374        1.006555     4.396124       1.276660     1.276660       

    mth_budget_no_organic    mth_budget  mth_pacing_budget  
0   7777.720359            10357.757272  6214.654363        
3   10908.972264           21259.301409  12755.580845       
4   8094.677336            8304.270602   4982.562361        
5   5244.232299            6892.268097   4135.360858        
6   2038.844455            4251.927313   2551.156388        
7   1095.520052            1550.253402   930.152041         
8   656.567478             809.228589    485.537153         
9   215.149509             715.217979    429.130787         
10  476.085819             476.085819    285.651492         
12  131.883721             188.021221    112.812733

In [759]:
## second-run control multiplier

second_run_ctrl = 0

if days_left_cur_mth <= 16:
    second_run_ctrl = 0.1
elif days_left_cur_mth <= 20:
    second_run_ctrl = 0.0
else:
    second_run_ctrl = 0.0

In [760]:
## Second run to fill open spot

running_dummy = 0
for idx, row in df_sec_rotation.iterrows():
    print(idx)
    print(row.remain_inv)
    # get all the SOT for this row
    temp_df_1 = sot_sec.loc[sot_sec.ZoneName == row['ZoneName']]
    
    #Qualify advertiser one more time - have one more day of budget
    temp_ad = Ad_ops_sec_rd[(Ad_ops_sec_rd.slab_running+Ad_ops_sec_rd.remain_budget*second_run_ctrl) > 0.0]
    
    #match the first 6 columns of final output, others can be joined later***
    temp_df_1 = temp_df_1[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay','final_split','remain_inv']]
    # slab_running rank
    temp_df_2 = temp_df_1.merge(temp_ad[['AdvertiserName','Product','slab_running']]\
                          ,'inner',left_on=['AdvertiserName','budget_product']\
                          , right_on = ['AdvertiserName','Product'])

    # create 1 - split
    temp_df_2['add_cap'] = 1 - temp_df_2.final_split
    
    # sort by slab running
    temp_df_2.sort_values(by = ['add_cap','slab_running'], ascending=[True,False], inplace=True)
    
    # fille in for split and qualify based on cap remaining
    temp_df_2['cum_perc'] = temp_df_2['add_cap'].cumsum()
    temp_df_2['use_cap'] = temp_df_2['remain_inv'] - temp_df_2['cum_perc'] 
    temp_df_2 = temp_df_2[temp_df_2['use_cap'] >= 0.0] # has to have equal sign in case it adds to 0
    temp_df_2['prorated_clicks'] = temp_df_2['ClickPerDay'] * (temp_df_2['add_cap'] + temp_df_2['final_split'])
    temp_df_2['output_split'] = temp_df_2['add_cap'] + temp_df_2['final_split']
    
    # depending on the spots, fill in from high to low
    if running_dummy == 0:
        #find rows that is closest to and below remain inventory  
        temp_df_3 = temp_df_2.head(int(row.remain_inv))
    else:
        temp_df_3 = temp_df_3.append(temp_df_2, ignore_index = True)
    # update ad budget table by the clicks above; also continue to qualify advertisers product
    temp_df_4 = temp_df_2.groupby(['AdvertiserName','budget_product'],as_index=False)\
    ['AdvertiserName','budget_product','prorated_clicks'].sum()
    
    #updating the Ad_ops for next iteration
    Ad_ops_sec_rd = pd.merge(Ad_ops_sec_rd, temp_df_4,\
           'left', left_on=['AdvertiserName','Product'], right_on=['AdvertiserName','budget_product'])
    
    #print(Ad_ops_sec_rd)
    # Filling NA with 0
    Ad_ops_sec_rd['prorated_clicks'] = Ad_ops_sec_rd[['prorated_clicks']].fillna(value=0)
    # update remaining budget
    Ad_ops_sec_rd['slab_running'] -= Ad_ops_sec_rd['prorated_clicks']
    #print(Ad_ops_sec_rd)
    # Then need to remove the last two columns
    Ad_ops_sec_rd.drop(['prorated_clicks','budget_product'],axis=1,inplace=True)
    ### need to qualify again so it won't go too low
    print(temp_df_2)
    
    #print(Ad_ops_sec_rd)
    running_dummy += temp_df_2.shape[0]
    
    

4
8.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
5
3.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
6
1.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
7
3.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
8
6.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_s

Empty DataFrame
Columns: [Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, AdvertiserName, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
58
5.0
Empty DataFrame
Columns: [Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, AdvertiserName, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []
59
10.0
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, final_split, remain_inv, Product, slab_running, add_cap, cum_perc, use_cap, prorated_clicks, output_split]
Index: []


In [761]:
# find the same items that's share
new_final = pd.merge(temp_df_3[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','output_split']],\
         final_output,\
         'right',on=['AdvertiserName','Apy','budget_product','ProductName','ZoneName'])

In [762]:
new_final['split'] = np.where(new_final.output_split.isna(),new_final.final_split,new_final.output_split)

In [763]:
new_final.drop(['output_split','final_split'],axis = 1,inplace=True)

In [764]:
new_final

AdvertiserName   Apy budget_product  \
0    Ally Bank                       2.20  Savings         
1    American Express National Bank  2.10  Savings         
2    Aspiration                      2.00  Checking        
3    Goldman Sachs Bank USA          2.70  Both            
4    Goldman Sachs Bank USA          2.25  Both            
5    Live Oak Bank                   1.10  Business        
6    Simple                          2.02  Checking        
7    American Express National Bank  2.10  Savings         
8    Goldman Sachs Bank USA          2.25  Both            
9    HSBC Direct                     2.25  Savings         
10   Goldman Sachs Bank USA          2.70  Both            
11   Aspiration                      2.00  Checking        
12   Simple                          2.02  Checking        
13   nbkc bank                       1.01  Checking        
14   Ally Bank                       2.20  Savings         
15   American Express National Bank  2.10  Savings         
16   Barclays                        2.20  Savings         
17   Discover Bank                   2.10  Both            
18   First Internet Bank             2.02  Business        
19   Goldman Sachs Bank USA          2.25  Both            
20   HSBC Direct                     2.25  Savings         
21   Vio Bank                        2.46  Savings         
22   Ally Bank                       2.20  Savings         
23   American Express National Bank  2.10  Savings         
24   Aspiration                      2.00  Checking        
25   BBVA Compass                    0.00  Checking        
26   Barclays                        2.20  Savings         
27   Capital One                     2.70  CDs             
28   Discover Bank                   3.00  Both            
29   Goldman Sachs Bank USA          2.25  Both            
30   HSBC Direct                     2.25  Savings         
31   Live Oak Bank                   1.10  Business        
32   UFB Direct                      2.45  Savings         
33   Vio Bank                        2.46  Savings         
34   nbkc bank                       1.01  Checking        
35   Ally Bank                       2.20  Savings         
36   American Express National Bank  2.10  Savings         
37   Aspiration                      2.00  Checking        
38   BBVA Compass                    2.00  Both            
39   BBVA Compass                    0.00  Checking        
40   Barclays                        2.20  Savings         
41   Capital One                     2.70  CDs             
42   Capital One                     2.80  CDs             
43   Capital One                     2.00  MMA             
44   Discover Bank                   2.65  Both            
45   Discover Bank                   2.10  Both            
46   First Internet Bank             2.02  Business        
47   Goldman Sachs Bank USA          2.70  Both            
48   Goldman Sachs Bank USA          3.00  Both            
49   Goldman Sachs Bank USA          2.25  Both            
50   HSBC Direct                     2.25  Savings         
51   Live Oak Bank                   1.10  Business        
52   UFB Direct                      2.45  Savings         
53   Vio Bank                        2.46  Savings         
54   nbkc bank                       0.00  Business        
55   nbkc bank                       1.01  Checking        
56   Goldman Sachs Bank USA          2.35  Both            
57   PurePoint Financial             2.80  CDs             
58   PurePoint Financial             2.50  CDs             
59   Goldman Sachs Bank USA          2.35  Both            
60   PurePoint Financial             2.80  CDs             
61   PurePoint Financial             2.50  CDs             
62   Goldman Sachs Bank USA          2.35  Both            
63   PurePoint Financial             2.50  CDs             
64   PurePoint Financial             2.80  CDs             
65   American Express National Bank  2.10  Savings         
6

In [765]:
# find the subset from second run that isn't shared, should be the majority
sec_run_output = temp_df_3[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','output_split', 'prorated_clicks']]\
.merge(new_final[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','split']], \
       'left', on=['AdvertiserName','Apy','budget_product','ProductName','ZoneName']) # don't change the join key; otherwise will have duplicates 

In [766]:
sec_run_output

Empty DataFrame
Columns: [output_split, prorated_clicks, AdvertiserName, Apy, budget_product, ProductName, ZoneName, split]
Index: []

In [767]:
# filter for just NAs for the ones that not in new final table, also excluding other columns
sec_run_output = sec_run_output[sec_run_output.split.isna()].loc[:,:'prorated_clicks']

In [768]:
sec_run_output.rename(columns={'output_split':'split'},inplace=True)

In [769]:
## finalizing the final table
new_final = new_final.append(sec_run_output, ignore_index=True)

In [770]:
# change the name to merge
Ad_ops_slab.rename(columns={'Product':'budget_product'},inplace=True)

In [771]:
new_final = new_final.merge(Ad_ops_slab[['AdvertiserName','budget_product','Running Budget','Pacing to Optimal']], 'left', on=['AdvertiserName','budget_product'])

In [772]:
new_final['pacing_rank']=new_final.groupby('ZoneName')['Pacing to Optimal'].rank(method='dense',ascending=True)
new_final['budget_rank']=new_final.groupby(by=['ZoneName'])['Running Budget'].rank(method='dense',ascending=False)

In [773]:
new_final = new_final.drop(labels=['Running Budget','Pacing to Optimal'],axis=1)

In [774]:
# get new index for ranking later
new_final = new_final.sort_values(by=['ZoneName','Apy','pacing_rank'], ascending=[True,False,True]).reset_index(drop=True)

In [775]:
new_final['rank'] = new_final.reset_index().groupby('ZoneName')['index'].rank(method='dense',ascending=True)

In [776]:
# Overwrite set to 0
new_final.overwrite.fillna(0.0,inplace=True)
# drop NA since those are older products
new_final.dropna(inplace=True)

In [777]:
## rework the rank for paid marketing
new_final_paid = new_final.loc[
                 (new_final.ZoneName.str.contains('LP'))
                 ]
new_final_Npaid = new_final.loc[
                 (~new_final.ZoneName.str.contains('LP'))
                 ]
new_final_paid.sort_values(by=['ZoneName','pacing_rank','Apy'], ascending=[True,True,False],inplace= True)
new_final_Npaid.sort_values(by=['ZoneName','Apy','pacing_rank'], ascending=[True,False,True],inplace= True)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [778]:
new_final = new_final_paid.append(new_final_Npaid)

In [779]:
Advertiser

Adjusted Clicks                      Advertiser          AdvertiserMoat  \
0   345.258576       American Express National Bank  American Express         
1   0.000000         American Express National Bank  American Express         
2   0.000000         North American Savings Bank     NASB                     
3   708.643380       Goldman Sachs Bank USA          GS Bank                  
4   276.809020       Capital One                     Capital One              
5   229.742270       HSBC Direct                     HSBC Direct              
6   187.959776       Ally Bank                       Ally                     
7   141.730910       Barclays                        Barclays                 
8   51.675113        nbkc bank                       NBKC Bank                
9   41.966828        Vio Bank                        Vio Bank                 
10  34.129818        Capital One                     Capital One              
11  26.974286        UFB Direct                      UFB Direct (Axos Bank)   
12  23.840599        First Internet Bank             First Internet Bank      
13  15.869527        Barclays                        Barclays                 
14  12.186561        Aspiration                      Aspiration               
15  10.261289        Live Oak Bank                   Live Oak Bank            
16  6.267374         nbkc bank                       NBKC Bank                
17  0.081926         BBVA Compass                    BBVA Compass             
18  0.000000         Synchrony Bank                  Synchrony                
19  0.000000         Ally Bank                       Ally                     
20  0.000000         Capital One                     Capital One              
21  0.000000         CIT Bank                        CIT Bank                 
22  0.000000         Vio Bank                        Vio Bank                 
23  0.000000         Axos Bank                       Axos Bank                
24  0.000000         Axos Bank                       Axos Bank                
25  0.000000         Citizens Access                 Citizens Access          
26  0.000000         PurePoint Financial             Purepoint                
27  0.000000         PurePoint Financial             Purepoint                
28  0.000000         First Internet Bank             First Internet Bank      
29  0.000000         earn.bank                       Earn.Bank                
30  0.000000         Discover Bank                   Discover                 
31  0.000000         Citi                            Citi                     
32 NaN               Penfed Credit Union             Penfed                   
33 NaN               Simple                          Simple                   

                    AdvertiserName        Budget    CPC  \
0   American Express National Bank  9200.000000   12.5    
1   American Express National Bank  0.000000      12.5    
2   North American Savings Bank     0.000000      12.5    
3   Goldman Sachs Bank USA          24000.000000  12.5    
4   Capital One                     6620.000000   11.0    
5   HSBC Direct                     6400.000000   12.5    
6   Ally Bank                       5729.000000   16.0    
7   Barclays                        7063.636364   11.0    
8   nbkc bank                       1200.000000   12.5    
9   Vio Bank                        1600.000000   12.5    
10  Capital One                     4545.454545   11.0    
11  UFB Direct                      600.000000    12.5    
12  First Internet Bank             400.000000    12.5    
13  Barclays                        3027.272727   11.0    
14  Aspiration                      208.333333    120.0   
15  Live Oak Bank                   240.000000    12.5    
16  nbkc bank                       120.000000    12.5    
17  BBVA Compass                    1.333333      75.0    
18  Synchrony Bank                  0.000000      0.0     
19  Ally Bank                       0.000000      16.0    

#### 3rd round fill in CPA Advertisers

In [780]:
# third run to add CPA advertisers
all_zones = pd.DataFrame(source_of_truth_n.ZoneName.unique())
all_zones = all_zones.rename(columns={0:'ZoneName'})

In [795]:
# Advertiser placement Counts
round2placementcount = new_final.groupby('ZoneName')[['AdvertiserName']].count().reset_index()
# if NA then it need to fill in CPA
round3zone = zone_sort_z4[['ZoneName','SpotAvailable']].merge(round2placementcount,'left',on='ZoneName').sort_values('ZoneName')
round3zone_NA = round3zone.loc[round3zone.AdvertiserName.isnull()].reset_index(drop=True)

In [787]:
# now only filter CPA advertiser to retrieve CPC/CPA value
round3cpa_ad = Advertiser.loc[Advertiser.cpc_cpa=='CPA']
round3cpa_ad = round3cpa_ad[['Advertiser','CPC']]
round3cpa_ad

In [802]:
## merge the round 3 NA zones with other data points from df
round3df = df_sec_rotation.merge(round3zone_NA,'inner',on='ZoneName')

In [835]:
## thrid run
running_dummy = 0
for idx, row in round3df.iterrows():
    print(idx)
    print(row.ZoneName)
    # get all the SOT for this row
    temp3_df_1 = sot_loop.loc[sot_loop.ZoneName == row['ZoneName']]
    #print(temp3_df_1)
    #Qualify advertiser one more time - have one more day of budget
    #temp_ad = Ad_ops_sec_rd[(Ad_ops_sec_rd.slab_running+Ad_ops_sec_rd.remain_budget*second_run_ctrl) > 0.0]
    
    #match the first 6 columns of final output, others can be joined later***
    temp3_df_1 = temp3_df_1[['AdvertiserName','Apy','budget_product','ProductName','ZoneName','ClickPerDay']]
    # slab_running rank
    temp3_df_2 = temp3_df_1.merge(round3cpa_ad\
                          ,'inner',left_on=['AdvertiserName']\
                          , right_on = ['Advertiser'])
    #print(temp3_df_2)
    # sort by CPA
    temp3_df_2.sort_values(by = ['CPC'], ascending=[False], inplace=True)
    
    # depending on the spots, fill in from high to low
    if running_dummy == 0:
        #find rows that is closest to and below remain inventory  
        temp3_df_3 = temp3_df_2.head(1)
    else:
        temp3_df_3 = temp3_df_3.append(temp3_df_2.head(1), ignore_index = True)
    print(temp3_df_3)
    running_dummy += temp3_df_2.shape[0]
    

0
LT - CRM Email
Empty DataFrame
Columns: [AdvertiserName, Apy, budget_product, ProductName, ZoneName, ClickPerDay, Advertiser, CPC]
Index: []
1
Account Comparison (2yr CD)
  AdvertiserName  Apy budget_product  ProductName  \
0  Discover Bank  2.7  Both           24 Month CD   

                      ZoneName  ClickPerDay     Advertiser   CPC  
0  Account Comparison (2yr CD)  3.0          Discover Bank  70.0  
2
Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)
  AdvertiserName  Apy budget_product  ProductName  \
0  Discover Bank  2.7  Both           24 Month CD   

                      ZoneName  ClickPerDay     Advertiser   CPC  
0  Account Comparison (2yr CD)  3.0          Discover Bank  70.0  
3
Main Rate Table (Bus. MMA)
  AdvertiserName  Apy budget_product  ProductName  \
0  Discover Bank  2.7  Both           24 Month CD   

                      ZoneName  ClickPerDay     Advertiser   CPC  
0  Account Comparison (2yr CD)  3.0          Discover Bank  70.0  
4
Main Rate T

   AdvertiserName   Apy budget_product            ProductName  \
0   Discover Bank  2.70  Both           24 Month CD             
1   Discover Bank  0.65  Both           6 Month CD              
2   Discover Bank  2.10  Both           Online Savings          
3   BBVA Compass   0.00  Checking       ClearConnect Checking   
4   Discover Bank  2.65  Both           12 Month CD             
5   Discover Bank  3.00  Both           5 Year CD               
6   Discover Bank  3.00  Both           5 Year CD               
7   Discover Bank  2.65  Both           18 Month CD             
8   Discover Bank  2.75  Both           3 Year CD               
9   Discover Bank  2.65  Both           18 Month CD             
10  Discover Bank  2.80  Both           4 Year CD               
11  Discover Bank  2.75  Both           3 Year CD               
12  Discover Bank  2.75  Both           3 Year CD               

                                                        ZoneName  ClickPerDay  \
0   Acco

In [836]:
# test and see which one got placed
temp3_df_3

AdvertiserName   Apy budget_product            ProductName  \
0   Discover Bank  2.70  Both           24 Month CD             
1   Discover Bank  0.65  Both           6 Month CD              
2   Discover Bank  2.10  Both           Online Savings          
3   BBVA Compass   0.00  Checking       ClearConnect Checking   
4   Discover Bank  2.65  Both           12 Month CD             
5   Discover Bank  3.00  Both           5 Year CD               
6   Discover Bank  3.00  Both           5 Year CD               
7   Discover Bank  2.65  Both           18 Month CD             
8   Discover Bank  2.75  Both           3 Year CD               
9   Discover Bank  2.65  Both           18 Month CD             
10  Discover Bank  2.80  Both           4 Year CD               
11  Discover Bank  2.75  Both           3 Year CD               
12  Discover Bank  2.75  Both           3 Year CD               
13  Discover Bank  2.80  Both           4 Year CD               
14  Discover Bank  2.80  Both           4 Year CD               

                                                        ZoneName  ClickPerDay  \
0   Account Comparison (2yr CD)                                   3.000000      
1   Main Rate Table (6mo CD)                                      2.000000      
2   Bonus Offers Page - Savings                                   1.000000      
3   LT - Rate Table (Chk)                                         1.000000      
4   Bank Pages Sponsored - Popular Accounts Comparison (1yr CD)   56.000000     
5   Bank Pages Sponsored - Popular Accounts Comparison (5yr CD)   43.285714     
6   Main Rate Table (5yr CD)                                      1.319432      
7   Main Rate Table (18mo CD)                                     1.440286      
8   Bank Pages Sponsored - Popular Accounts Comparison (3yr CD)   6.000000      
9   Bank Pages Sponsored - Popular Accounts Comparison (18mo CD)  9.000000      
10  Bank Pages Sponsored - Popular Accounts Comparison (4yr CD)   1.000000      
11  Main Rate Table (3yr CD)                                      1.000000      
12  Account Comparison (3yr CD)                                   2.000000      
13  Account Comparison (4yr CD)                                   1.000000      
14  Main Rate Table (4yr CD)                                      1.000000      

       Advertiser   CPC  
0   Discover Bank  70.0  
1   Discover Bank  70.0  
2   Discover Bank  70.0  
3   BBVA Compass   75.0  
4   Discover Bank  70.0  
5   Discover Bank  70.0  
6   Discover Bank  70.0  
7   Discover Bank  70.0  
8   Discover Bank  70.0  
9   Discover Bank  70.0  
10  Discover Bank  70.0  
11  Discover Bank  70.0  
12  Discover Bank  70.0  
13  Discover Bank  70.0  
14  Discover Bank  70.0

In [838]:
# find the same items that's share
new_final_n = pd.merge(temp3_df_3[['AdvertiserName','Apy','budget_product','ProductName','ZoneName']],\
         new_final,\
         'right',on=['AdvertiserName','Apy','budget_product','ProductName','ZoneName'])

In [840]:
new_final = new_final_n.copy()

In [841]:
#second run result
new_final

AdvertiserName   Apy budget_product  \
0    Capital One                     2.00  MMA             
1    American Express National Bank  2.10  Savings         
2    HSBC Direct                     2.25  Savings         
3    Barclays                        2.20  Savings         
4    Goldman Sachs Bank USA          2.25  Both            
5    Capital One                     2.00  MMA             
6    American Express National Bank  2.10  Savings         
7    HSBC Direct                     2.25  Savings         
8    Barclays                        2.20  Savings         
9    Goldman Sachs Bank USA          2.25  Both            
10   Goldman Sachs Bank USA          2.70  Both            
11   Capital One                     2.80  CDs             
12   Capital One                     2.00  MMA             
13   UFB Direct                      2.45  Savings         
14   American Express National Bank  2.10  Savings         
15   HSBC Direct                     2.25  Savings         
16   Barclays                        2.20  Savings         
17   Goldman Sachs Bank USA          2.25  Both            
18   Capital One                     2.00  MMA             
19   American Express National Bank  2.10  Savings         
20   Goldman Sachs Bank USA          2.25  Both            
21   American Express National Bank  2.10  Savings         
22   HSBC Direct                     2.25  Savings         
23   Goldman Sachs Bank USA          2.25  Both            
24   American Express National Bank  2.10  Savings         
25   Capital One                     2.00  MMA             
26   Goldman Sachs Bank USA          3.00  Both            
27   Capital One                     2.80  CDs             
28   Capital One                     2.70  CDs             
29   Goldman Sachs Bank USA          2.70  Both            
30   Discover Bank                   2.65  Both            
31   Vio Bank                        2.46  Savings         
32   UFB Direct                      2.45  Savings         
33   HSBC Direct                     2.25  Savings         
34   Goldman Sachs Bank USA          2.25  Both            
35   Ally Bank                       2.20  Savings         
36   Barclays                        2.20  Savings         
37   Discover Bank                   2.10  Both            
38   American Express National Bank  2.10  Savings         
39   First Internet Bank             2.02  Business        
40   Capital One                     2.00  MMA             
41   Aspiration                      2.00  Checking        
42   Live Oak Bank                   1.10  Business        
43   nbkc bank                       1.01  Checking        
44   nbkc bank                       0.00  Business        
45   BBVA Compass                    0.00  Checking        
46   Discover Bank                   3.00  Both            
47   Capital One                     2.70  CDs             
48   Vio Bank                        2.46  Savings         
49   UFB Direct                      2.45  Savings         
50   HSBC Direct                     2.25  Savings         
51   Goldman Sachs Bank USA          2.25  Both            
52   Ally Bank                       2.20  Savings         
53   Barclays                        2.20  Savings         
54   American Express National Bank  2.10  Savings         
55   Aspiration                      2.00  Checking        
56   Live Oak Bank                   1.10  Business        
57   nbkc bank                       1.01  Checking        
58   BBVA Compass                    0.00  Checking        
59   nbkc bank                       1.01  Checking        
60   American Express National Bank  2.10  Savings         
61   American Express National Bank  2.10  Savings         
62   Goldman Sachs Bank USA          2.25  Both            
63   Barclays                        2.20  Savings         
64   American Express National Bank  2.10  Savings         
65   American Express National Bank  2.10  Savings         
6

#### Final Reports

In [842]:
prior_day_placement.Rotation = prior_day_placement.Rotation/100

In [843]:
prior_day_placement.sort_values('ZoneName')

Id  ZoneId  \
0    2857  19       
1    2858  20       
2    2859  21       
3    2850  51       
4    1413  51       
27   2804  48       
26   2801  48       
24   2505  48       
23   2548  48       
22   729   48       
21   1357  48       
20   705   48       
19   672   48       
18   1193  48       
17   1977  48       
16   2109  48       
25   2792  48       
14   2108  48       
5    2774  48       
15   2728  48       
7    2570  48       
8    2571  48       
6    2569  48       
10   1127  48       
11   1344  48       
12   2547  48       
13   1459  48       
9    2788  48       
44   2775  49       
43   2568  49       
42   2838  49       
41   2787  49       
40   862   49       
39   1343  49       
38   1126  49       
37   2727  49       
34   1458  49       
35   1205  49       
33   923   49       
32   671   49       
31   2504  49       
30   2773  49       
29   2516  49       
28   2793  49       
36   1976  49       
45   2862  93       
46   2861  88       
47   1709  89       
48   2863  90       
49   2864  91       
50   2866  92       
51   1461  95       
52   2034  94       
53   1398  87       
54   2591  172      
55   2584  171      
56   2585  171      
57   1759  162      
58   1761  162      
59   2735  112      
60   2852  112      
61   2394  112      
63   2853  113      
64   2736  113      
62   2395  113      
65   2737  114      
66   2854  114      
67   2396  114      
68   2271  165      
69   2413  165      
70   2825  165      
71   2826  165      
72   2763  175      
73   2764  175      
74   2762  175      
78   2596  154      
77   1354  154      
79   1248  154      
75   2843  154      
76   1250  154      
80   1723  159      
81   1724  159      
82   2518  159      
83   2753  159      
84   2844  159      
85   2830  151      
86   2834  151      
87   2831  151      
88   2851  151      
98   2818  150      
97   2373  150      
96   1348  150      
95   1135  150      
94   993   150      
91   2820  150      
92   2821  150      
90   2819  150      
89   2845  150      
93   2823  150      
99   2536  170      
100  2846  170      
101  2441  167      
102  2847  133      
108  2478  130      
109  2814  130      
107  2226  130      
103  1666  130      
105  1703  130      
104  1668  130      
106  2111  130      
110  1959  164      
111  1438  157      
112  1424  157      
131  2607  158      
130  2606  158      
128  2790  158      
127  2495  158      
126  2730  158      
125  1683  158      
124  2551  158      
123  2372  158      
122  1684  158      
129  2605  158      
120  2112  158      
119  2367  158      
118  1697  158      
117  2772  158      
116  2494  158      
115  1694  158      
114  2506  158      
113  2806  158      
121  1537  158      
132  2265  156      
133  1650  156      
134  2731  156      
140  2848  148      
139  2824  148      
138  2574  148      
137  1347  148      
135  1020  148      
136  1133  148      
141  1415  117      
142  1416  117      
143  2099  117      
144  850   117      
145  2336  119      
146  1465  119      
147  2732  119      
155  2507  116      
158  2777  116      
157  2789  116      
159  2754  116      
154  849   116      
156  2805  116      
152  1131  116      
151  2318  116      
150  1159  116      
149  1345  116      
148  1090  116      
153  1360  116      
160  2795  44       
161  703   23       
162  1198  24       
163  2797  25       
164  2798  26       
165  2799  27       
166  2800  45       
167  2107  106      
168  861   108      
169  1358  108      
170  2770  108      
171  1460  29       
172  2729  29       
173  2511  105      
174  2501  32       
175  2512  33       
176  2514  101      
177  2515  102      
178  2837  34       
179  2517  103      
180  790   38       
181  670   28       
182  1349  28       
183  1975  28       
184  2811  28       
185  2849  28       
186  2417  168      
187  2416  168      
192  2415  47       
191  2264  47    

In [844]:
# Fixing SEM and Native CD plaements
prior_day_placement.loc[(prior_day_placement.Term == '18-month') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (18mo CD)']
prior_day_placement.loc[(prior_day_placement.Term == '1-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (1yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '2-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (2yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '3-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (3yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '4-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (4yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '5-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (5yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '6-year') & (prior_day_placement.ZoneName == 'LP - Native (CD)'), ['ZoneName']] =['LP - Native (6yr CD)']

prior_day_placement.loc[(prior_day_placement.Term == '18-month') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (18mo CD)']
prior_day_placement.loc[(prior_day_placement.Term == '1-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (1yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '2-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (2yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '3-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (3yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '4-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (4yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '5-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (5yr CD)']
prior_day_placement.loc[(prior_day_placement.Term == '6-year') & (prior_day_placement.ZoneName == 'LP - SEM (CD)'), ['ZoneName']] =['LP - SEM (6yr CD)']

In [845]:
prior_day_placement['rank_ytd']=prior_day_placement.groupby(['ZoneName'])['Priority'].rank(method='dense',ascending=True)

In [846]:
prior_day_placement.sort_values(['ZoneName','rank_ytd'])

Id  ZoneId  \
0    2857  19       
1    2858  20       
2    2859  21       
4    1413  51       
3    2850  51       
10   1127  48       
5    2774  48       
6    2569  48       
7    2570  48       
8    2571  48       
9    2788  48       
11   1344  48       
12   2547  48       
13   1459  48       
14   2108  48       
15   2728  48       
16   2109  48       
17   1977  48       
18   1193  48       
19   672   48       
20   705   48       
21   1357  48       
22   729   48       
23   2548  48       
24   2505  48       
25   2792  48       
26   2801  48       
27   2804  48       
29   2516  49       
35   1205  49       
32   671   49       
33   923   49       
38   1126  49       
40   862   49       
28   2793  49       
30   2773  49       
31   2504  49       
34   1458  49       
36   1976  49       
37   2727  49       
39   1343  49       
41   2787  49       
42   2838  49       
43   2568  49       
44   2775  49       
45   2862  93       
46   2861  88       
47   1709  89       
48   2863  90       
49   2864  91       
50   2866  92       
51   1461  95       
52   2034  94       
53   1398  87       
54   2591  172      
55   2584  171      
56   2585  171      
57   1759  162      
58   1761  162      
59   2735  112      
60   2852  112      
61   2394  112      
62   2395  113      
63   2853  113      
64   2736  113      
65   2737  114      
66   2854  114      
67   2396  114      
69   2413  165      
68   2271  165      
70   2825  165      
71   2826  165      
72   2763  175      
73   2764  175      
74   2762  175      
75   2843  154      
77   1354  154      
78   2596  154      
76   1250  154      
79   1248  154      
84   2844  159      
80   1723  159      
83   2753  159      
81   1724  159      
82   2518  159      
88   2851  151      
85   2830  151      
87   2831  151      
86   2834  151      
89   2845  150      
98   2818  150      
96   1348  150      
97   2373  150      
95   1135  150      
94   993   150      
91   2820  150      
90   2819  150      
93   2823  150      
92   2821  150      
99   2536  170      
100  2846  170      
101  2441  167      
102  2847  133      
109  2814  130      
107  2226  130      
105  1703  130      
103  1666  130      
104  1668  130      
108  2478  130      
106  2111  130      
110  1959  164      
112  1424  157      
111  1438  157      
114  2506  158      
131  2607  158      
129  2605  158      
130  2606  158      
113  2806  158      
115  1694  158      
116  2494  158      
117  2772  158      
118  1697  158      
119  2367  158      
120  2112  158      
121  1537  158      
122  1684  158      
123  2372  158      
124  2551  158      
125  1683  158      
126  2730  158      
127  2495  158      
128  2790  158      
132  2265  156      
133  1650  156      
134  2731  156      
140  2848  148      
139  2824  148      
137  1347  148      
138  2574  148      
136  1133  148      
135  1020  148      
144  850   117      
141  1415  117      
142  1416  117      
143  2099  117      
145  2336  119      
146  1465  119      
147  2732  119      
148  1090  116      
149  1345  116      
150  1159  116      
151  2318  116      
152  1131  116      
153  1360  116      
154  849   116      
155  2507  116      
156  2805  116      
157  2789  116      
158  2777  116      
159  2754  116      
160  2795  44       
161  703   23       
162  1198  24       
163  2797  25       
164  2798  26       
165  2799  27       
166  2800  45       
167  2107  106      
169  1358  108      
168  861   108      
170  2770  108      
172  2729  29       
171  1460  29       
173  2511  105      
174  2501  32       
175  2512  33       
176  2514  101      
177  2515  102      
178  2837  34       
179  2517  103      
180  790   38       
184  2811  28       
183  1975  28       
181  670   28       
182  1349  28       
185  2849  28       
186  2417  168      
187  2416  168      
188  668   47       
191  2264  47    

In [861]:
change_table = new_final.copy()

In [862]:
change_table = change_table.loc[(change_table.ZoneName != 'Bank Pages Sponsored - Most Popular Accounts')&
                 (change_table.ZoneName != 'Bank Pages Sponsored - Open An Account')&
                 (~change_table.ZoneName.str.contains('MagnifyMoney - BP'))&
                 (~change_table.ZoneName.str.contains('MagnifyMoney - LP'))&
                 (~change_table.ZoneName.str.contains('MagnifyMoney - Rate table'))&
                 (~change_table.ZoneName.str.contains('MagnifyMoney - Bank Friction Pages'))
                 #(~change_table.ZoneName.str.contains('CC'))&
                 #(~change_table.ZoneName.str.contains('HiatusApp'))&
                 #(~change_table.ZoneName.str.contains('CRM'))&
                 #(~change_table.ZoneName.str.contains('MyLT'))&
                 #(~change_table.ZoneName.str.contains('Bonus Offers Page - Savings'))&
                 #(~change_table.ZoneName.str.contains('Blog Best'))&
                 #(~change_table.ZoneName.str.contains('LP - Native MSN Page (CDs)'))&
                 #(~change_table.ZoneName.str.contains('LP - SEM B'))#&
                 #(~change_table.ZoneName.str.contains('Account Comparison'))
                 ]
                

In [863]:
prior_day_placement = prior_day_placement.loc[(prior_day_placement.ZoneName != 'Bank Pages Sponsored - Most Popular Accounts')&
                 (prior_day_placement.ZoneName != 'Bank Pages Sponsored - Open An Account')&
                 (~prior_day_placement.ZoneName.str.contains('MagnifyMoney - BP'))&
                 (~prior_day_placement.ZoneName.str.contains('MagnifyMoney - LP'))&
                 (~prior_day_placement.ZoneName.str.contains('MagnifyMoney - Rate table'))&
                 (~prior_day_placement.ZoneName.str.contains('MagnifyMoney - Bank Friction Pages'))
                 #(~prior_day_placement.ZoneName.str.contains('CC'))&
                 #(~prior_day_placement.ZoneName.str.contains('HiatusApp'))&
                 #(~prior_day_placement.ZoneName.str.contains('CRM'))&
                 #(~prior_day_placement.ZoneName.str.contains('MyLT'))&
                 #(~prior_day_placement.ZoneName.str.contains('Bonus Offers Page - Savings'))&
                 #(~prior_day_placement.ZoneName.str.contains('Blog Best'))&
                 #(~prior_day_placement.ZoneName.str.contains('LP - Native MSN Page (CDs)'))&
                 #(~prior_day_placement.ZoneName.str.contains('LP - SEM B'))#&
                 #(~prior_day_placement.ZoneName.str.contains('Account Comparison'))
                 ]

In [864]:
new_change_tbl = change_table.merge(prior_day_placement,'outer',left_on=['ZoneName','AdvertiserName','ProductName','rank','split'],\
                right_on=['ZoneName','AdvertiserName','ProductName','rank_ytd','Rotation'])

In [865]:
# Tonight check and see how it compares
# need to change budget rank to descending first to match rotation rank
# need to check datetime when i get back to SF
new_change_tbl = new_change_tbl[new_change_tbl.Rotation.isna()==True].sort_values(['ZoneName','Apy','pacing_rank']\
                                                                 , ascending=[True,False,True])

In [866]:
change_table

AdvertiserName   Apy budget_product  \
0    Capital One                     2.00  MMA             
1    American Express National Bank  2.10  Savings         
2    HSBC Direct                     2.25  Savings         
3    Barclays                        2.20  Savings         
4    Goldman Sachs Bank USA          2.25  Both            
5    Capital One                     2.00  MMA             
6    American Express National Bank  2.10  Savings         
7    HSBC Direct                     2.25  Savings         
8    Barclays                        2.20  Savings         
9    Goldman Sachs Bank USA          2.25  Both            
10   Goldman Sachs Bank USA          2.70  Both            
11   Capital One                     2.80  CDs             
12   Capital One                     2.00  MMA             
13   UFB Direct                      2.45  Savings         
14   American Express National Bank  2.10  Savings         
15   HSBC Direct                     2.25  Savings         
16   Barclays                        2.20  Savings         
17   Goldman Sachs Bank USA          2.25  Both            
18   Capital One                     2.00  MMA             
19   American Express National Bank  2.10  Savings         
20   Goldman Sachs Bank USA          2.25  Both            
24   American Express National Bank  2.10  Savings         
25   Capital One                     2.00  MMA             
59   nbkc bank                       1.01  Checking        
60   American Express National Bank  2.10  Savings         
61   American Express National Bank  2.10  Savings         
62   Goldman Sachs Bank USA          2.25  Both            
63   Barclays                        2.20  Savings         
64   American Express National Bank  2.10  Savings         
65   American Express National Bank  2.10  Savings         
66   PurePoint Financial             2.80  CDs             
67   PurePoint Financial             2.50  CDs             
68   Goldman Sachs Bank USA          2.35  Both            
69   PurePoint Financial             2.80  CDs             
70   PurePoint Financial             2.50  CDs             
71   Goldman Sachs Bank USA          2.35  Both            
72   PurePoint Financial             2.80  CDs             
73   PurePoint Financial             2.50  CDs             
74   Goldman Sachs Bank USA          2.35  Both            
75   American Express National Bank  2.10  Savings         
76   American Express National Bank  2.10  Savings         
77   Capital One                     2.00  MMA             
78   UFB Direct                      2.45  Savings         
79   HSBC Direct                     2.25  Savings         
80   Goldman Sachs Bank USA          2.25  Both            
81   Barclays                        2.20  Savings         
82   American Express National Bank  2.10  Savings         
83   First Internet Bank             2.02  Business        
84   Live Oak Bank                   1.10  Business        
85   American Express National Bank  2.10  Savings         
92   Capital One                     2.70  CDs             
93   HSBC Direct                     2.25  Savings         
94   American Express National Bank  2.10  Savings         
95   Aspiration                      2.00  Checking        
107  Capital One                     2.70  CDs             
108  Goldman Sachs Bank USA          2.70  Both            
109  Capital One                     2.80  CDs             
110  nbkc bank                       0.00  Business        
111  First Internet Bank             2.02  Business        
112  Live Oak Bank                   1.10  Business        
113  nbkc bank                       0.00  Business        
114  Aspiration                      2.00  Checking        
115  nbkc bank                       1.01  Checking        
116  Discover Bank                   2.65  Both            
117  Discover Bank                   2.65  Both            
118  Discover Bank                   2.70  Both            
1

In [867]:
## rework the rank for paid marketing
change_table_paid = change_table.loc[
                 (change_table.ZoneName.str.contains('LP'))
                 ]
change_table_Npaid = change_table.loc[
                 (~change_table.ZoneName.str.contains('LP'))
                 ]
change_table_paid.sort_values(by=['ZoneName','pacing_rank','Apy'], ascending=[True,True,False],inplace= True)
change_table_Npaid.sort_values(by=['ZoneName','Apy','pacing_rank'], ascending=[True,False,True],inplace= True)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


In [868]:
change_table = change_table_paid.append(change_table_Npaid)

In [869]:
change_table.reset_index(drop=True,inplace=True)

In [870]:
change_table['index']=change_table.reset_index()['index']

In [871]:
# rank within each zone 
change_table['rank']=change_table.groupby(['ZoneName'])['index'].rank(method='dense',ascending=True)

In [872]:
# remove the index
change_table.drop('index',axis=1,inplace=True)

In [873]:
## Side by side output
side_by_side = change_table.merge(prior_day_placement,'outer',left_on=['ZoneName','rank'],\
                right_on=['ZoneName','rank_ytd'])

In [874]:
side_by_side.rename(columns={'AdvertiserName_x':'AdvertiserName_today','ProductName_x':'ProductName_today',\
                            'AdvertiserName_y':'AdvertiserName_ytd','ProductName_y':'ProductName_ytd',\
                            'rank':'rank_today',\
                            'Rotation':'split_ytd','split':'split_today'},inplace=True)

In [875]:
side_by_side_2 = side_by_side[['ZoneName','AdvertiserName_ytd','ProductName_ytd','rank_ytd','split_ytd',\
              'AdvertiserName_today','ProductName_today','rank_today','split_today']]

In [876]:
side_by_side_2['change']=np.where(side_by_side_2.AdvertiserName_today==side_by_side_2.AdvertiserName_ytd,\
         np.where(side_by_side_2.ProductName_today==side_by_side_2.ProductName_ytd,\
         np.where(side_by_side_2.split_today == side_by_side_2.split_ytd,0,1),1),1)

C:\Users\ctam\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [877]:
zone_sort_z4

ZoneName  \
0   LT - Rate Table (5yr CD)                                       
1   Main Rate Table (18mo CD)                                      
2   Bank Pages Sponsored - Popular Accounts Comparison (3yr CD)    
3   Bank Pages Sponsored - Popular Accounts Comparison (18mo CD)   
4   Bank Pages Sponsored - Popular Accounts Comparison (4yr CD)    
5   Blog Best CD Accounts                                          
6   Main Rate Table (3yr CD)                                       
7   Account Comparison (3yr CD)                                    
8   LT - Rate Table (MMA)                                          
9   Account Comparison (4yr CD)                                    
10  KPGR - Sidebar - Featured Accounts                             
11  LT - Rate Table (2yr CD)                                       
12  Main Rate Table (4yr CD)                                       
13  CC - Sidebar - Featured Accounts                               
14  LT - Rate Table (1yr CD)                                       
15  Main Rate Table (5yr CD)                                       
16  LP - SEM (4yr CD)                                              
17  LP - SEM (3yr CD)                                              
18  Bank Pages Sponsored - Popular Accounts Comparison (5yr CD)    
19  MyLT - Recommended Alert                                       
20  LP - Native (5yr CD)                                           
21  LP - Native (2yr CD)                                           
22  LP - Native (1yr CD)                                           
23  Bank Pages Sponsored - Popular Accounts Comparison (MMA)       
24  LP - SEM (5yr CD)                                              
25  Bank Pages Sponsored - Popular Accounts Comparison (1yr CD)    
26  Account Comparison (Savings)                                   
27  Main Rate Table (6mo CD)                                       
28  Main Rate Table (IRA 5yr)                                      
29  Bank Pages Sponsored - Popular Accounts Comparison (Chk)       
30  Main Rate Table (Bus. MMA)                                     
31  Bank Pages - Horizontal                                        
32  Main Rate Table (Checking Regular)                             
33  Sidebar - Featured Rates (CD 1yr)                              
34  Main Rate Table (IRA 1yr)                                      
35  Main Rate Table (Bus. Savings)                                 
36  Main Rate Table (Bus. Checking)                                
37  Main Rate Table (IRA 4yr)                                      
38  Main Rate Table (IRA 2yr)                                      
39  Main Rate Table (IRA 18m)                                      
40  Main Rate Table (IRA 3yr)                                      
41  Main Rate Table (IRA 6mo)                                      
42  Bonus Offers Page - Savings                                    
43  LP - Native MSN Page (CDs)                                     
44  LT - Rate Table (Chk)                                          
45  LT - Sidebar - Featured Accounts                               
46  VP - Sidebar - Featured Checking Accounts                      
47  Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)    
48  Bank Pages Sponsored - Popular Accounts Comparison (Sav)       
49  Main Rate Table (2yr CD)                                       
50  Main Rate Table (1yr CD)                                       
51  HiatusApp - Recommended Accounts                               
52  MagnifyMoney - Featured Accounts Sidebar                       
53  Account Comparison (2yr CD)                                    
54  LT - CRM Email                                                 
55  Sidebar - Featured Rates (Savings)                             
56  VP - Sidebar - Featured Accounts                               
57  Sidebar - Featured Accounts                                    
58  LP - Native (Sav)                       

In [878]:
## Adding ZoneID
side_by_side_2 = side_by_side_2.merge(zone_sort_z4[['ZoneName','ZoneID']],'left',on=['ZoneName'])

In [879]:
#Make Display = 0
side_by_side_2.ZoneID.fillna(0,inplace=True)

In [880]:
side_by_side_2.ZoneID = side_by_side_2.ZoneID.astype(int)

In [881]:
## Adding HyperLink
side_by_side_2['SiteLink']="http://core.depositaccounts.com/ads/zone.aspx?id="+side_by_side_2.ZoneID.apply(str)

In [882]:
## Adding change column to improve User Experience
side_by_side_2['Change_']=side_by_side_2['change']
side_by_side_2['Change__']=side_by_side_2['change']

In [883]:
side_by_side_2=side_by_side_2[['ZoneName','Change_','AdvertiserName_ytd','ProductName_ytd','rank_ytd','split_ytd','Change__','AdvertiserName_today','ProductName_today','rank_today','split_today','change','ZoneID','SiteLink']]

In [884]:
# Update SiteLink Output for Display
side_by_side_2.SiteLink = np.where(side_by_side_2.ZoneName.str.contains('Display'),'https://www.google.com/dfp/1249809#delivery/ListOrders',side_by_side_2.SiteLink)

In [885]:
side_by_side_2['SiteLink2'] = np.where(side_by_side_2.ZoneID==151,'http://core.depositaccounts.com/ads/zone.aspx?id=149','')
side_by_side_2['SiteLink2'] = np.where(side_by_side_2.ZoneID==150,'http://core.depositaccounts.com/ads/zone.aspx?id=148',side_by_side_2.SiteLink2)

In [886]:
Ad_ops_sec_rd.slab_running.sum()
# Changing algo to include pacing increase the total slab running (remaining budget) from 1645 to 1807

125.22955089628088

In [887]:
Ad_ops_slab.slab_running.sum()

-137.65269230905977

In [888]:
new_final.groupby(['AdvertiserName']).sum()[['prorated_clicks']]

prorated_clicks
AdvertiserName                                 
Ally Bank                       242.070718     
American Express National Bank  341.541847     
Aspiration                      71.528977      
BBVA Compass                    5.941833       
Barclays                        146.393557     
Capital One                     227.733624     
Discover Bank                   52.555128      
First Internet Bank             27.782918      
Goldman Sachs Bank USA          714.398549     
HSBC Direct                     230.030561     
Live Oak Bank                   10.441764      
PurePoint Financial             122.655775     
UFB Direct                      27.618516      
Vio Bank                        63.055268      
nbkc bank                       36.358871

In [889]:
Ad_ops_sec_rd

AdvertiserName  Pacing to Optimal   Product  \
0  American Express National Bank  207.666667         Savings    
1  Goldman Sachs Bank USA          3667.000000        Both       
2  Capital One                    -312.333333         MMA        
3  HSBC Direct                     314.333333         Savings    
4  Barclays                        2167.000000        Savings    
5  nbkc bank                      -81.000000          Checking   
6  UFB Direct                     -59.000000          Savings    
7  First Internet Bank            -134.666667         Business   
8  Barclays                        1659.000000        CDs        
9  nbkc bank                      -26.000000          Business   

   Running Budget  pacing_indx  remain_budget  slab_budget  slab_running  \
0  345.258576      0.949152     259.257345     3.716728     3.716728       
1  708.643380      0.397917     259.406701    -5.755169    -5.755169       
2  276.809020      1.081651     269.822578     99.352333    99.352333      
3  229.742270      0.924048     174.807743    -0.288291    -0.288291       
4  141.730910      0.580095     67.961482     -4.662646    -4.662646       
5  51.675113       1.020564     36.517335      20.306957    20.306957      
6  26.974286       1.014937     21.885583     -0.644229    -0.644229       
7  23.840599       1.034421     7.171650      -3.942319    -3.942319       
8  15.869527       0.659084     15.869527      15.869527    15.869527      
9  6.267374        1.006555     4.396124       1.276660     1.276660       

   mth_budget_no_organic    mth_budget  mth_pacing_budget  
0  7777.720359            10357.757272  6214.654363        
1  10908.972264           21259.301409  12755.580845       
2  8094.677336            8304.270602   4982.562361        
3  5244.232299            6892.268097   4135.360858        
4  2038.844455            4251.927313   2551.156388        
5  1095.520052            1550.253402   930.152041         
6  656.567478             809.228589    485.537153         
7  215.149509             715.217979    429.130787         
8  476.085819             476.085819    285.651492         
9  131.883721             188.021221    112.812733

In [890]:
df.loc[df.AdvertiserName == 'Aspiration']

SiteName AdvertiserName                      ZoneType  \
27   DepositAccounts.com  Aspiration     Bank Page - Own                
70   DepositAccounts.com  Aspiration     Bank Page - Own                
247  DepositAccounts.com  Aspiration     Main Rate Table                
280  DepositAccounts.com  Aspiration     Side Bar - Featured Accounts   
358  MagnifyMoney.com     Aspiration     Bank Page - Own                
399  MagnifyMoney.com     Aspiration     Side Bar - Featured Accounts   
449  MagnifyMoney.com     Aspiration     Rate Tables                    

                                         ZoneName zonegroup zone_pre_det  \
27   Bank Pages Sponsored - Most Popular Accounts  zone_2    Y             
70   Bank Pages Sponsored - Open An Account        zone_2    Y             
247  Main Rate Table (Checking Regular)            zone_4    N             
280  Sidebar - Featured Accounts                   zone_4    N             
358  MagnifyMoney - BP - Most Popular Accounts     zone_1    Y             
399  MagnifyMoney - Featured Accounts Sidebar      zone_4    N             
449  MagnifyMoney - Rate table and Blogs (Chk)     zone_1    Y             

     ZoneID  SpotAvailable             ProductName ProductDetail   ...    \
27   48      20.0           Spend and Save Account  Checking       ...     
70   49      20.0           Spend and Save Account  Checking       ...     
247  29      5.0            Spend and Save Account  Checking       ...     
280  47      5.0            Spend and Save Account  Checking       ...     
358  158     20.0           Spend and Save Account  Checking       ...     
399  156     3.0            Spend and Save Account  Checking       ...     
449  119     20.0           Spend and Save Account  Checking       ...     

     ClickPerDay_yesterday_o  ClickPerDay_last_31_days_o  DayCount  \
27   3.0                      2.2                         49         
70   3.0                      5.1                         53         
247  8.0                      5.9                         42         
280  27.0                     25.1                        31         
358  1.0                      3.4                         51         
399  6.0                      14.0                        34         
449  19.0                     16.3                        56         

     TotalClicks  ClickPerDay_2Months  ClickPerDay  SiteZoneAdvertiserRank  \
27   110          2.244898             2.720224     1.0                      
70   244          4.603774             3.737519     1.0                      
247  223          5.309524             6.912709     1.0                      
280  778          25.096774            26.413731    1.0                      
358  252          4.941176             1.747706     1.0                      
399  467          13.735294            10.978676    1.0                      
449  1007         17.982143            19.018411    1.0                      

     UsedInLoop  UniqueProductShown  CDTerm  
27   0           1                   None    
70   0           1                   None    
247  0           1                   None    
280  0           1                   None    
358  0           1                   None    
399  0           1                   None    
449  0           1                   None    

[7 rows x 38 columns]

In [891]:
CPD_table = df.groupby(['AdvertiserName','ZoneName'],as_index=False).sum()[['AdvertiserName','ZoneName','ClickPerDay']]

In [892]:
df.loc[df.AdvertiserName.str.contains('Capital One')].groupby(by=['ZoneName','ProductName']).sum()['ClickPerDay_yesterday']

ZoneName                                                     ProductName   
Bank Pages - Horizontal                                        Money Market    11.666667 
Bank Pages Sponsored - Most Popular Accounts                   Money Market    15.000000 
                                                             12 Month   CD     45.000000 
                                                             24 Month   CD     14.000000 
Bank Pages Sponsored - Open An Account                       12 Month   CD     12.000000 
Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)  24 Month   CD     0.000000  
LP - Native (1yr CD)                                         12 Month   CD     0.000000  
LP - Native (2yr CD)                                         24 Month   CD     0.000000  
LP - Native (Sav)                                              Money Market    10.000000 
LP - Native MSN Page (Savings)                                 Money Market    2.000000  
LP - SEM (1yr CD)       

In [893]:
CPD_table.loc[CPD_table.AdvertiserName == 'Capital One']

AdvertiserName  \
128  Capital One     
129  Capital One     
130  Capital One     
131  Capital One     
132  Capital One     
133  Capital One     
134  Capital One     
135  Capital One     
136  Capital One     
137  Capital One     
138  Capital One     
139  Capital One     
140  Capital One     
141  Capital One     
142  Capital One     
143  Capital One     
144  Capital One     
145  Capital One     
146  Capital One     
147  Capital One     
148  Capital One     
149  Capital One     
150  Capital One     
151  Capital One     
152  Capital One     
153  Capital One     
154  Capital One     

                                                        ZoneName  ClickPerDay  
128  Bank Pages - Horizontal                                      11.395720    
129  Bank Pages Sponsored - Most Popular Accounts                 76.808571    
130  Bank Pages Sponsored - Open An Account                       13.522000    
131  Bank Pages Sponsored - Popular Accounts Comparison (2yr CD)  8.290694     
132  LP - Native (1yr CD)                                         3.678408     
133  LP - Native (2yr CD)                                         6.626042     
134  LP - Native (Sav)                                            15.943574    
135  LP - Native MSN Page (Savings)                               2.701808     
136  LP - SEM (1yr CD)                                            125.077000   
137  LP - SEM (2yr CD)                                            54.735259    
138  LP - SEM (Sav)                                               46.033286    
139  LP - SEM B (Sav)                                             1.000000     
140  LT - Rate Table (1yr CD)                                     1.108333     
141  LT - Rate Table (2yr CD)                                     1.000000     
142  LT - Rate Table (MMA)                                        1.301667     
143  MagnifyMoney - BP - Most Popular Accounts                    5.117528     
144  MagnifyMoney - Featured Accounts Sidebar                     72.238095    
145  MagnifyMoney - LP (CD)                                       27.345176    
146  MagnifyMoney - LP (Sav)                                      4.724167     
147  MagnifyMoney - Rate table and Blogs (CD)                     81.135786    
148  MagnifyMoney - Rate table and Blogs (Sav and MMA)            2.733739     
149  Main Rate Table (1yr CD)                                     13.248923    
150  Main Rate Table (2yr CD)                                     2.932097     
151  Main Rate Table (Money Market)                               8.743945     
152  Main Rate Table (Savings)                                    9.223166     
153  Sidebar - Featured Accounts                                  122.917718   
154  Sidebar - Featured Rates (CD 1yr)                            39.591477

In [894]:
Ad_ops_slab

AdvertiserName  Pacing to Optimal budget_product  \
0   American Express National Bank  207.666667         Savings         
1   American Express National Bank  0.000000           CDs             
2   North American Savings Bank     0.000000           Savings         
3   Goldman Sachs Bank USA          3667.000000        Both            
4   Capital One                    -312.333333         MMA             
5   HSBC Direct                     314.333333         Savings         
6   Barclays                        2167.000000        Savings         
7   nbkc bank                      -81.000000          Checking        
8   UFB Direct                     -59.000000          Savings         
9   First Internet Bank            -134.666667         Business        
10  Barclays                        1659.000000        CDs             
11  Live Oak Bank                  -15.000000          Business        
12  nbkc bank                      -26.000000          Business        
13  Synchrony Bank                  0.000000           Both            
14  Ally Bank                       2670.000000        CDs             
15  Capital One                     0.000000           Business        
16  CIT Bank                        0.000000           Savings         
17  Vio Bank                        0.000000           CDs             
18  Axos Bank                       0.000000           Checking        
19  Axos Bank                       0.000000           Business        
20  Citizens Access                 0.000000           Both            
21  PurePoint Financial             0.000000           Savings         
22  First Internet Bank             12.000000          MMA             
23  earn.bank                       0.000000           MMA             
24  Citi                            0.000000           Savings         
25  Ally Bank                       569.366667         Savings         
26  Vio Bank                        330.333333         Savings         
27  Capital One                     2323.333333        CDs             
28  Aspiration                     -66.388889          Checking        
29  BBVA Compass                   -0.488889           Checking        
30  PurePoint Financial             0.000000           CDs             
31  Discover Bank                   38.000000          Both            

    Running Budget  pacing_indx  remain_budget  slab_budget  slab_running  \
0   345.258576      0.949152     259.257345     3.716728     3.716728       
1   0.000000        1.000000     0.000000       0.000000     0.000000       
2   0.000000        1.000000     0.000000       0.000000     0.000000       
3   708.643380      0.397917     259.406701    -5.755169    -5.755169       
4   276.809020      1.081651     269.822578     99.352333    99.352333      
5   229.742270      0.924048     174.807743    -0.288291    -0.288291       
6   141.730910      0.580095     67.961482     -4.662646    -4.662646       
7   51.675113       1.020564     36.517335      20.306957    20.306957      
8   26.974286       1.014937     21.885583     -0.644229    -0.644229       
9   23.840599       1.034421     7.171650      -3.942319    -3.942319       
10  15.869527       0.659084     15.869527      15.869527    15.869527      
11  10.261289       1.003777     2.311719      -0.180475    -0.180475       
12  6.267374        1.006555     4.396124       1.276660     1.276660       
13  0.000000        1.000000     0.000000       0.000000     0.000000       
14  0.000000        0.511214     0.000000       0.000000     0.000000       
15  0.000000        1.000000     0.000000       0.000000     0.000000       
16  0.000000        1.000000     0.000000       0.000000     0.000000       
17  0.000000        1.000000     0.000000       0.000000     0.000000       
18  0.000000        1.000000     0.000000       0.000000     0.000000       
19  0.000000        1.000000     0.000000       0.000000     0.000000       
20  0.000000        1.0000

## Output

#### Running Budget

In [ ]:
budget_ad_prod = Advertiser[['AdvertiserName','Product','Budget']]

In [ ]:
rotation_output_1h = new_final.sort_values(by=['ZoneName','Apy','pacing_rank'], ascending=[True,False,True])
rotation_output_2h = final_output.sort_values(by=['ZoneName','Apy','pacing_rank'],ascending=[True,False,True])
side_by_side_1h = side_by_side_2.sort_values(['ZoneName','rank_today']).reset_index(drop=True)

In [ ]:
# find first row to add lines
side_by_side_1h['Dups'] = side_by_side_1h.duplicated(['ZoneName'])
side_by_side_1h.reset_index(inplace=True)
first_row_idx = side_by_side_1h.loc[side_by_side_1h.Dups == False][['index']]

In [ ]:
row_color_index = side_by_side_1h.loc[side_by_side_1h.Dups == False][['ZoneName','index']]

In [ ]:
row_color_index = row_color_index.reset_index(drop=True).reset_index()

In [ ]:
row_color_index.rename(columns={'level_0':'Color_idx'},inplace=True)

In [ ]:
side_by_side_1h = side_by_side_1h.merge(row_color_index[['ZoneName','Color_idx']],on='ZoneName')

In [ ]:
side_by_side_1h.drop(['index','Dups'], axis = 1, inplace=True)

In [ ]:
side_by_side_2h = side_by_side_1h.drop(side_by_side_1h.columns[1:7], axis = 1)

In [ ]:
writer = pd.ExcelWriter(r'P:\Sales\DA\Daily Output\New output {0}-{1}-{2}.xlsx'.format(now.month,now.day,now.year))#writer is a staging area for multiple sheets
side_by_side_2h.to_excel(writer,'Daily Change')
side_by_side_1h.to_excel(writer,'Daily Change with Prior Day')
rotation_output_1h.to_excel(writer,'Rotation_max')
rotation_output_2h.to_excel(writer,'Rotation_exact')

#budget_ad_prod.to_excel(writer,'Daily Budget')

#add formatting
workbook  = writer.book
worksheet_chg = writer.sheets['Daily Change with Prior Day']
worksheet_output = writer.sheets['Daily Change']

# Conditional Formatting
yellow_format = workbook.add_format({'bold': True,'bg_color': '#FFFFCC'}) # background color
green_format = workbook.add_format({'bg_color': '#CCFFCC'})
color_format = workbook.add_format({'bg_color': '#E0E0E0'})
percent_fmt = workbook.add_format({'num_format': '0%'})

border_r = workbook.add_format({'right': 1})
border_l = workbook.add_format({'left': 1})
border_t = workbook.add_format({'top': 1})

# #Set row border
# for idx, row in first_row_idx.iterrows():
#     worksheet_chg.set_row(idx+1,None,border_t)

# Set row color - With Yesterday
for idx, row in side_by_side_1h[['Color_idx']].iterrows():
    if row.values%2==0:
        worksheet_chg.set_row(idx+1,None,color_format)
        #worksheet_chg.set_format(idx+1,6,None, percent_fmt)
        worksheet_chg.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
        worksheet_chg.conditional_format(idx+1, 11,idx+1, 11, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
    else: 
        worksheet_chg.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
        worksheet_chg.conditional_format(idx+1, 11,idx+1, 11, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
        
for idx, row in side_by_side_2h[['Color_idx']].iterrows():
    if row.values%2==0:
        worksheet_output.set_row(idx+1,None,color_format)
        #worksheet_chg.set_format(idx+1,6,None, percent_fmt)
        worksheet_output.conditional_format(idx+1, 5,idx+1, 5, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
        worksheet_output.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    0,
                                        'format':  yellow_format})
        worksheet_output.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '=',
                                        'value':    0,
                                        'format':  color_format})
    
    else: 
        worksheet_output.conditional_format(idx+1, 5,idx+1, 5, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    -1,
                                        'format':  percent_fmt})
        worksheet_output.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '>',
                                        'value':    0,
                                        'format':  yellow_format})
        worksheet_output.conditional_format(idx+1, 6,idx+1, 6, {'type':   'cell',
                                        'criteria': '=',
                                        'value':    0,
                                        'format':  color_format})

        
# worksheet_chg.set_column('G:G', None, percent_fmt)
# worksheet_chg.set_column('L:L', None, percent_fmt)

# set column border
# worksheet_chg.set_column('B:B',None,border_r)
# worksheet_chg.set_column('C:C',None,border_r)
# worksheet_chg.set_column('G:G',None,border_r)
# worksheet_chg.set_column('H:H',None,border_r)
# worksheet_chg.set_column('L:L',None,border_r)
# worksheet_chg.set_column('M:M',None,border_r)
# worksheet_chg.set_column('Q:Q',None,border_l)


# worksheet_chg.conditional_format('C1:C1000', {'type':   'cell',
#                                         'criteria': '>',
#                                         'value':    0,
#                                         'format':  yellow_format})

# worksheet_chg.conditional_format('H1:H1000', {'type':   'cell',
#                                         'criteria': '>',
#                                         'value':    0,
#                                         'format':  yellow_format})

# worksheet_chg.conditional_format('M1:M1000', {'type':   'cell',
#                                         'criteria': '>',
#                                         'value':    0,
#                                         'format':  yellow_format})
writer.save()

In [ ]:
print('Timestamp: {:%Y-%m-%d %H:%M:%S}'.format(datetime.datetime.now()))

In [ ]:
zone_sort_z4.sort_values('open_rate',ascending=False)

In [ ]:
# how much non MM and non-bank page are left on the table
inventory_2.groupby(by=['product_type'],as_index=False).sum()[['product_type','potential_clicks']]

## Add paid vs non-paid placement flag

In [ ]:
source_of_truth_daily="""
	select Priority, Rotation, Paused, p.Archived, pst.Name as Status, z.Name as ZoneName, z.ZoneType, z.Id ZoneID
	, a.Name as AdvertiserName, bp.Name as ProductName
	,bpt.Apy
	from
	Ads..placements p with(nolock)
	inner join Ads..PlacementStatusType pst with(nolock) on p.placementstatustypeid = pst.id 
	and pst.name in ('running','ready')
	inner join ads..Zones z with(nolock)
	on p.ZoneId = z.Id
	inner join ads..Sites s  with(nolock) on s.id=z.SiteId --the site
	inner join ads..TagGroups tg  with(nolock) on tg.Id=p.TagGroupId --the parent grouping for the tag (links change often, so we group them)
	inner join ads..Advertisers a  with(nolock) on a.Id=tg.AdvertiserId --the advertiser
	inner join findata.dbo.bankproducts bp with(nolock) on bp.id=p.productid
	and bp.Active=1 -- and bp.Active=1 currently only is citi bank
	inner join findata.dbo.bankproducttiers bpt on bpt.BankProductId=bp.id and 25000 between bpt.MinAmount and bpt.MaxAmount
	inner join FinData..Sections sc  with(nolock) on sc.Id = bp.SectionId--get product details
	left join FinData..Products pd  with(nolock) on pd.Id=bp.ProductId
	where a.Name not like ('%Portal%')
	and a.Archived=0 
	"""

In [ ]:
source_of_truth_daily=pd.read_sql(source_of_truth_daily,conn)

In [ ]:
now = datetime.datetime.today()
path_pl=r'P:\Sales\DA\Source of Truth'
new_writer = pd.ExcelWriter(r'P:\Sales\DA\Source of Truth\SOT {0}-{1}-{2}.xlsx'.format(now.month,now.day,now.year))#writer is a staging area for multiple sheets
source_of_truth_daily.to_excel(new_writer,'Output')
zone_sort_z4.to_excel(new_writer,'Zone')
new_writer.save()

In [ ]:
# 'Bank'
# 'Budget Product': Ad_ops['running budget']
# 'ZoneName':output_pm.ZoneName
# 'ZoneType':output_pm['ZoneType']
# 'ProductLookUp':output_pm.ProductDetails **************************
# 'ProductUsed':output_pm.ProductName
# 'SpotAvailable':no needed
# 'ExpectedCPD':output_pm.final_clicks
# 'BankBudget':Ad_ops['Running Budget_pre_d']
# 'CumulatedClicks':running budget - running budget pre_d ********************
# 'ClickPerDayNeeded': Advertiser_running['Clicks needed per day'] *******************
# 'ModifiedClickPerDayNeeded': Ad_ops['Running Budget'] ****************
# 'Slot Ratio':output_pm.rd_value
# 'Site_link':"http://core.depositaccounts.com/ads/zone.aspx?id="+str(zone_sort_z4['ZoneID']) *************

In [ ]:
# {'Bank':bankE
#                           ,'Budget Product':Advertiser.Product[advertiser_index]
#                           ,'Budget Placement':Advertiser.Placement[advertiser_index]
#                           ,'SiteName':availablePlacementv3['SiteName'][placement_index]
#                           ,'ZoneName':availablePlacementv3['ZoneName'][placement_index]
#                           ,'ZoneType':availablePlacementv3['ZoneType'][placement_index]
#                           ,'ProductLookUp':availablePlacementv3['ProductLookUp'][placement_index]
#                           ,'ProductUsed':ProductPlaced
#                           ,'SpotAvailable':availablePlacementv3['SpotAvailable'][placement_index]
#                           ,'ExpectedCPD':ClickPerDay
#                           ,'BankBudget':Advertiser['Running Budget'][advertiser_index]
#                           ,'CumulatedClicks':Advertiser['Adjusted Clicks'][advertiser_index]-Advertiser['Running Budget'][advertiser_index]
#                           ,'ClickPerDayNeeded':Advertiser['Clicks needed per day'][advertiser_index]
#                           ,'ModifiedClickPerDayNeeded':Advertiser['Adjusted Clicks'][advertiser_index]
#                           ,'DfIndex':TempIndex
#                           ,'xproduct':xproduct
#                           ,'Slot Ratio':pl_ratio
#                           ,'Site_link':"http://core.depositaccounts.com/ads/zone.aspx?id="+str(availablePlacementv3['ZoneID'][placement_index])
#                           #,'Site_link':"'<a href='http://core.depositaccounts.com/ads/zone.aspx?id="+str(availablePlacementv3['ZoneID'][placement_index])+"'>Link</a>"
#                           #,'temp':float(dfUniq.loc[(dfUniq['ZoneName']=='Bank Pages Sponsored - Most Popular Accounts')
#                           #                   &(dfUniq['AdvertiserName']==Bank)]['UniqueZoneShown'])
#                           }

In [ ]:
output_table.loc[(output_table.budget_product == 'Business')]

In [587]:
sot_grid.loc[(sot_grid.ProductDetail == 'Business')].sort_values('AdvertiserName')

AdvertiserName   Apy  Archived  ClickPerDay  \
250  Axos Bank            1.06  0         1.000000      
25   First Internet Bank  1.81  0         1.560000      
287  First Internet Bank  1.81  0         10.736842     
286  First Internet Bank  1.81  0         2.181818      
252  First Internet Bank  1.81  0         1.000000      
118  First Internet Bank  1.81  0         6.890000      
97   First Internet Bank  1.81  0         1.440000      
74   First Internet Bank  1.81  0         8.000000      
288  Live Oak Bank        1.10  0         1.525000      
77   Live Oak Bank        1.10  0         1.820000      
255  Live Oak Bank        1.10  0         1.000000      
30   Live Oak Bank        1.10  0         1.560000      
102  Live Oak Bank        1.10  0         1.840000      
104  SECU                 2.00  0         1.426667      
123  SECU                 2.00  0         6.890000      
289  SECU                 2.00  0         6.130921      
110  nbkc bank            0.00  0         1.000000      
285  nbkc bank            0.00  0         1.025000      

     ClickPerDay_last_7_days  ClickPerDay_yesterday ProductDetail  \
250 NaN                      NaN                     Business       
25  NaN                      NaN                     Business       
287  12.0                     0.0                    Business       
286  2.0                      0.0                    Business       
252 NaN                      NaN                     Business       
118  8.0                      7.0                    Business       
97   1.8                      1.0                    Business       
74   8.0                      0.0                    Business       
288  1.0                      0.0                    Business       
77   2.8                      1.0                    Business       
255  0.0                      0.0                    Business       
30   1.0                      0.0                    Business       
102  1.4                      0.0                    Business       
104  0.0                      0.0                    Business       
123  0.0                      0.0                    Business       
289 NaN                      NaN                     Business       
110  1.0                      0.0                    Business       
285  1.0                      0.0                    Business       

                                    ProductName  Rotation  \
250  Business Premium Savings                    100        
25   Business Money Market Savings               100        
287  Business Money Market Savings               100        
286  Business Money Market Savings               100        
252  Business Money Market Savings               100        
118  Business Money Market Savings               100        
97   Business Money Market Savings               100        
74   Business Money Market Savings               100        
288  Business Savings                            100        
77   Business Savings                            100        
255  Business Savings                            100        
30   Business Savings                            100        
102  Business Savings                            100        
104  Business Savings - Money Market Intro Rate  100        
123  Business Savings - Money Market Intro Rate  100        
289  Business Savings - Money Market Intro Rate  100        
110  Business Account                            100        
285  Business Account                            100        

                 ShortName  SpotAvailable   Term  ZoneID  \
250  None                   10             Other  130      
25   Business Money Market  20             Other  158      
287  Business Money Market  4              Other  108      
286  Business Money Market  4              Other  107      
252  Business Money Market  10             Other  130      
118  Business Money Market  20             Other  49       
97   Business Money Market  20    

In [588]:
# Advertiser.to_html(r'C:\Users\ctam\Documents\Work Files\Deposit Account\Placement Optimization\Outputs\Advertiser_txt.html')
# Advertiser.to_csv(r'C:\Users\ctam\Documents\Work Files\Deposit Account\Placement Optimization\Outputs\Advertiser_txt.txt', sep='\t', index=False)

In [589]:
#start with the one who need to most budget first
#Advertiser=Advertiser.sort_values(by='Running Budget',ascending=False).reset_index(drop=True)
#Advertiser.to_html('C:\Users\ctam\Documents\Work Files\Deposit Account\Placement Optimization\Outputs\Advertiser_txt.html',index=False, col_space=100)